In [2]:
import numpy as np
import os
import pandas as pd
from arcpy import env
from arcpy import TableToTable_conversion
import matplotlib.ticker as mtick

In [3]:
dirWork = os.getcwd()
dirData = os.path.join(dirWork, r'data')
dirTDM  = os.path.join(dirData, r'tdm\1_WF')
dirFactors   = os.path.join(dirWork, r'data-processed\factors')
dirResults   = os.path.join(dirWork, r'results')

# Run Settings

In [4]:
#set to true for first time to create CSVs, false to speed up for subsequent times
process_TDMdbftocsv = False

#export results
export_results = True

# Define Scenarios

In [5]:
df_Scenarios = pd.DataFrame()


#define AdjCode for pivot when model is not related to forecast
#AADT will be adjusted based on difference between scenario and forecast scenario TDMs
#if ForecastScenarioID is note defined, then the associated forecast volume will be used for that year
#DBF don't include filename extension

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'Base15',
                                    'ScenarioName'   : '2015 Base',
                                    'ScenarioYear'   :  2015,
                                    'ScenarioGroup'  : 'Base',
                                    'SegSummaryCSV'  : 'v831_SE15_Net15_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'Base19',
                                    'ScenarioName'   : '2019 Base',
                                    'ScenarioYear'   :  2019,
                                    'ScenarioGroup'  : 'Base',
                                    'SegSummaryCSV'  : 'v831_SE19_Net19_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'Base15'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'TIP24',
                                    'ScenarioName'   : '2024 TIP',
                                    'ScenarioYear'   :  2024,
                                    'ScenarioGroup'  : 'TIP',
                                    'SegSummaryCSV'  : 'v831_SE24_Net24_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'Base19'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'RTP30',
                                    'ScenarioName'   : '2030 RTP',
                                    'ScenarioYear'   :  2030,
                                    'ScenarioGroup'  : 'RTP',
                                    'SegSummaryCSV'  : 'v831_SE30_Net30_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'TIP24'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'RTP40',
                                    'ScenarioName'   : '2040 RTP',
                                    'ScenarioYear'   :  2040,
                                    'ScenarioGroup'  : 'RTP',
                                    'SegSummaryCSV'  : 'v831_SE40_Net40_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'RTP30'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode' : 'RTP50',
                                    'ScenarioName' : '2050 RTP',
                                    'ScenarioYear' :  2050,
                                    'ScenarioGroup': 'RTP',
                                    'SegSummaryCSV': 'v831_SE50_Net50_Summary_SEGID_Detailed.csv',
                                    'Process'      : 'Yes',
                                    'PrvScenarioCode': 'RTP40'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'NB30',
                                    'ScenarioName'   : '2030 No Build',
                                    'ScenarioYear'   :  2030,
                                    'ScenarioGroup'  : 'No Build',
                                    'AdjScenarioCode': 'RTP30',
                                    'SegSummaryCSV'  : 'v831_SE30_Net24_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'TIP24'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'NB40',
                                    'ScenarioName'   : '2040 No Build',
                                    'ScenarioYear'   :  2040,
                                    'ScenarioGroup'  : 'No Build',
                                    'AdjScenarioCode': 'RTP40',
                                    'SegSummaryCSV'  : 'v831_SE40_Net24_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'NB30'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'NB50',
                                    'ScenarioName'   : '2050 No Build',
                                    'ScenarioYear'   :  2050,
                                    'ScenarioGroup'  : 'No Build',
                                    'AdjScenarioCode': 'RTP50',
                                    'SegSummaryCSV'  : 'v831_SE50_Net24_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'NB40'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'UF30',
                                    'ScenarioName'   : '2030 Needs',
                                    'ScenarioYear'   :  2030,
                                    'ScenarioGroup'  : 'Needs',
                                    'AdjScenarioCode': 'RTP30',
                                    'SegSummaryCSV'  : 'v831_SE30_Net30UF_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'TIP24'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'UF40',
                                    'ScenarioName'   : '2040 Needs',
                                    'ScenarioYear'   :  2040,
                                    'ScenarioGroup'  : 'Needs',
                                    'AdjScenarioCode': 'RTP40',
                                    'SegSummaryCSV'  : 'v831_SE40_Net40UF_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'UF30'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'UF50',
                                    'ScenarioName'   : '2050 Needs',
                                    'ScenarioYear'   :  2050,
                                    'ScenarioGroup'  : 'Needs',
                                    'AdjScenarioCode': 'RTP50',
                                    'SegSummaryCSV'  : 'v831_SE50_Net50UF_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'UF40'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'S550',
                                    'ScenarioName'   : '2050 S5 Draft',
                                    'ScenarioYear'   :  2050,
                                    'ScenarioGroup'  : 'Scenario',
                                    'AdjScenarioCode': 'RTP50',
                                    'SegSummaryCSV'  : 'v831_SE50_Net50_Summary_SEGID_Detailed_S5DraftRecommendations.csv',
                                    'Process'        : 'Yes'
                                   },ignore_index=True)

#all scenarios will be read in to allow for pivoting if needed
df_Scenarios.index.name = 'ScenarioID'
df_Scenarios['ScenarioYear'] = pd.to_numeric(df_Scenarios['ScenarioYear'], downcast='integer')
df_Scenarios

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
0              Yes       Base15          Base      2015 Base          2015   
1              Yes       Base19          Base      2019 Base          2019   
2              Yes        TIP24           TIP       2024 TIP          2024   
3              Yes        RTP30           RTP       2030 RTP          2030   
4              Yes        RTP40           RTP       2040 RTP          2040   
5              Yes        RTP50           RTP       2050 RTP          2050   
6              Yes         NB30      No Build  2030 No Build          2030   
7              Yes         NB40      No Build  2040 No Build          2040   
8              Yes         NB50      No Build  2050 No Build          2050   
9              Yes         UF30         Needs     2030 Needs          2030   
10             Yes         UF40         Needs     2040 Needs          2040   
11             Yes         UF50         Needs     2050 Needs          2050   
12             Yes         S550      Scenario  2050 S5 Draft          2050   

                                                SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                      
0                  v831_SE15_Net15_Summary_SEGID_Detailed.csv             NaN   
1                  v831_SE19_Net19_Summary_SEGID_Detailed.csv          Base15   
2                  v831_SE24_Net24_Summary_SEGID_Detailed.csv          Base19   
3                  v831_SE30_Net30_Summary_SEGID_Detailed.csv           TIP24   
4                  v831_SE40_Net40_Summary_SEGID_Detailed.csv           RTP30   
5                  v831_SE50_Net50_Summary_SEGID_Detailed.csv           RTP40   
6                  v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
7                  v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
8                  v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
9                v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
10               v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
11               v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   
12          v831_SE50_Net50_Summary_SEGID_Detailed_S5Draft...             NaN   

           AdjScenarioCode  
ScenarioID                  
0                      NaN  
1                      NaN  
2                      NaN  
3                      NaN  
4                      NaN  
5                      NaN  
6                    RTP30  
7                    RTP40  
8                    RTP50  
9                    RTP30  
10                   RTP40  
11                   RTP50  
12                   RTP50

In [6]:
df_Scenarios_toProcess = df_Scenarios[df_Scenarios['Process']=='Yes']
df_Scenarios_toProcess

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
0              Yes       Base15          Base      2015 Base          2015   
1              Yes       Base19          Base      2019 Base          2019   
2              Yes        TIP24           TIP       2024 TIP          2024   
3              Yes        RTP30           RTP       2030 RTP          2030   
4              Yes        RTP40           RTP       2040 RTP          2040   
5              Yes        RTP50           RTP       2050 RTP          2050   
6              Yes         NB30      No Build  2030 No Build          2030   
7              Yes         NB40      No Build  2040 No Build          2040   
8              Yes         NB50      No Build  2050 No Build          2050   
9              Yes         UF30         Needs     2030 Needs          2030   
10             Yes         UF40         Needs     2040 Needs          2040   
11             Yes         UF50         Needs     2050 Needs          2050   
12             Yes         S550      Scenario  2050 S5 Draft          2050   

                                                SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                      
0                  v831_SE15_Net15_Summary_SEGID_Detailed.csv             NaN   
1                  v831_SE19_Net19_Summary_SEGID_Detailed.csv          Base15   
2                  v831_SE24_Net24_Summary_SEGID_Detailed.csv          Base19   
3                  v831_SE30_Net30_Summary_SEGID_Detailed.csv           TIP24   
4                  v831_SE40_Net40_Summary_SEGID_Detailed.csv           RTP30   
5                  v831_SE50_Net50_Summary_SEGID_Detailed.csv           RTP40   
6                  v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
7                  v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
8                  v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
9                v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
10               v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
11               v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   
12          v831_SE50_Net50_Summary_SEGID_Detailed_S5Draft...             NaN   

           AdjScenarioCode  
ScenarioID                  
0                      NaN  
1                      NaN  
2                      NaN  
3                      NaN  
4                      NaN  
5                      NaN  
6                    RTP30  
7                    RTP40  
8                    RTP50  
9                    RTP30  
10                   RTP40  
11                   RTP50  
12                   RTP50

In [7]:
df_Scenarios_toAdjust = df_Scenarios_toProcess[df_Scenarios_toProcess['AdjScenarioCode'].notnull()]
df_Scenarios_toAdjust

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
6              Yes         NB30      No Build  2030 No Build          2030   
7              Yes         NB40      No Build  2040 No Build          2040   
8              Yes         NB50      No Build  2050 No Build          2050   
9              Yes         UF30         Needs     2030 Needs          2030   
10             Yes         UF40         Needs     2040 Needs          2040   
11             Yes         UF50         Needs     2050 Needs          2050   
12             Yes         S550      Scenario  2050 S5 Draft          2050   

                                                SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                      
6                  v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
7                  v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
8                  v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
9                v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
10               v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
11               v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   
12          v831_SE50_Net50_Summary_SEGID_Detailed_S5Draft...             NaN   

           AdjScenarioCode  
ScenarioID                  
6                    RTP30  
7                    RTP40  
8                    RTP50  
9                    RTP30  
10                   RTP40  
11                   RTP50  
12                   RTP50

In [8]:
#define functions to get scenario data
def idFromCode (sCode):
    return df_Scenarios.index[df_Scenarios['ScenarioCode'] == sCode].tolist()[0]
def yrFromCode (sCode):
    return df_Scenarios[df_Scenarios['ScenarioCode'] == sCode].iloc[0]['ScenarioYear']
def codeFromID (sID):
    return df_Scenarios.loc[sID]['ScenarioCode']
def yearFromID (sID):
    return df_Scenarios.loc[sID]['ScenarioYear']

#quick tests of functions
#display(idFromCode('50RTP'))
#display(yrFromCode('50RTP'))
#display(codeFromID(4))
#display(yearFromID(4))
#display(df_Scenarios.loc[7]['ScenarioCode'])

# Define Desired V/C Groupings

In [9]:
#season groups

df_VCGroup_Seasons = pd.DataFrame()

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Ann',
                                                'SeasonName'    : 'Annual',
                                                'SeasonGroup'   : 'S00-Ann',
                                                'SeasonType'    : 'Season'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Win',
                                                'SeasonName'    : 'Winter',
                                                'SeasonGroup'   : 'S01-Win',
                                                'SeasonType'    : 'Season'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Spr',
                                                'SeasonName'    : 'Spring',
                                                'SeasonGroup'   : 'S02-Spr',
                                                'SeasonType'    : 'Season'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Sum',
                                                'SeasonName'    : 'Summer',
                                                'SeasonGroup'   : 'S03-Sum',
                                                'SeasonType'    : 'Season'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Fal',
                                                'SeasonName'    : 'Fall',
                                                'SeasonGroup'   : 'S04-Fal',
                                                'SeasonType'    : 'Season'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Jan',
                                                'SeasonName'    : 'January',
                                                'SeasonGroup'   : 'M01-Jan',
                                                'SeasonType'    : 'Month',
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Feb',
                                                'SeasonName'    : 'February',
                                                'SeasonGroup'   : 'M02-Feb',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Mar',
                                                'SeasonName'    : 'March',
                                                'SeasonGroup'   : 'M03-Mar',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Apr',
                                                'SeasonName'    : 'April',
                                                'SeasonGroup'   : 'M04-Apr',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'May',
                                                'SeasonName'    : 'May',
                                                'SeasonGroup'   : 'M05-May',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Jun',
                                                'SeasonName'    : 'June',
                                                'SeasonGroup'   : 'M06-Jun',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Jul',
                                                'SeasonName'    : 'July',
                                                'SeasonGroup'   : 'M07-Jul',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Aug',
                                                'SeasonName'    : 'August',
                                                'SeasonGroup'   : 'M08-Aug',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Sep',
                                                'SeasonName'    : 'September',
                                                'SeasonGroup'   : 'M09-Sep',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Oct',
                                                'SeasonName'    : 'October',
                                                'SeasonGroup'   : 'M10-Oct',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Nov',
                                                'SeasonName'    : 'November',
                                                'SeasonGroup'   : 'M11-Nov',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Dec',
                                                'SeasonName'    : 'December',
                                                'SeasonGroup'   : 'M12-Dec',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

display(df_VCGroup_Seasons)

#day-of-week groups

df_VCGroup_DOWPkHr = pd.DataFrame()

df_VCGroup_DOWPkHr = df_VCGroup_DOWPkHr.append({'DOWPkCode' : 'WkAM',
                                                'DOWPkName' : 'AM - Weekday',
                                                'DOWGroup'  : 'W1-Weekday',
                                                'Prd'       : 'AM',
                                                'HrPctOf'   : 'Prd' #calculate peak Hr using Prd volume
                                               },ignore_index=True)

df_VCGroup_DOWPkHr = df_VCGroup_DOWPkHr.append({'DOWPkCode' : 'WkMD',
                                                'DOWPkName' : 'Midday - Weekday',
                                                'DOWGroup'  : 'W1-Weekday',
                                                'Prd'       : 'MD',
                                                'HrPctOf'   : 'Prd' #calculate peak Hr using Prd volume
                                               },ignore_index=True)

df_VCGroup_DOWPkHr = df_VCGroup_DOWPkHr.append({'DOWPkCode' : 'WkPM',
                                                'DOWPkName' : 'PM - Weekday',
                                                'DOWGroup'  : 'W1-Weekday',
                                                'Prd'       : 'PM',
                                                'HrPctOf'   : 'Prd' #calculate peak Hr using Prd volume
                                               },ignore_index=True)

df_VCGroup_DOWPkHr = df_VCGroup_DOWPkHr.append({'DOWPkCode' : 'FrPM',
                                                'DOWPkName' : 'PM - Friday',
                                                'DOWGroup'  : '5-Friday',
                                                'Prd'       : 'PM',
                                                'HrPctOf'   : 'DY' #calculate peak Hr using DY volume
                                               },ignore_index=True)

df_VCGroup_DOWPkHr = df_VCGroup_DOWPkHr.append({'DOWPkCode' : 'SaDY',
                                                'DOWPkName' : 'Saturday',
                                                'DOWGroup'  : '6-Saturday',
                                                'Prd'       : 'DY',
                                                'HrPctOf'   : 'DY' #calculate peak Hr using DY volume
                                               },ignore_index=True)

df_VCGroup_DOWPkHr = df_VCGroup_DOWPkHr.append({'DOWPkCode' : 'SuDY',
                                                'DOWPkName' : 'Sunday',
                                                'DOWGroup'  : '7-Sunday',
                                                'Prd'       : 'DY',
                                                'HrPctOf'   : 'DY' #calculate peak Hr using DY volume
                                               },ignore_index=True)

display(df_VCGroup_DOWPkHr)

#directional factor when using DY volumes for peak Hr calcs
#taken from HCM 2000 Exhibit 9-2
dDYDirectionalFactor = 0.6

#directional factor not used in Prd volume calcs, since those include directionality

SeasonCode SeasonGroup SeasonName SeasonType
0         Ann     S00-Ann     Annual     Season
1         Win     S01-Win     Winter     Season
2         Spr     S02-Spr     Spring     Season
3         Sum     S03-Sum     Summer     Season
4         Fal     S04-Fal       Fall     Season
5         Jan     M01-Jan    January      Month
6         Feb     M02-Feb   February      Month
7         Mar     M03-Mar      March      Month
8         Apr     M04-Apr      April      Month
9         May     M05-May        May      Month
10        Jun     M06-Jun       June      Month
11        Jul     M07-Jul       July      Month
12        Aug     M08-Aug     August      Month
13        Sep     M09-Sep  September      Month
14        Oct     M10-Oct    October      Month
15        Nov     M11-Nov   November      Month
16        Dec     M12-Dec   December      Month

DOWGroup DOWPkCode         DOWPkName HrPctOf Prd
0  W1-Weekday      WkAM      AM - Weekday     Prd  AM
1  W1-Weekday      WkMD  Midday - Weekday     Prd  MD
2  W1-Weekday      WkPM      PM - Weekday     Prd  PM
3    5-Friday      FrPM       PM - Friday      DY  PM
4  6-Saturday      SaDY          Saturday      DY  DY
5    7-Sunday      SuDY            Sunday      DY  DY

In [10]:
import itertools

#create df with all possible season and day-of-weak/peak groups
df_VCGroups = pd.DataFrame(list(itertools.product(df_VCGroup_Seasons['SeasonCode'],df_VCGroup_DOWPkHr['DOWPkCode'])),columns=['SeasonCode','DOWPkCode'])

df_VCGroups = pd.DataFrame(df_VCGroups)
pd.set_option('display.max_rows', df_VCGroups.shape[0]+1)

#display(df_VCGroups)

#add season data
df_VCGroups = pd.DataFrame.merge(df_VCGroups, df_VCGroup_Seasons, on='SeasonCode')

#add dow-peak data
df_VCGroups = pd.DataFrame.merge(df_VCGroups, df_VCGroup_DOWPkHr, on='DOWPkCode')

#set id name
df_VCGroups.index.name = 'VCGroupID'

df_VCGroups['VCGroupCode'] = df_VCGroups['SeasonCode'] + df_VCGroups['DOWPkCode']

df_VCGroups = df_VCGroups.drop(columns=['SeasonCode','DOWPkCode','SeasonName','DOWPkName'])

display(df_VCGroups)

SeasonGroup SeasonType    DOWGroup HrPctOf Prd VCGroupCode
VCGroupID                                                           
0             S00-Ann     Season  W1-Weekday     Prd  AM     AnnWkAM
1             S01-Win     Season  W1-Weekday     Prd  AM     WinWkAM
2             S02-Spr     Season  W1-Weekday     Prd  AM     SprWkAM
3             S03-Sum     Season  W1-Weekday     Prd  AM     SumWkAM
4             S04-Fal     Season  W1-Weekday     Prd  AM     FalWkAM
5             M01-Jan      Month  W1-Weekday     Prd  AM     JanWkAM
6             M02-Feb      Month  W1-Weekday     Prd  AM     FebWkAM
7             M03-Mar      Month  W1-Weekday     Prd  AM     MarWkAM
8             M04-Apr      Month  W1-Weekday     Prd  AM     AprWkAM
9             M05-May      Month  W1-Weekday     Prd  AM     MayWkAM
10            M06-Jun      Month  W1-Weekday     Prd  AM     JunWkAM
11            M07-Jul      Month  W1-Weekday     Prd  AM     JulWkAM
12            M08-Aug      Month  W1-Weekday     Prd  AM     AugWkAM
13            M09-Sep      Month  W1-Weekday     Prd  AM     SepWkAM
14            M10-Oct      Month  W1-Weekday     Prd  AM     OctWkAM
15            M11-Nov      Month  W1-Weekday     Prd  AM     NovWkAM
16            M12-Dec      Month  W1-Weekday     Prd  AM     DecWkAM
17            S00-Ann     Season  W1-Weekday     Prd  MD     AnnWkMD
18            S01-Win     Season  W1-Weekday     Prd  MD     WinWkMD
19            S02-Spr     Season  W1-Weekday     Prd  MD     SprWkMD
20            S03-Sum     Season  W1-Weekday     Prd  MD     SumWkMD
21            S04-Fal     Season  W1-Weekday     Prd  MD     FalWkMD
22            M01-Jan      Month  W1-Weekday     Prd  MD     JanWkMD
23            M02-Feb      Month  W1-Weekday     Prd  MD     FebWkMD
24            M03-Mar      Month  W1-Weekday     Prd  MD     MarWkMD
25            M04-Apr      Month  W1-Weekday     Prd  MD     AprWkMD
26            M05-May      Month  W1-Weekday     Prd  MD     MayWkMD
27            M06-Jun      Month  W1-Weekday     Prd  MD     JunWkMD
28            M07-Jul      Month  W1-Weekday     Prd  MD     JulWkMD
29            M08-Aug      Month  W1-Weekday     Prd  MD     AugWkMD
30            M09-Sep      Month  W1-Weekday     Prd  MD     SepWkMD
31            M10-Oct      Month  W1-Weekday     Prd  MD     OctWkMD
32            M11-Nov      Month  W1-Weekday     Prd  MD     NovWkMD
33            M12-Dec      Month  W1-Weekday     Prd  MD     DecWkMD
34            S00-Ann     Season  W1-Weekday     Prd  PM     AnnWkPM
35            S01-Win     Season  W1-Weekday     Prd  PM     WinWkPM
36            S02-Spr     Season  W1-Weekday     Prd  PM     SprWkPM
37            S03-Sum     Season  W1-Weekday     Prd  PM     SumWkPM
38            S04-Fal     Season  W1-Weekday     Prd  PM     FalWkPM
39            M01-Jan      Month  W1-Weekday     Prd  PM     JanWkPM
40            M02-Feb      Month  W1-Weekday     Prd  PM     FebWkPM
41            M03-Mar      Month  W1-Weekday     Prd  PM     MarWkPM
42            M04-Apr      Month  W1-Weekday     Prd  PM     AprWkPM
43            M05-May      Month  W1-Weekday     Prd  PM     MayWkPM
44            M06-Jun      Month  W1-Weekday     Prd  PM     JunWkPM
45            M07-Jul      Month  W1-Weekday     Prd  PM     JulWkPM
46            M08-Aug      Month  W1-Weekday     Prd  PM     AugWkPM
47            M09-Sep      Month  W1-Weekday     Prd  PM     SepWkPM
48            M10-Oct      Month  W1-Weekday     Prd  PM     OctWkPM
49            M11-Nov      Month  W1-Weekday     Prd  PM     NovWkPM
50            M12-Dec      Month  W1-Weekday     Prd  PM     DecWkPM
51            S00-Ann     Season    5-Friday      DY  PM     AnnFrPM
52            S01-Win     Season    5-Friday      DY  PM     WinFrPM
53            S02-Spr     Season    5-Friday      DY  PM     SprFrPM
54            S03-Sum     Season    5-Friday      DY  PM     SumFrPM
55            S04-Fal     Season    5-Friday      DY  PM     FalFrPM
56      

# TDM SEGID Detail

In [11]:
#column names from TDM
nameSegID      = 'SEGID'
nameFG         = 'FUNCGROUP'
nameLinks      = 'LINKS'
nameLanes      = 'LANES'
nameVol        = 'VOL'
nameCap1HL     = 'CAP1HL'
nameAT         = 'AREATYPE'
nameFT         = 'FT'
nameFTClass    = 'FTCLASS'
nameFGFac      = 'FGFAC'
namePrdFac     = 'PRDFAC'
nameDYVOL      = 'DY_VOL'
nameDirections = 'DIRECTIONS'
nameDFac       = 'DFAC'
nameMDPct      = 'MDPCT'
nameHVPct      = 'HVPCT'
nameSegTotal   = 'SegDYVol_TDM'

#column for scenario year
nameSID = 'ScenarioID'
nameS =   'ScenarioName'
nameSYr = 'ScenarioYear'

#additional column name variables
nameLT = 'LT'
nameMD = 'MD'
nameHV = 'HV'

nameVolType = 'VolType'
namePrd  = 'Prd'
nameCapPer  = 'CapPer'
nameCap1Hr  = 'Cap1Hr'
nameDir     = 'Dir'

#value for functional group (FG) total row, so that it can be removed
nameFGTotalValue = 'Total'

#arrays for values by direction

aNameDir1Columns   = ['D1_'+nameFT,'D1_'+nameFTClass,'D1_'+nameLanes,'D1_'+nameCap1HL]
aNameDir2Columns   = ['D2_'+nameFT,'D2_'+nameFTClass,'D2_'+nameLanes,'D2_'+nameCap1HL]
aNameDirColumns    = [      nameFT,      nameFTClass,      nameLanes,      nameCap1HL]    
aNameDirIndexNoDir = [nameSegID,nameFG]
aNameDirIndexWiDir = [nameSegID,nameFG,nameDir]

#arrays for values by Prd
aNamePrdFac = ['DY_PRDFAC','AM_PRDFAC','MD_PRDFAC','PM_PRDFAC','EV_PRDFAC'] #add DY_PRDFAC = 1 later in script for calc ease

#arrays for values by direction, Prd
aNameDirPrdDFac      = ['D1_DY_'+nameDFac     ,'D1_AM_'+nameDFac     ,'D1_MD_'+nameDFac     ,'D1_PM_'+nameDFac     ,'D1_EV_'+nameDFac     ,'D2_DY_'+nameDFac     ,'D2_AM_'+nameDFac     ,'D2_MD_'+nameDFac     ,'D2_PM_'+nameDFac     ,'D2_EV_'+nameDFac     ]
aNameDirPrdMDPct = ['D1_DY_'+nameMDPct,'D1_AM_'+nameMDPct,'D1_MD_'+nameMDPct,'D1_PM_'+nameMDPct,'D1_EV_'+nameMDPct,'D2_DY_'+nameMDPct,'D2_AM_'+nameMDPct,'D2_MD_'+nameMDPct,'D2_PM_'+nameMDPct,'D2_EV_'+nameMDPct]
aNameDirPrdHVPct = ['D1_DY_'+nameHVPct,'D1_AM_'+nameHVPct,'D1_MD_'+nameHVPct,'D1_PM_'+nameHVPct,'D1_EV_'+nameHVPct,'D2_DY_'+nameHVPct,'D2_AM_'+nameHVPct,'D2_MD_'+nameHVPct,'D2_PM_'+nameHVPct,'D2_EV_'+nameHVPct]

indexTotal             = [nameSegID]
indexMelt              = [nameSegID,nameFG]
#indexDY             = [nameSegID,nameFG,nameCap1HL,nameLinks,nameLanes,nameAT,nameFT]

#Hrs within Prd, for capacity
dPrdDuration = {
     'Prd'     : ['AM','MD','PM','EV','DY'],
     'PrdHrs': [   3,   6,   3,  12,     24]
     
}
df_PrdDuration = pd.DataFrame(dPrdDuration)

In [12]:
dfs_TDM =[]
dfs_TDM_Total = []

#all scenarios will be read in to allow for pivoting

for (idx, row) in df_Scenarios.iterrows():

    print(row.loc[nameS] + ' CSV Processing')

    csvFileName = os.path.join(dirTDM, row.SegSummaryCSV)

    df_TDM_import = pd.read_csv(csvFileName)
    df_TDM_import[nameFG] = df_TDM_import[nameFG].str.strip() #strip leading and trailing spaces
    
    #totals for DY segment volume
    df_TDM_SegDYVol = df_TDM_import[df_TDM_import[nameFG] == nameFGTotalValue].copy()
    df_TDM_SegDYVol = df_TDM_SegDYVol[[nameSegID,nameDYVOL]]
    df_TDM_SegDYVol = df_TDM_SegDYVol.rename(columns={nameDYVOL: nameSegTotal})
    
    dfs_TDM_Total.append(df_TDM_SegDYVol[[nameSegID,nameSegTotal]])
    
    #display(df_TDM_SegDYVol)
    
    #Remove rows with no links and total
    df_TDM_import         = df_TDM_import[df_TDM_import[nameLinks] > 0                ]
    df_TDM_import         = df_TDM_import[df_TDM_import[nameFG]    != nameFGTotalValue]

    #data with segment level values
    df_TDM_Seg = pd.DataFrame.merge(df_TDM_import[[nameSegID,nameFG,nameAT,nameFGFac]],df_TDM_SegDYVol,on=nameSegID)    
    
    #normalize data with direction fields
    df_Dir1Columns          = df_TDM_import[aNameDirIndexNoDir + aNameDir1Columns].copy()
    df_Dir1Columns.columns  = (aNameDirIndexNoDir + aNameDirColumns)
    df_Dir1Columns[nameDir] = 'D1'
    
    df_Dir2Columns          = df_TDM_import[aNameDirIndexNoDir + aNameDir2Columns].copy()
    df_Dir2Columns.columns  = (aNameDirIndexNoDir + aNameDirColumns)
    df_Dir2Columns[nameDir] = 'D2'
    
    #display(df_Dir1Columns)
    #display(df_Dir2Columns)
    
    df_TDM_Dir = pd.concat([df_Dir1Columns,df_Dir2Columns])
    #display(df_Dir)
    
    #normalize data with Prd fields
    df_TDM_import['DY_PRDFAC'] = 1
    df_TDM_PrdFac = pd.melt(df_TDM_import, id_vars=indexMelt, value_vars=aNamePrdFac)

    #directional factors
    df_TDM_PrdFac[namePrd] = df_TDM_PrdFac['variable'].str.get(0) + df_TDM_PrdFac['variable'].str.get(1)
    df_TDM_PrdFac          = df_TDM_PrdFac.rename(columns={'value': namePrdFac})
    df_TDM_PrdFac          = df_TDM_PrdFac.drop(columns=['variable'])
    
    df_TDM_Prd = df_TDM_PrdFac
    
    #display(df_TDM_Prd)
    
    #normalize data with dir/Prd fields
    df_TDM_DFac      = pd.melt(df_TDM_import, id_vars=indexMelt, value_vars=aNameDirPrdDFac     )
    df_TDM_MDPct = pd.melt(df_TDM_import, id_vars=indexMelt, value_vars=aNameDirPrdMDPct)
    df_TDM_HVPct = pd.melt(df_TDM_import, id_vars=indexMelt, value_vars=aNameDirPrdHVPct)

    #directional factors
    df_TDM_DFac[nameDir] = df_TDM_DFac['variable'].str.get(0) + df_TDM_DFac['variable'].str.get(1)
    df_TDM_DFac[namePrd] = df_TDM_DFac['variable'].str.get(3) + df_TDM_DFac['variable'].str.get(4)
    df_TDM_DFac          = df_TDM_DFac.rename(columns={'value': nameDFac})
    df_TDM_DFac          = df_TDM_DFac.drop(columns=['variable'])
    
    #display(df_TDM_DFac)
    
    #medium truck Pcts
    df_TDM_MDPct[nameDir] = df_TDM_MDPct['variable'].str.get(0) + df_TDM_MDPct['variable'].str.get(1)
    df_TDM_MDPct[namePrd] = df_TDM_MDPct['variable'].str.get(3) + df_TDM_MDPct['variable'].str.get(4)
    df_TDM_MDPct          = df_TDM_MDPct.rename(columns={'value': nameMDPct})
    df_TDM_MDPct          = df_TDM_MDPct.drop(columns=['variable'])
    
    #display(df_TDM_MDPct)    
    
    #medium truck Pcts
    df_TDM_HVPct[nameDir] = df_TDM_HVPct['variable'].str.get(0) + df_TDM_HVPct['variable'].str.get(1)
    df_TDM_HVPct[namePrd] = df_TDM_HVPct['variable'].str.get(3) + df_TDM_HVPct['variable'].str.get(4)
    df_TDM_HVPct          = df_TDM_HVPct.rename(columns={'value': nameHVPct})
    df_TDM_HVPct          = df_TDM_HVPct.drop(columns=['variable'])
    
    #display(df_TDM_HVPct)
    
    #merge dir/Prd dataframes
    df_TDM_DirPrd = pd.DataFrame.merge(df_TDM_DFac  ,df_TDM_MDPct,on=(nameSegID,nameFG,nameDir,namePrd))
    df_TDM_DirPrd = pd.DataFrame.merge(df_TDM_DirPrd,df_TDM_HVPct,on=(nameSegID,nameFG,nameDir,namePrd))
    
    #display(df_DirPrd)
    
    df_TDM_byFGDirPrd = pd.DataFrame.merge(df_TDM_Seg          ,df_TDM_Dir   ,on=(nameSegID,nameFG)) #merge direction
    df_TDM_byFGDirPrd = pd.DataFrame.merge(df_TDM_byFGDirPrd,df_TDM_Prd   ,on=(nameSegID,nameFG)) #merge Prd
    df_TDM_byFGDirPrd = pd.DataFrame.merge(df_TDM_byFGDirPrd,df_TDM_DirPrd,on=(nameSegID,nameFG,namePrd,nameDir)) #merge Prd/direction

    #calculate DY directional for peak-Hr-Pct-of-DY calcs
    #assumes when DY volumes is used, TDM directional factor not valid, eg. weekends    
    #both directions use same directional factor
    df_TDM_byFGDirPrd.loc[(df_TDM_byFGDirPrd[namePrd] == 'DY'), nameDFac] = dDYDirectionalFactor
    df_TDM_byFGDirPrd.loc[(df_TDM_byFGDirPrd[namePrd] == 'DY'), namePrd] = 'DY'
        
    df_TDM_byFGDirPrd = df_TDM_byFGDirPrd[[nameSegID,nameAT,nameSegTotal,nameFG,nameFGFac,nameDir,nameLanes,nameFT,nameFTClass,nameCap1HL,nameDFac,namePrd,namePrdFac,nameMDPct,nameHVPct]]
    display(df_TDM_byFGDirPrd)

    dfs_TDM.append(df_TDM_byFGDirPrd)

    df_Check = df_TDM_byFGDirPrd.copy()
    df_Check['FactorsCombined'] = df_Check[nameFGFac] * df_Check[nameDFac] * df_Check[namePrdFac]
    
    #The sum of all factors should 2.2 (1.0 for non-total and 2xDFac(0.6) for totals, add little extra on each side for rounding
    df_Check = df_Check.groupby(indexTotal).agg({'FactorsCombined':[np.sum]})
    df_Check.columns = df_Check.columns.droplevel(1)
    df_Check = df_Check[((df_Check['FactorsCombined'] > 2.2003) | (df_Check['FactorsCombined'] < 2.1997) & (df_Check['FactorsCombined'] != 0))]
    display(print(row.loc[nameS] + ' Checks:'))
    display(df_Check)

print('Done')

2015 Base CSV Processing


SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES    FT  \
0      0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
1      0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
2      0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
3      0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
4      0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
...           ...       ...           ...       ...    ...  ..    ...   ...   
36845   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
36846   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
36847   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
36848   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
36849   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   

                         FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPCT  HVPCT  
0         Principal Arterial        1065  0.6000  DY  1.0000    8.0    6.0  
1         Principal Arterial        1065  0.4916  AM  0.1819    6.5    4.8  
2         Principal Arterial        1065  0.4914  MD  0.3250    9.1    6.8  
3         Principal Arterial        1065  0.5010  PM  0.2595    6.8    5.1  
4         Principal Arterial        1065  0.5155  EV  0.2336    8.8    6.6  
...                          ...     ...     ...  ..     ...    ...    ...  
36845           Freeway             1473  0.6000  DY  1.0000   13.0    6.7  
36846           Freeway             1473  0.5008  AM  0.1876   11.3    5.8  
36847           Freeway             1473  0.5045  MD  0.3212   14.5    7.5  
36848           Freeway             1473  0.5156  PM  0.2597   11.6    5.9  
36849           Freeway             1473  0.5370  EV  0.2315   14.1    7.2  

[36850 rows x 15 columns]

2015 Base Checks:


None

Empty DataFrame
Columns: [FactorsCombined]
Index: []

...

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0      0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
1      0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
2      0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
3      0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
4      0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
...           ...       ...           ...       ...    ...  ..    ...  ...   
41355   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
41356   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
41357   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
41358   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
41359   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   

                  FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPCT  HVPCT  
0      Principal Arterial    1065  0.6000  DY  1.0000    7.9    5.9  
1      Principal Arterial    1065  0.5738  AM  0.1884    5.4    3.9  
2      Principal Arterial    1065  0.5042  MD  0.3186    9.0    6.8  
3      Principal Arterial    1065  0.4552  PM  0.2612    7.3    5.4  
4      Principal Arterial    1065  0.4808  EV  0.2318    9.5    7.0  
...                   ...     ...     ...  ..     ...    ...    ...  
41355      Minor Arterial     939  0.6000  DY  1.0000   17.3    7.4  
41356      Minor Arterial     939  0.4871  AM  0.1803   15.1    6.5  
41357      Minor Arterial     939  0.5018  MD  0.3062   18.5    8.3  
41358      Minor Arterial     939  0.5257  PM  0.3189   17.2    6.9  
41359      Minor Arterial     939  0.5088  EV  0.1946   17.5    7.6  

[41360 rows x 15 columns]

2050 S5 Draft Checks:


None

Empty DataFrame
Columns: [FactorsCombined]
Index: []

Done


In [13]:
#df_TDM_byFGDirPrd[df_TDM_byFGDirPrd[nameSegID]=='0015_282.2']

In [14]:
#df_TDM_Seg[df_TDM_Seg[nameSegID]=='0015_282.2']

In [15]:
df_TDM_byFGDirPrd

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0      0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
1      0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
2      0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
3      0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
4      0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
...           ...       ...           ...       ...    ...  ..    ...  ...   
41355   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
41356   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
41357   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
41358   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
41359   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   

                  FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPCT  HVPCT  
0      Principal Arterial    1065  0.6000  DY  1.0000    7.9    5.9  
1      Principal Arterial    1065  0.5738  AM  0.1884    5.4    3.9  
2      Principal Arterial    1065  0.5042  MD  0.3186    9.0    6.8  
3      Principal Arterial    1065  0.4552  PM  0.2612    7.3    5.4  
4      Principal Arterial    1065  0.4808  EV  0.2318    9.5    7.0  
...                   ...     ...     ...  ..     ...    ...    ...  
41355      Minor Arterial     939  0.6000  DY  1.0000   17.3    7.4  
41356      Minor Arterial     939  0.4871  AM  0.1803   15.1    6.5  
41357      Minor Arterial     939  0.5018  MD  0.3062   18.5    8.3  
41358      Minor Arterial     939  0.5257  PM  0.3189   17.2    6.9  
41359      Minor Arterial     939  0.5088  EV  0.1946   17.5    7.6  

[41360 rows x 15 columns]

In [16]:
df_Scenarios_toProcess

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
0              Yes       Base15          Base      2015 Base          2015   
1              Yes       Base19          Base      2019 Base          2019   
2              Yes        TIP24           TIP       2024 TIP          2024   
3              Yes        RTP30           RTP       2030 RTP          2030   
4              Yes        RTP40           RTP       2040 RTP          2040   
5              Yes        RTP50           RTP       2050 RTP          2050   
6              Yes         NB30      No Build  2030 No Build          2030   
7              Yes         NB40      No Build  2040 No Build          2040   
8              Yes         NB50      No Build  2050 No Build          2050   
9              Yes         UF30         Needs     2030 Needs          2030   
10             Yes         UF40         Needs     2040 Needs          2040   
11             Yes         UF50         Needs     2050 Needs          2050   
12             Yes         S550      Scenario  2050 S5 Draft          2050   

                                                SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                      
0                  v831_SE15_Net15_Summary_SEGID_Detailed.csv             NaN   
1                  v831_SE19_Net19_Summary_SEGID_Detailed.csv          Base15   
2                  v831_SE24_Net24_Summary_SEGID_Detailed.csv          Base19   
3                  v831_SE30_Net30_Summary_SEGID_Detailed.csv           TIP24   
4                  v831_SE40_Net40_Summary_SEGID_Detailed.csv           RTP30   
5                  v831_SE50_Net50_Summary_SEGID_Detailed.csv           RTP40   
6                  v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
7                  v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
8                  v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
9                v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
10               v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
11               v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   
12          v831_SE50_Net50_Summary_SEGID_Detailed_S5Draft...             NaN   

           AdjScenarioCode  
ScenarioID                  
0                      NaN  
1                      NaN  
2                      NaN  
3                      NaN  
4                      NaN  
5                      NaN  
6                    RTP30  
7                    RTP40  
8                    RTP50  
9                    RTP30  
10                   RTP40  
11                   RTP50  
12                   RTP50

In [17]:
df_Scenarios_toAdjust

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
6              Yes         NB30      No Build  2030 No Build          2030   
7              Yes         NB40      No Build  2040 No Build          2040   
8              Yes         NB50      No Build  2050 No Build          2050   
9              Yes         UF30         Needs     2030 Needs          2030   
10             Yes         UF40         Needs     2040 Needs          2040   
11             Yes         UF50         Needs     2050 Needs          2050   
12             Yes         S550      Scenario  2050 S5 Draft          2050   

                                                SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                      
6                  v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
7                  v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
8                  v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
9                v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
10               v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
11               v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   
12          v831_SE50_Net50_Summary_SEGID_Detailed_S5Draft...             NaN   

           AdjScenarioCode  
ScenarioID                  
6                    RTP30  
7                    RTP40  
8                    RTP50  
9                    RTP30  
10                   RTP40  
11                   RTP50  
12                   RTP50

In [18]:
#calculate adjustment for forecast for those non-RTP scenarios

dfs_ForecastAdj = []

for (idx, row) in df_Scenarios_toAdjust.iterrows():

    #print(row.loc[nameS] + ' CSV Importing')
    
    df_base = dfs_TDM_Total[idFromCode(row.loc['AdjScenarioCode'])]
    df_base.columns = (['SEGID','DYVolBase'])
    df_scenario  = dfs_TDM_Total[idFromCode(row.loc['ScenarioCode'])]
    df_scenario.columns = (['SEGID','DYVolScenario'])
    
    display(df_base)
    display(df_scenario)
    
    df_ForecastAdj = pd.DataFrame.merge(df_scenario,df_base,on=nameSegID,how='left')
    df_ForecastAdj['DYVolAdj'] = df_ForecastAdj['DYVolScenario'] - df_ForecastAdj['DYVolBase']
    
    df_ForecastAdj.to_csv(os.path.join(dirResults,'ForecastAdj_' + row.loc['ScenarioCode'] + '.csv'))
    
    display(df_ForecastAdj)
    
    dfs_ForecastAdj.append(df_ForecastAdj)

SEGID  DYVolBase
0      0006_146.9     1559.1
5      0006_149.9     1755.5
10     0006_150.6     1970.6
15     0006_152.6     2894.4
20     0006_152.9     3986.8
...           ...        ...
18850   WFRC_8215     7150.7
18855   WFRC_8216    18404.2
18860   WFRC_8217        0.0
18865   WFRC_8218    33756.9
18870   WFRC_8219     4713.8

[3775 rows x 2 columns]

SEGID  DYVolScenario
0      0006_146.9         1546.0
5      0006_149.9         1998.1
10     0006_150.6         2226.3
15     0006_152.6         3243.1
20     0006_152.9         4373.1
...           ...            ...
18350   WFRC_8213          706.9
18355   WFRC_8215         6655.8
18360   WFRC_8216        17437.8
18365   WFRC_8217            0.0
18370   WFRC_8218        34052.5

[3675 rows x 2 columns]

SEGID  DYVolScenario  DYVolBase  DYVolAdj
0     0006_146.9         1546.0     1559.1     -13.1
1     0006_149.9         1998.1     1755.5     242.6
2     0006_150.6         2226.3     1970.6     255.7
3     0006_152.6         3243.1     2894.4     348.7
4     0006_152.9         4373.1     3986.8     386.3
...          ...            ...        ...       ...
3670   WFRC_8213          706.9      710.0      -3.1
3671   WFRC_8215         6655.8     7150.7    -494.9
3672   WFRC_8216        17437.8    18404.2    -966.4
3673   WFRC_8217            0.0        0.0       0.0
3674   WFRC_8218        34052.5    33756.9     295.6

[3675 rows x 4 columns]

SEGID  DYVolBase
0      0006_146.9     1684.9
5      0006_149.9     2230.4
10     0006_150.6     2456.4
15     0006_152.6     3346.8
20     0006_152.9     4750.9
...           ...        ...
19170   WFRC_8215     9600.5
19175   WFRC_8216    22968.7
19180   WFRC_8217        0.0
19185   WFRC_8218    37570.2
19190   WFRC_8219     4935.3

[3839 rows x 2 columns]

SEGID  DYVolScenario
0      0006_146.9         1669.8
5      0006_149.9         3098.9
10     0006_150.6         3352.3
15     0006_152.6         4473.5
20     0006_152.9         6005.6
...           ...            ...
18350   WFRC_8213          829.5
18355   WFRC_8215         8957.0
18360   WFRC_8216        23391.2
18365   WFRC_8217            0.0
18370   WFRC_8218        38507.2

[3675 rows x 2 columns]

...

SEGID  DYVolScenario
0      0006_146.9         1813.3
5      0006_149.9         3029.6
10     0006_150.6         3276.9
15     0006_152.6         4372.0
20     0006_152.9         5982.7
...           ...            ...
19625   WFRC_8215        11926.5
19630   WFRC_8216        28419.9
19635   WFRC_8217        25320.7
19640   WFRC_8218        42391.0
19645   WFRC_8219        13363.9

[3930 rows x 2 columns]

SEGID  DYVolScenario  DYVolBase  DYVolAdj
0     0006_146.9         1813.3     1811.9       1.4
1     0006_149.9         3029.6     3020.6       9.0
2     0006_150.6         3276.9     3267.4       9.5
3     0006_152.6         4372.0     4370.0       2.0
4     0006_152.9         5982.7     5979.1       3.6
...          ...            ...        ...       ...
3925   WFRC_8215        11926.5    12274.6    -348.1
3926   WFRC_8216        28419.9    28433.0     -13.1
3927   WFRC_8217        25320.7    25756.0    -435.3
3928   WFRC_8218        42391.0    42419.0     -28.0
3929   WFRC_8219        13363.9    13113.3     250.6

[3930 rows x 4 columns]

SEGID  DYVolBase
0      0006_146.9     1811.9
5      0006_149.9     3020.6
10     0006_150.6     3267.4
15     0006_152.6     4370.0
20     0006_152.9     5979.1
...           ...        ...
19610   WFRC_8215    12274.6
19615   WFRC_8216    28433.0
19620   WFRC_8217    25756.0
19625   WFRC_8218    42419.0
19630   WFRC_8219    13113.3

[3927 rows x 2 columns]

SEGID  DYVolScenario
0      0006_146.9         1814.0
5      0006_149.9         2890.6
10     0006_150.6         3131.6
15     0006_152.6         4196.5
20     0006_152.9         5767.2
...           ...            ...
19610   WFRC_8215        12055.4
19615   WFRC_8216        29587.0
19620   WFRC_8217        25139.8
19625   WFRC_8218        41955.8
19630   WFRC_8219        12431.0

[3927 rows x 2 columns]

SEGID  DYVolScenario  DYVolBase  DYVolAdj
0     0006_146.9         1814.0     1811.9       2.1
1     0006_149.9         2890.6     3020.6    -130.0
2     0006_150.6         3131.6     3267.4    -135.8
3     0006_152.6         4196.5     4370.0    -173.5
4     0006_152.9         5767.2     5979.1    -211.9
...          ...            ...        ...       ...
3922   WFRC_8215        12055.4    12274.6    -219.2
3923   WFRC_8216        29587.0    28433.0    1154.0
3924   WFRC_8217        25139.8    25756.0    -616.2
3925   WFRC_8218        41955.8    42419.0    -463.2
3926   WFRC_8219        12431.0    13113.3    -682.3

[3927 rows x 4 columns]

# AADT and AvgAnnualPrdVol Forecasts (Segments, Forecasts, TDM)

In [19]:
#import arcgis libraries
from arcgis.gis import *
gis = GIS()

shp_Forecasts = os.path.join(dirData,  r'forecasts\WFRCForecasts_2019RTP_v831_20200508_StateWideMerged_20200608h.shp')
                        
#import into spatially-enabled DataFrame
sdf_Forecasts = pd.DataFrame.spatial.from_featureclass(shp_Forecasts)
sdf_Forecasts

FID                   RELEASE       SEGID ROUTE_ID        BMP  \
0        0  2019 RTP v8.3.1 20200508  0068_036.0     0068  36.037998   
1        1  2019 RTP v8.3.1 20200508   WFRC_8000     WFRC   1.488000   
2        2  2019 RTP v8.3.1 20200508  0131_001.7     0131   1.742000   
3        3  2019 RTP v8.3.1 20200508  0068_038.1     0068  38.106998   
4        4  2019 RTP v8.3.1 20200508  2927_000.0     2927   0.000000   
...    ...                       ...         ...      ...        ...   
8510  8510  2019 RTP v8.3.1 20200508    MAG_6248        0   0.000000   
8511  8511  2019 RTP v8.3.1 20200508  2822_000.0     2822   0.000000   
8512  8512  2019 RTP v8.3.1 20200508    MAG_6249        0   0.000000   
8513  8513  2019 RTP v8.3.1 20200508    MAG_6250        0   0.000000   
8514  8514  2019 RTP v8.3.1 20200508    MAG_6251        0   0.000000   

            EMP         FULLNAME  CO_FIPS    CO_NAME            X  ...  \
0     38.106998  CAMP WILLIAMS R       35  SALT LAKE  420614.3190  ...   
1      1.488000                        35  SALT LAKE  420880.8540  ...   
2      3.047000  PORTER ROCKWELL       35  SALT LAKE  422891.2500  ...   
3     39.167000  CAMP WILLIAMS R       35  SALT LAKE  419789.5850  ...   
4      1.019000    DEER RIDGE DR       35  SALT LAKE  428613.1110  ...   
...         ...              ...      ...        ...          ...  ...   
8510   0.000000                        49       UTAH  432054.9277  ...   
8511   3.328000     NEBO LOOP RD       49       UTAH  439736.1222  ...   
8512   0.000000                         0                  0.0000  ...   
8513   0.000000                         0                  0.0000  ...   
8514   0.000000                         0                  0.0000  ...   

      FAC_SUM  FAC_FAL  FAC_MAXMO  FAC_MAX  FACMANADJ  SUTRUCKS  CUTRUCKS  \
0       1.057    1.022          6    1.067          0     0.063     0.030   
1       1.057    1.022          6    1.067          0     0.035     0.025   
2       1.026    1.018          9    1.044          0     0.032     0.018   
3       1.057    1.022          6    1.067          0     0.040     0.020   
4       1.057    1.022          6    1.067          0     0.035     0.025   
...       ...      ...        ...      ...        ...       ...       ...   
8510    1.026    1.018          9    1.044          0     0.032     0.018   
8511    1.088    1.033          8    1.092          0     0.017     0.012   
8512    1.057    1.022          6    1.067          0     0.120     0.100   
8513    1.057    1.022          6    1.067          0     0.120     0.100   
8514    1.011    1.004          5    1.023          0     0.034     0.015   

      PLANAREA   Shape_Leng                                              SHAPE  
0         WFRC     0.000000  {"paths": [[[421160.5499999998, 4476386.34], [...  
1         WFRC     0.000000  {"paths": [[[420067.91000000015, 4479534.80000...  
2         WFRC     0.000000  {"paths": [[[422222.28000000026, 4480359.77], ...  
3         WFRC     0.000000  {"paths": [[[420067.91000000015, 4479534.80000...  
4         WFRC     0.000000  {"paths": [[[427935.76999999955, 4480756.36999...  
...        ...          ...                                                ...  
8510       MAG   473.796140  {"paths": [[[435487.7599999998, 4462445.02], [...  
8511       MAG  5344.226776  {"paths": [[[438394.3700000001, 4430771.32], [...  
8512       MAG   595.109691  {"paths": [[[442185.8794999998, 4440527.9736],...  
8513       MAG   441.873728  {"paths": [[[442531.98900000006, 4440253.285],...  
8514       MAG   807.882418  {"paths": [[[443317.86000000034, 4440169.38000...  

[8515 rows x 104 columns]

In [20]:
for col in sdf_Forecasts.columns: 
    print(col) 

FID
RELEASE
SEGID
ROUTE_ID
BMP
EMP
FULLNAME
CO_FIPS
CO_NAME
X
Y
DISTANCE
F2050
F2040
F2030
F2024
F2019
CH17TO50
CH40TO50
CH30TO40
CH24TO30
CH19TO24
CH15TO19
CH17TO19
FNOTES
MOREINFO
WFRC_FLG
AADT2017
AADT2016
AADT2015
AADT2014
AADT2013
AADT2012
AADT2011
AADT2010
AADT2009
AADT2008
AADT2007
AADT2006
AADT2005
AADT2004
AADT2003
AADT2002
AADT2001
AADT2000
AADT1999
AADT1998
AADT1997
AADT1996
AADT1994
AADT1993
AADT1992
AADT1991
AADT1990
AADT1989
AADT1988
AADT1987
AADT1986
AADT1985
AADT1984
AADT1983
AADT1982
AADT1981
SUTRK2017
CUTRK2017
DOWFACFC
DOWFACAT
FAC_MON
FAC_TUE
FAC_WED
FAC_THU
FAC_FRI
FAC_SAT
FAC_SUN
FAC_WDAVG
FAC_WEAVG
FAC_WEMAX
SSNGRP
SSNVOLCLS
SSNATGROUP
FAC_JAN
FAC_FEB
FAC_MAR
FAC_APR
FAC_MAY
FAC_JUN
FAC_JUL
FAC_AUG
FAC_SEP
FAC_OCT
FAC_NOV
FAC_DEC
FAC_WIN
FAC_SPR
FAC_SUM
FAC_FAL
FAC_MAXMO
FAC_MAX
FACMANADJ
SUTRUCKS
CUTRUCKS
PLANAREA
Shape_Leng
SHAPE


In [21]:
df = sdf_Forecasts

df = df[(df[nameSegID]=='0015_295.6')]

df

FID                   RELEASE       SEGID ROUTE_ID         BMP      EMP  \
388  388  2019 RTP v8.3.1 20200508  0015_295.6     0015  295.640991  297.944   

        FULLNAME  CO_FIPS    CO_NAME           X  ...  FAC_SUM  FAC_FAL  \
388  I-15 NB FWY       35  SALT LAKE  423474.649  ...    1.033    1.012   

     FAC_MAXMO  FAC_MAX  FACMANADJ  SUTRUCKS  CUTRUCKS  PLANAREA  Shape_Leng  \
388          8    1.039          0      0.24     0.067      WFRC         0.0   

                                                 SHAPE  
388  {"paths": [[[423819.33999999985, 4493412.10999...  

[1 rows x 104 columns]

In [22]:
#normalize data with forecasts

meltIndex    = ['SEGID','DOWFACFC','SSNGRP']
valueColumns = ['AADT2015','F2019','F2024','F2030','F2040','F2050']
df_Forecasts = pd.melt(sdf_Forecasts, id_vars=meltIndex, value_vars=valueColumns)
df_Forecasts.columns = ('SEGID','DOWFACFC','SsnGrp','FCOL','ForecastAADT')
df_Forecasts['FYEAR'] = (df_Forecasts['FCOL'].str[-4:]).astype('int64')
df_Forecasts['ForecastAADTAdj'] = 0 #placeholder column to preserve location
df_Forecasts['AvgAnnualPrdVol'] = 0 #placeholder column to preserve location
df_Forecasts = df_Forecasts[['SEGID','FYEAR','ForecastAADT','ForecastAADTAdj','AvgAnnualPrdVol','DOWFACFC','SsnGrp']]
df_Forecasts

SEGID  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0      0068_036.0   2015         22030                0                0   
1       WFRC_8000   2015             0                0                0   
2      0131_001.7   2015             0                0                0   
3      0068_038.1   2015         21330                0                0   
4      2927_000.0   2015             0                0                0   
...           ...    ...           ...              ...              ...   
51085    MAG_6248   2050        118000                0                0   
51086  2822_000.0   2050          2100                0                0   
51087    MAG_6249   2050         15000                0                0   
51088    MAG_6250   2050         23000                0                0   
51089    MAG_6251   2050         20000                0                0   

         DOWFACFC             SsnGrp  
0        Arterial  StatewideArterial  
1        Arterial  StatewideArterial  
2        Arterial  StatewideArterial  
3        Arterial  StatewideArterial  
4        Arterial  StatewideArterial  
...           ...                ...  
51085  Expressway  StatewideArterial  
51086    Arterial  StatewideArterial  
51087    Arterial  StatewideArterial  
51088    Arterial  StatewideArterial  
51089    Arterial  StatewideArterial  

[51090 rows x 7 columns]

In [23]:
#df_Forecasts[(df_Forecasts[nameSegID]=='0015_282.2')]

In [24]:
df_Scenarios_toProcess

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
0              Yes       Base15          Base      2015 Base          2015   
1              Yes       Base19          Base      2019 Base          2019   
2              Yes        TIP24           TIP       2024 TIP          2024   
3              Yes        RTP30           RTP       2030 RTP          2030   
4              Yes        RTP40           RTP       2040 RTP          2040   
5              Yes        RTP50           RTP       2050 RTP          2050   
6              Yes         NB30      No Build  2030 No Build          2030   
7              Yes         NB40      No Build  2040 No Build          2040   
8              Yes         NB50      No Build  2050 No Build          2050   
9              Yes         UF30         Needs     2030 Needs          2030   
10             Yes         UF40         Needs     2040 Needs          2040   
11             Yes         UF50         Needs     2050 Needs          2050   
12             Yes         S550      Scenario  2050 S5 Draft          2050   

                                                SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                      
0                  v831_SE15_Net15_Summary_SEGID_Detailed.csv             NaN   
1                  v831_SE19_Net19_Summary_SEGID_Detailed.csv          Base15   
2                  v831_SE24_Net24_Summary_SEGID_Detailed.csv          Base19   
3                  v831_SE30_Net30_Summary_SEGID_Detailed.csv           TIP24   
4                  v831_SE40_Net40_Summary_SEGID_Detailed.csv           RTP30   
5                  v831_SE50_Net50_Summary_SEGID_Detailed.csv           RTP40   
6                  v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
7                  v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
8                  v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
9                v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
10               v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
11               v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   
12          v831_SE50_Net50_Summary_SEGID_Detailed_S5Draft...             NaN   

           AdjScenarioCode  
ScenarioID                  
0                      NaN  
1                      NaN  
2                      NaN  
3                      NaN  
4                      NaN  
5                      NaN  
6                    RTP30  
7                    RTP40  
8                    RTP50  
9                    RTP30  
10                   RTP40  
11                   RTP50  
12                   RTP50

In [25]:
#Hrs within Prd, for capacity
dRoundForecast = {
     'RoundIndex'  : [ 1,  2,   3,    4,     5],
     'ForecastBin' : [ 0,100,1000,10000,100000],
     'RoundToValue': [10, 50, 100,  500,  1000]
}
df_RoundForecast = pd.DataFrame(dRoundForecast)
display(df_RoundForecast)

lRoundBins = df_RoundForecast['ForecastBin'].to_list()
lRoundBase = df_RoundForecast['RoundToValue'].to_list()

def forecast_round(x):
    base = lRoundBase[np.digitize([x],lRoundBins)[0]-1]
    return int(base * round(float(x)/base))

#df = pd.Series([11,16,21]).apply(lambda x: custom_round(x, base=5))

RoundIndex  ForecastBin  RoundToValue
0           1            0            10
1           2          100            50
2           3         1000           100
3           4        10000           500
4           5       100000          1000

In [26]:
display(lRoundBase[np.digitize([1],lRoundBins)[0]-1])
display(lRoundBase[np.digitize([54],lRoundBins)[0]-1])
display(lRoundBase[np.digitize([123],lRoundBins)[0]-1])
display(lRoundBase[np.digitize([1254],lRoundBins)[0]-1])
display(lRoundBase[np.digitize([15456],lRoundBins)[0]-1])
display(lRoundBase[np.digitize([2897651],lRoundBins)[0]-1])
display(lRoundBase[np.digitize([1564654654654],lRoundBins)[0]-1])

display(forecast_round(1))
display(forecast_round(54))
display(forecast_round(123))
display(forecast_round(1254))
display(forecast_round(15456))
display(forecast_round(2897651))
display(forecast_round(1564654654654))

10

10

50

100

500

...

100

1300

15500

2898000

1564654655000

In [27]:
#calculate forecast DY volume for each scenario to process

dfs_PrdForecasts = []
df_Forecasts_SYEAR_tocsv = pd.DataFrame()

for (idx, row) in df_Scenarios_toProcess.iterrows():

    _scenarioID = idx
    
    print(row.loc[nameS] + ' Processing')
    print(idx)
    #df_base = dfs_TDM_Total[idFromCode(row.loc['AdjScenarioCode'])]

    #display(dfs_TDM[idx])
    
    df_TDM = dfs_TDM[idx]
    
    #get TDM year
    _scenarioyear = yearFromID(_scenarioID)
    
    #filter only for year of forecast
    
    df_Forecasts['ForecastAADTAdj'] = df_Forecasts['ForecastAADT'] # set adjusted volume so value is set for unadjusted scenarios
    
    df_Forecasts_SYEAR = df_Forecasts[df_Forecasts.FYEAR == _scenarioyear]
    
    #adjust forecast
    
    for (idx, row) in df_Scenarios_toAdjust.iterrows():
        if (_scenarioID == idx):
            #display("adjust this")
            
            #get adjust id
            _adjustId = df_Scenarios_toAdjust.index.get_loc(idx)

            #display(_adjustId)
            #display(dfs_ForecastAdj[_adjustId])
            
            df_Forecasts_Adjust = pd.DataFrame.merge(df_Forecasts_SYEAR,dfs_ForecastAdj[_adjustId],on='SEGID')
            
            #adjust volume. if scenario vol = 0 then zero out forecast volume, otherwise forecast volume is adjusted
            df_Forecasts_Adjust.loc[(df_Forecasts_Adjust['DYVolScenario'] == 0), 'ForecastAADTAdj'] = 0
            df_Forecasts_Adjust.loc[(df_Forecasts_Adjust['DYVolScenario']  > 0), 'ForecastAADTAdj'] = df_Forecasts_Adjust['ForecastAADT'] + df_Forecasts_Adjust['DYVolAdj'] 
            
            df_Forecasts_Adjust.loc[(df_Forecasts_Adjust['DYVolScenario'] == 0), 'ForecastAADTAdj'] = 0
            
            #if adjustment < 0 then bring to 0
            df_Forecasts_Adjust.loc[(df_Forecasts_Adjust['ForecastAADTAdj']   < 0), 'ForecastAADTAdj'] = 0  
            
            #display(df_Forecasts_Adjust) 
            
            df_Forecasts_Adjust = df_Forecasts_Adjust[['SEGID','FYEAR','ForecastAADT','ForecastAADTAdj','AvgAnnualPrdVol','DOWFACFC','SsnGrp']]
            #df_Forecasts_Adjust = df_Forecasts_Adjust.rename(columns={"DYVolBase": "ForecastAADT"})
            
            #display(df_Forecasts_Adjust['ForecastAADTAdj'])
            df_Forecasts_Adjust['RoundBin'] = np.digitize(df_Forecasts_Adjust['ForecastAADTAdj'],lRoundBins)
            df_Forecasts_Adjust_forRounding = pd.DataFrame.merge(df_Forecasts_Adjust,df_RoundForecast,left_on='RoundBin',right_on='RoundIndex')
            df_Forecasts_Adjust_forRounding['ForecastAADTAdjRounded'] = round((df_Forecasts_Adjust_forRounding['ForecastAADTAdj']/df_Forecasts_Adjust_forRounding['RoundToValue']),0)*df_Forecasts_Adjust_forRounding['RoundToValue']
            df_Forecasts_Adjust_forRounding = df_Forecasts_Adjust_forRounding.fillna(0)
            df_Forecasts_Adjust_forRounding['ForecastAADTAdjRounded'] = df_Forecasts_Adjust_forRounding['ForecastAADTAdjRounded'].astype(int)
            display(df_Forecasts_Adjust_forRounding[['ForecastAADTAdj','RoundBin','RoundToValue','ForecastAADTAdjRounded']])
            
            df_Forecasts_Adjust_forRounding['ForecastAADTAdj'] = df_Forecasts_Adjust_forRounding['ForecastAADTAdjRounded']
            
            df_Forecasts_Adjust_forRounding = df_Forecasts_Adjust_forRounding.drop(columns=['RoundIndex','ForecastBin','RoundBin','RoundToValue','ForecastAADTAdjRounded'])
            
            df_Forecasts_SYEAR = df_Forecasts_Adjust_forRounding.copy()            
            
    df_Forecasts_SYEAR = df_Forecasts_SYEAR.fillna(0)
    #df_Forecasts_SYEAR['ForecastAADT'] = df_Forecasts_SYEAR['ForecastAADT'].astype(int)
    #df_Forecasts_SYEAR['ForecastAADTAdj'] = df_Forecasts_SYEAR['ForecastAADTAdj'].astype(int)
    
    #display(df_Forecasts_SYEAR)
    
    df_Forecasts_SYEAR_export = df_Forecasts_SYEAR.copy()
    df_Forecasts_SYEAR_export['ScenarioCode'] = codeFromID(_scenarioID)
    df_Forecasts_SYEAR_export = df_Forecasts_SYEAR_export[['ScenarioCode','SEGID','ForecastAADT']]
    
    df_Forecasts_SYEAR_tocsv = pd.concat([df_Forecasts_SYEAR_tocsv,df_Forecasts_SYEAR_export])
    
    #display(os.path.join(dirResults + "0_Forecast_" + codeFromID(_scenarioID) + ".csv"))
    #df_Forecasts_SYEAR_export.to_csv(os.path.join(dirResults + r"\\0_Forecast_" + codeFromID(_scenarioID) + ".csv"),index=False)
    
    #join with TDM data
    df_Forecasts_withPrd = pd.DataFrame.merge(df_TDM, df_Forecasts_SYEAR, on=('SEGID'))
    
    df_Forecasts_withPrd['AvgAnnualPrdVol'] = df_Forecasts_withPrd['ForecastAADTAdj'] * df_Forecasts_withPrd[nameFGFac] * df_Forecasts_withPrd[nameDFac] * df_Forecasts_withPrd[namePrdFac]
    
    #display(df_Forecasts_withPrd.head(20))
    
    dfs_PrdForecasts.append(df_Forecasts_withPrd)

display(os.path.join(dirResults + r"\\0_Forecasts.csv"))
df_Forecasts_SYEAR_tocsv.to_csv(os.path.join(dirResults + r"\\0_Forecasts.csv"),index=False)


2015 Base Processing
0
2019 Base Processing
1
2024 TIP Processing
2
2030 RTP Processing
3
2040 RTP Processing
4
2050 RTP Processing
5
2030 No Build Processing
6


ForecastAADTAdj  RoundBin  RoundToValue  ForecastAADTAdjRounded
0             48004.4         4           500                   48000
1             16923.2         4           500                   17000
2             31978.1         4           500                   32000
3             34666.0         4           500                   34500
4             22533.0         4           500                   22500
...               ...       ...           ...                     ...
3666            168.9         2            50                     150
3667            162.2         2            50                     150
3668            113.0         2            50                     100
3669            630.9         2            50                     650
3670            313.5         2            50                     300

[3671 rows x 4 columns]

2040 No Build Processing
7


ForecastAADTAdj  RoundBin  RoundToValue  ForecastAADTAdjRounded
0             48920.1         4           500                   49000
1             25166.9         4           500                   25000
2             12111.7         4           500                   12000
3             37638.5         4           500                   37500
4             15692.2         4           500                   15500
...               ...       ...           ...                     ...
3666            660.9         2            50                     650
3667            298.4         2            50                     300
3668            544.7         2            50                     550
3669            760.8         2            50                     750
3670            237.9         2            50                     250

[3671 rows x 4 columns]

2050 No Build Processing
8


...

2050 Needs Processing
11


ForecastAADTAdj  RoundBin  RoundToValue  ForecastAADTAdjRounded
0             10132.6         4           500                   10000
1             56174.6         4           500                   56000
2             20949.8         4           500                   21000
3             31991.7         4           500                   32000
4             28718.9         4           500                   28500
...               ...       ...           ...                     ...
3893            698.2         2            50                     700
3894            948.8         2            50                     950
3895            200.9         2            50                     200
3896            100.1         2            50                     100
3897            400.5         2            50                     400

[3898 rows x 4 columns]

2050 S5 Draft Processing
12


ForecastAADTAdj  RoundBin  RoundToValue  ForecastAADTAdjRounded
0              8622.8         3           100                    8600
1              6428.3         3           100                    6400
2              2692.9         3           100                    2700
3              2344.2         3           100                    2300
4              3356.5         3           100                    3400
...               ...       ...           ...                     ...
3890              0.0         1            10                       0
3891             99.7         1            10                     100
3892              0.0         1            10                       0
3893              0.0         1            10                       0
3894              0.0         1            10                       0

[3895 rows x 4 columns]

'E:\\GitHub\\V-over-C-Calculations\\results\\\\0_Forecasts.csv'

In [30]:
#format forecasts as table for joining with other analysis
table = pd.pivot_table(df_Forecasts_SYEAR_tocsv, values='ForecastAADT', index=['SEGID'],
                    columns=['ScenarioCode'], aggfunc=np.sum, fill_value=0)
display(table)

table.to_csv(os.path.join(dirResults + r"\\0_Forecasts_Table.csv"))

ScenarioCode  Base15  Base19   NB30   NB40   NB50  RTP30  RTP40  RTP50   S550  \
SEGID                                                                           
0006_000.0       375       0      0      0      0      0      0    600      0   
0006_000.7       375       0      0      0      0      0      0    550      0   
0006_016.0       375       0      0      0      0      0      0    600      0   
0006_046.0       390       0      0      0      0      0      0    600      0   
0006_060.2       390       0      0      0      0      0      0    600      0   
...              ...     ...    ...    ...    ...    ...    ...    ...    ...   
WFRC_8215          0    3700   6300   8800  11500   6300   8800  11500  11500   
WFRC_8216          0       0  15000  19000  23500  15000  19000  23500  23500   
WFRC_8217          0       0      0      0  19500      0      0  19500  19500   
WFRC_8218          0   25500  30000  33500  37500  30000  33500  37500  37500   
WFRC_8219          0       0      0      0      0   6200   6400  13500  13500   

ScenarioCode  TIP24   UF30   UF40   UF50  
SEGID                                     
0006_000.0        0      0      0      0  
0006_000.7        0      0      0      0  
0006_016.0        0      0      0      0  
0006_046.0        0      0      0      0  
0006_060.2        0      0      0      0  
...             ...    ...    ...    ...  
WFRC_8215      4500   6300   8800  11500  
WFRC_8216     12000  15000  19000  23500  
WFRC_8217         0      0      0  19500  
WFRC_8218     27500  30000  33500  37500  
WFRC_8219         0   6200   6400  13500  

[8508 rows x 13 columns]

In [178]:
dfs_PrdForecasts[0]

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES    FT  \
0      0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
1      0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
2      0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
3      0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
4      0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
...           ...       ...           ...       ...    ...  ..    ...   ...   
36815   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
36816   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
36817   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
36818   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
36819   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   

                         FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPCT  HVPCT  \
0         Principal Arterial        1065  0.6000  DY  1.0000    8.0    6.0   
1         Principal Arterial        1065  0.4916  AM  0.1819    6.5    4.8   
2         Principal Arterial        1065  0.4914  MD  0.3250    9.1    6.8   
3         Principal Arterial        1065  0.5010  PM  0.2595    6.8    5.1   
4         Principal Arterial        1065  0.5155  EV  0.2336    8.8    6.6   
...                          ...     ...     ...  ..     ...    ...    ...   
36815           Freeway             1473  0.6000  DY  1.0000   13.0    6.7   
36816           Freeway             1473  0.5008  AM  0.1876   11.3    5.8   
36817           Freeway             1473  0.5045  MD  0.3212   14.5    7.5   
36818           Freeway             1473  0.5156  PM  0.2597   11.6    5.9   
36819           Freeway             1473  0.5370  EV  0.2315   14.1    7.2   

       FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol     DOWFACFC  \
0       2015          1400             1400       840.000000     Arterial   
1       2015          1400             1400       125.190856     Arterial   
2       2015          1400             1400       223.587000     Arterial   
3       2015          1400             1400       182.013300     Arterial   
4       2015          1400             1400       168.589120     Arterial   
...      ...           ...              ...              ...          ...   
36815   2015             0                0         0.000000  FreewayI215   
36816   2015             0                0         0.000000  FreewayI215   
36817   2015             0                0         0.000000  FreewayI215   
36818   2015             0                0         0.000000  FreewayI215   
36819   2015             0                0         0.000000  FreewayI215   

                  SsnGrp  
0      StatewideArterial  
1      StatewideArterial  
2      StatewideArterial  
3      StatewideArterial  
4      StatewideArterial  
...                  ...  
36815        FreewayI215  
36816        FreewayI215  
36817        FreewayI215  
36818        FreewayI215  
36819        FreewayI215  

[36820 rows x 21 columns]

In [179]:
df = dfs_PrdForecasts[0]

df[(df[nameSegID]=='0015_282.2')]

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP   FGFAC Dir  LANES    FT  \
830  0015_282.2       3.0      129585.4  Arterial  0.0043  D1    1.0   4.0   
831  0015_282.2       3.0      129585.4  Arterial  0.0043  D1    1.0   4.0   
832  0015_282.2       3.0      129585.4  Arterial  0.0043  D1    1.0   4.0   
833  0015_282.2       3.0      129585.4  Arterial  0.0043  D1    1.0   4.0   
834  0015_282.2       3.0      129585.4  Arterial  0.0043  D1    1.0   4.0   
835  0015_282.2       3.0      129585.4  Arterial  0.0043  D2    1.0   4.0   
836  0015_282.2       3.0      129585.4  Arterial  0.0043  D2    1.0   4.0   
837  0015_282.2       3.0      129585.4  Arterial  0.0043  D2    1.0   4.0   
838  0015_282.2       3.0      129585.4  Arterial  0.0043  D2    1.0   4.0   
839  0015_282.2       3.0      129585.4  Arterial  0.0043  D2    1.0   4.0   
840  0015_282.2       3.0      129585.4   Freeway  0.9028  D1    3.0  33.0   
841  0015_282.2       3.0      129585.4   Freeway  0.9028  D1    3.0  33.0   
842  0015_282.2       3.0      129585.4   Freeway  0.9028  D1    3.0  33.0   
843  0015_282.2       3.0      129585.4   Freeway  0.9028  D1    3.0  33.0   
844  0015_282.2       3.0      129585.4   Freeway  0.9028  D1    3.0  33.0   
845  0015_282.2       3.0      129585.4   Freeway  0.9028  D2    3.0  33.0   
846  0015_282.2       3.0      129585.4   Freeway  0.9028  D2    3.0  33.0   
847  0015_282.2       3.0      129585.4   Freeway  0.9028  D2    3.0  33.0   
848  0015_282.2       3.0      129585.4   Freeway  0.9028  D2    3.0  33.0   
849  0015_282.2       3.0      129585.4   Freeway  0.9028  D2    3.0  33.0   
850  0015_282.2       3.0      129585.4   Managed  0.0929  D1    1.0  38.0   
851  0015_282.2       3.0      129585.4   Managed  0.0929  D1    1.0  38.0   
852  0015_282.2       3.0      129585.4   Managed  0.0929  D1    1.0  38.0   
853  0015_282.2       3.0      129585.4   Managed  0.0929  D1    1.0  38.0   
854  0015_282.2       3.0      129585.4   Managed  0.0929  D1    1.0  38.0   
855  0015_282.2       3.0      129585.4   Managed  0.0929  D2    1.0  38.0   
856  0015_282.2       3.0      129585.4   Managed  0.0929  D2    1.0  38.0   
857  0015_282.2       3.0      129585.4   Managed  0.0929  D2    1.0  38.0   
858  0015_282.2       3.0      129585.4   Managed  0.0929  D2    1.0  38.0   
859  0015_282.2       3.0      129585.4   Managed  0.0929  D2    1.0  38.0   

                       FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPCT  HVPCT  \
830          Collector             748  0.6000  DY  1.0000   15.9    6.0   
831          Collector             748  0.8304  AM  0.2027   16.9    4.9   
832          Collector             748  0.5890  MD  0.1933   15.6    5.5   
833          Collector             748  0.2968  PM  0.4643   16.9    7.2   
834          Collector             748  0.4692  EV  0.1397   11.6    7.0   
835          Collector             748  0.6000  DY  1.0000   12.3    5.3   
836          Collector             748  0.1696  AM  0.2027   10.4    3.8   
837          Collector             748  0.4110  MD  0.1933    9.2    3.5   
838          Collector             748  0.7032  PM  0.4643   14.6    6.5   
839          Collector             748  0.5308  EV  0.1397    6.3    2.5   
840           Freeway             1730  0.6000  DY  1.0000   14.1    6.3   
841           Freeway             1730  0.5391  AM  0.1895    9.1    4.0   
842           Freeway             1730  0.4870  MD  0.3353   15.8    7.1   
843           Freeway             1730  0.4486  PM  0.2347   12.9    5.8   
844           Freeway             1730  0.4308  EV  0.2405   17.5    7.7   
845           Freeway             1730  0.6000  DY  1.0000   13.1    5.8   
846           Freeway             1730  0.4609  AM  0.1895   12.3    5.1   
847           Freeway             1730  0.5130  MD  0.3353   15.4    6.9   
848           Freeway             1730  0.5514  PM  0.2347    9.9    4.5   
849           Freeway             1730  0.5692  EV  0.2405   13.7    6.

# Adjust for Season, DOW

In [180]:
#read in data from other notebook pre-processing

csv_SeasonFactors = os.path.join(dirFactors, r'SeasonFactors.csv')
csv_DOWFactors = os.path.join(dirFactors, r'DOWFactors.csv')
csv_TODFactors = os.path.join(dirFactors, r'TODFactors.csv')

df_SeasonFactors = pd.read_csv(csv_SeasonFactors)
df_DOWFactors = pd.read_csv(csv_DOWFactors)
df_TODFactors = pd.read_csv(csv_TODFactors)

df_SeasonFactors = df_SeasonFactors.rename(columns={"FuncGroup": nameFG, "AreaType": nameAT})
df_DOWFactors = df_DOWFactors.rename(columns={"FuncGroup": nameFG, "AreaType": nameAT})
df_TODFactors = df_TODFactors.rename(columns={"FuncGroup": nameFG, "AreaType": nameAT})

display(df_SeasonFactors)
display(df_DOWFactors)
display(df_TODFactors)
display(df_TODFactors[df_TODFactors['SeasonGroup']=='S00-Ann'])

SsnGrp      SsnATGroup     SsnVolCls  AREATYPE  Vol_From  \
0            AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
1            AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
2            AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
3            AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
4            AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
...                 ...             ...           ...       ...       ...   
8887  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
8888  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
8889  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
8890  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
8891  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   

       Vol_To FUNCGROUP SiteGroupSeason SeasonGroup  SeasonFactor  
0     1000000  Arterial             SN0     M01-Jan         0.273  
1     1000000  Arterial             SN0     M02-Feb         0.303  
2     1000000  Arterial             SN0     M03-Mar         0.397  
3     1000000  Arterial             SN0     M04-Apr         0.499  
4     1000000  Arterial             SN0     M05-May         1.005  
...       ...       ...             ...         ...           ...  
8887  1000000   CD Road             SNX     S03-Sum         1.066  
8888  1000000   CD Road             SNX     S04-Fal         1.001  
8889  1000000   CD Road             SNX    MaxMonth         1.099  
8890  1000000   CD Road             SNX   MaxSeason         1.066  
8891  1000000   CD Road             SNX     S00-Ann         1.000  

[8892 rows x 10 columns]

DOWFACFC  AREATYPE FUNCGROUP SiteGroupDOW     DOWGroup  DOWFactor
0        Arterial         1  Arterial          WD0     1-Monday      0.907
1        Arterial         1  Arterial          WD0    2-Tuesday      0.902
2        Arterial         1  Arterial          WD0  3-Wednesday      0.943
3        Arterial         1  Arterial          WD0   4-Thursday      0.995
4        Arterial         1  Arterial          WD0     5-Friday      1.170
...           ...       ...       ...          ...          ...        ...
2335  FreewayUS40         5   CD Road          WDK     5-Friday      1.170
2336  FreewayUS40         5   CD Road          WDK   6-Saturday      1.029
2337  FreewayUS40         5   CD Road          WDK     7-Sunday      0.777
2338  FreewayUS40         5   CD Road          WDK   W1-Weekday      1.007
2339  FreewayUS40         5   CD Road          WDK    MaxSatSun      1.007

[2340 rows x 6 columns]

SiteGroupSeason SeasonGroup    DOWGroup Prd HrPctOf  VolPkHrPct
0                 SN0     M01-Jan    1-Monday  AM     Prd      0.5528
1                 SN0     M01-Jan    1-Monday  DY     Prd      0.1351
2                 SN0     M01-Jan    1-Monday  EV     Prd      0.2926
3                 SN0     M01-Jan    1-Monday  MD     Prd      0.2534
4                 SN0     M01-Jan    1-Monday  PM     Prd      0.4179
...               ...         ...         ...  ..     ...         ...
58135             XX4     S04-Fal  W2-Weekend  AM      DY      0.0611
58136             XX4     S04-Fal  W2-Weekend  DY      DY      0.0872
58137             XX4     S04-Fal  W2-Weekend  EV      DY      0.0623
58138             XX4     S04-Fal  W2-Weekend  MD      DY      0.0658
58139             XX4     S04-Fal  W2-Weekend  PM      DY      0.0867

[58140 rows x 6 columns]

SiteGroupSeason SeasonGroup    DOWGroup Prd HrPctOf  VolPkHrPct
540               SN0     S00-Ann    1-Monday  AM     Prd      0.4722
541               SN0     S00-Ann    1-Monday  DY     Prd      0.1144
542               SN0     S00-Ann    1-Monday  EV     Prd      0.2825
543               SN0     S00-Ann    1-Monday  MD     Prd      0.2266
544               SN0     S00-Ann    1-Monday  PM     Prd      0.3920
...               ...         ...         ...  ..     ...         ...
57955             XX4     S00-Ann  W2-Weekend  AM      DY      0.0608
57956             XX4     S00-Ann  W2-Weekend  DY      DY      0.0872
57957             XX4     S00-Ann  W2-Weekend  EV      DY      0.0617
57958             XX4     S00-Ann  W2-Weekend  MD      DY      0.0658
57959             XX4     S00-Ann  W2-Weekend  PM      DY      0.0867

[3420 rows x 6 columns]

In [181]:
df_SD = pd.DataFrame.merge(df_SeasonFactors,df_DOWFactors,on=(nameAT,nameFG))
df_SD

SsnGrp      SsnATGroup     SsnVolCls  AREATYPE  Vol_From  \
0               AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
1               AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
2               AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
3               AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
4               AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
...                    ...             ...           ...       ...       ...   
1040359  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
1040360  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
1040361  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
1040362  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
1040363  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   

          Vol_To FUNCGROUP SiteGroupSeason SeasonGroup  SeasonFactor  \
0        1000000  Arterial             SN0     M01-Jan         0.273   
1        1000000  Arterial             SN0     M01-Jan         0.273   
2        1000000  Arterial             SN0     M01-Jan         0.273   
3        1000000  Arterial             SN0     M01-Jan         0.273   
4        1000000  Arterial             SN0     M01-Jan         0.273   
...          ...       ...             ...         ...           ...   
1040359  1000000   CD Road             SNX     S00-Ann         1.000   
1040360  1000000   CD Road             SNX     S00-Ann         1.000   
1040361  1000000   CD Road             SNX     S00-Ann         1.000   
1040362  1000000   CD Road             SNX     S00-Ann         1.000   
1040363  1000000   CD Road             SNX     S00-Ann         1.000   

            DOWFACFC SiteGroupDOW     DOWGroup  DOWFactor  
0           Arterial          WD0     1-Monday      0.907  
1           Arterial          WD0    2-Tuesday      0.902  
2           Arterial          WD0  3-Wednesday      0.943  
3           Arterial          WD0   4-Thursday      0.995  
4           Arterial          WD0     5-Friday      1.170  
...              ...          ...          ...        ...  
1040359  FreewayUS40          WDK     5-Friday      1.170  
1040360  FreewayUS40          WDK   6-Saturday      1.029  
1040361  FreewayUS40          WDK     7-Sunday      0.777  
1040362  FreewayUS40          WDK   W1-Weekday      1.007  
1040363  FreewayUS40          WDK    MaxSatSun      1.007  

[1040364 rows x 14 columns]

In [182]:
#add season factor

dfs_PrdForecasts_Season = []

#for (idx, row) in dfs_PrdForecasts.iterrows():

for df_PrdForecasts in dfs_PrdForecasts: 
    
    #joing forecasts data with season factors
    df_PrdForecasts_Season = pd.DataFrame.merge(df_PrdForecasts,df_SeasonFactors,on=('SsnGrp',nameFG,nameAT),how='left')
    
    #remove unapplicable volume classes
    df_PrdForecasts_Season = df_PrdForecasts_Season[(df_PrdForecasts_Season.ForecastAADT >= df_PrdForecasts_Season.Vol_From) & (df_PrdForecasts_Season.ForecastAADT < df_PrdForecasts_Season.Vol_To)]
    
    #calculate Average Season
    df_PrdForecasts_Season['AvgSsnPrdVol'] = df_PrdForecasts_Season['AvgAnnualPrdVol'] *df_PrdForecasts_Season['SeasonFactor'] 
    df_PrdForecasts_Season['AvgSsnPrdVol'] = df_PrdForecasts_Season['AvgSsnPrdVol'].astype(int)
    
    display(df_PrdForecasts_Season)
    
    dfs_PrdForecasts_Season.append(df_PrdForecasts_Season)
    

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES    FT  \
19      0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
20      0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
21      0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
22      0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
23      0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
...            ...       ...           ...       ...    ...  ..    ...   ...   
772535   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
772536   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
772537   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
772538   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
772539   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   

                          FTCLASS  CAP1HL   DFAC Prd  PRDFAC  MDPCT  HVPCT  \
19         Principal Arterial        1065  0.600  DY  1.0000    8.0    6.0   
20         Principal Arterial        1065  0.600  DY  1.0000    8.0    6.0   
21         Principal Arterial        1065  0.600  DY  1.0000    8.0    6.0   
22         Principal Arterial        1065  0.600  DY  1.0000    8.0    6.0   
23         Principal Arterial        1065  0.600  DY  1.0000    8.0    6.0   
...                           ...     ...    ...  ..     ...    ...    ...   
772535           Freeway             1473  0.537  EV  0.2315   14.1    7.2   
772536           Freeway             1473  0.537  EV  0.2315   14.1    7.2   
772537           Freeway             1473  0.537  EV  0.2315   14.1    7.2   
772538           Freeway             1473  0.537  EV  0.2315   14.1    7.2   
772539           Freeway             1473  0.537  EV  0.2315   14.1    7.2   

        FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol     DOWFACFC  \
19       2015          1400             1400            840.0     Arterial   
20       2015          1400             1400            840.0     Arterial   
21       2015          1400             1400            840.0     Arterial   
22       2015          1400             1400            840.0     Arterial   
23       2015          1400             1400            840.0     Arterial   
...       ...           ...              ...              ...          ...   
772535   2015             0                0              0.0  FreewayI215   
772536   2015             0                0              0.0  FreewayI215   
772537   2015             0                0              0.0  FreewayI215   
772538   2015             0                0              0.0  FreewayI215   
772539   2015             0                0              0.0  FreewayI215   

                   SsnGrp      SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
19      StatewideArterial         1-Rural    UTRuralLow         0     2500   
20      StatewideArterial         1-Rural    UTRuralLow         0     2500   
21      StatewideArterial         1-Rural    UTRuralLow         0     2500   
22      StatewideArterial         1-Rural    UTRuralLow         0     2500   
23      StatewideArterial         1-Rural    UTRuralLow         0     2500   
...                   ...             ...           ...       ...      ...   
772535        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
772536        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
772537        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
772538        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
772539        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   

       SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  
19                 SNP     M01-Jan         0.815           684  
20                 SNP     M02-Feb         0.862           724  
21                 SNP     M03-Mar         0.9

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
19      0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
20      0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
21      0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
22      0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
23      0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
798375   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
798376   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
798377   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
798378   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
798379   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   

                   FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPCT  HVPCT  FYEAR  \
19      Principal Arterial    1065  0.6000  DY  1.0000    7.9    5.9   2050   
20      Principal Arterial    1065  0.6000  DY  1.0000    7.9    5.9   2050   
21      Principal Arterial    1065  0.6000  DY  1.0000    7.9    5.9   2050   
22      Principal Arterial    1065  0.6000  DY  1.0000    7.9    5.9   2050   
23      Principal Arterial    1065  0.6000  DY  1.0000    7.9    5.9   2050   
...                    ...     ...     ...  ..     ...    ...    ...    ...   
798375      Minor Arterial     939  0.5088  EV  0.1946   17.5    7.6   2050   
798376      Minor Arterial     939  0.5088  EV  0.1946   17.5    7.6   2050   
798377      Minor Arterial     939  0.5088  EV  0.1946   17.5    7.6   2050   
798378      Minor Arterial     939  0.5088  EV  0.1946   17.5    7.6   2050   
798379      Minor Arterial     939  0.5088  EV  0.1946   17.5    7.6   2050   

        ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  DOWFACFC  \
19              2100             2100       1260.00000  Arterial   
20              2100             2100       1260.00000  Arterial   
21              2100             2100       1260.00000  Arterial   
22              2100             2100       1260.00000  Arterial   
23              2100             2100       1260.00000  Arterial   
...              ...              ...              ...       ...   
798375         13500            13000       1287.16224  Arterial   
798376         13500            13000       1287.16224  Arterial   
798377         13500            13000       1287.16224  Arterial   
798378         13500            13000       1287.16224  Arterial   
798379         13500            13000       1287.16224  Arterial   

                   SsnGrp    SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
19      StatewideArterial       1-Rural    UTRuralLow         0     2500   
20      StatewideArterial       1-Rural    UTRuralLow         0     2500   
21      StatewideArterial       1-Rural    UTRuralLow         0     2500   
22      StatewideArterial       1-Rural    UTRuralLow         0     2500   
23      StatewideArterial       1-Rural    UTRuralLow         0     2500   
...                   ...           ...           ...       ...      ...   
798375  StatewideArterial  2-Transition  0-AllVolumes         0  1000000   
798376  StatewideArterial  2-Transition  0-AllVolumes         0  1000000   
798377  StatewideArterial  2-Transition  0-AllVolumes         0  1000000   
798378  StatewideArterial  2-Transition  0-AllVolumes         0  1000000   
798379  StatewideArterial  2-Transition  0-AllVolumes         0  1000000   

       SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  
19                 SNP     M01-Jan         0.815          1026  
20                 SNP     M02-Feb         0.862          1086  
21                 SNP     M03-Mar         0.949          1195  
22                 SNP     M04-Apr         1.023          1288  
23                 SNP     M05-May         1.079          13

In [183]:
#add dow factor

dfs_PrdForecasts_Season_DOW = []

#for (idx, row) in dfs_PrdForecasts.iterrows():

for df_PrdForecasts_Season in dfs_PrdForecasts_Season: 
    
    #joing forecasts data with season factors
    df_PrdForecasts_Season_DOW = pd.DataFrame.merge(df_PrdForecasts_Season,df_DOWFactors,on=('DOWFACFC',nameFG,nameAT),how='left')
    
    #calculate Average Season DOW
    df_PrdForecasts_Season_DOW['AvgSsnDOWPrdVol'] = df_PrdForecasts_Season_DOW['AvgSsnPrdVol'] * df_PrdForecasts_Season_DOW['DOWFactor'] 
    df_PrdForecasts_Season_DOW['AvgSsnDOWPrdVol'] = df_PrdForecasts_Season_DOW['AvgSsnDOWPrdVol'].astype(int)

    display(df_PrdForecasts_Season_DOW)
    
    dfs_PrdForecasts_Season_DOW.append(df_PrdForecasts_Season_DOW)

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES    FT  \
0        0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
1        0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
2        0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
3        0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
4        0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0   2.0   
...             ...       ...           ...       ...    ...  ..    ...   ...   
6296215   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
6296216   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
6296217   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
6296218   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   
6296219   WFRC_8218       3.0       24394.7   CD Road    1.0  D2    1.0  31.0   

                           FTCLASS  CAP1HL   DFAC Prd  PRDFAC  MDPCT  HVPCT  \
0           Principal Arterial        1065  0.600  DY  1.0000    8.0    6.0   
1           Principal Arterial        1065  0.600  DY  1.0000    8.0    6.0   
2           Principal Arterial        1065  0.600  DY  1.0000    8.0    6.0   
3           Principal Arterial        1065  0.600  DY  1.0000    8.0    6.0   
4           Principal Arterial        1065  0.600  DY  1.0000    8.0    6.0   
...                            ...     ...    ...  ..     ...    ...    ...   
6296215           Freeway             1473  0.537  EV  0.2315   14.1    7.2   
6296216           Freeway             1473  0.537  EV  0.2315   14.1    7.2   
6296217           Freeway             1473  0.537  EV  0.2315   14.1    7.2   
6296218           Freeway             1473  0.537  EV  0.2315   14.1    7.2   
6296219           Freeway             1473  0.537  EV  0.2315   14.1    7.2   

         FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol     DOWFACFC  \
0         2015          1400             1400            840.0     Arterial   
1         2015          1400             1400            840.0     Arterial   
2         2015          1400             1400            840.0     Arterial   
3         2015          1400             1400            840.0     Arterial   
4         2015          1400             1400            840.0     Arterial   
...        ...           ...              ...              ...          ...   
6296215   2015             0                0              0.0  FreewayI215   
6296216   2015             0                0              0.0  FreewayI215   
6296217   2015             0                0              0.0  FreewayI215   
6296218   2015             0                0              0.0  FreewayI215   
6296219   2015             0                0              0.0  FreewayI215   

                    SsnGrp      SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
0        StatewideArterial         1-Rural    UTRuralLow         0     2500   
1        StatewideArterial         1-Rural    UTRuralLow         0     2500   
2        StatewideArterial         1-Rural    UTRuralLow         0     2500   
3        StatewideArterial         1-Rural    UTRuralLow         0     2500   
4        StatewideArterial         1-Rural    UTRuralLow         0     2500   
...                    ...             ...           ...       ...      ...   
6296215        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
6296216        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
6296217        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
6296218        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
6296219        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   

        SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol SiteGroupDOW  \
0                   SNP     M01-Jan         0.815           684          WD0   
1                   SNP     M01-Ja

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0        0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
1        0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
2        0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
3        0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
4        0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
...             ...       ...           ...       ...    ...  ..    ...  ...   
7017835   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
7017836   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
7017837   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
7017838   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   
7017839   WFRC_8219       2.0       12431.0  Arterial    1.0  D2    1.0  3.0   

                    FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPCT  HVPCT  FYEAR  \
0        Principal Arterial    1065  0.6000  DY  1.0000    7.9    5.9   2050   
1        Principal Arterial    1065  0.6000  DY  1.0000    7.9    5.9   2050   
2        Principal Arterial    1065  0.6000  DY  1.0000    7.9    5.9   2050   
3        Principal Arterial    1065  0.6000  DY  1.0000    7.9    5.9   2050   
4        Principal Arterial    1065  0.6000  DY  1.0000    7.9    5.9   2050   
...                     ...     ...     ...  ..     ...    ...    ...    ...   
7017835      Minor Arterial     939  0.5088  EV  0.1946   17.5    7.6   2050   
7017836      Minor Arterial     939  0.5088  EV  0.1946   17.5    7.6   2050   
7017837      Minor Arterial     939  0.5088  EV  0.1946   17.5    7.6   2050   
7017838      Minor Arterial     939  0.5088  EV  0.1946   17.5    7.6   2050   
7017839      Minor Arterial     939  0.5088  EV  0.1946   17.5    7.6   2050   

         ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  DOWFACFC  \
0                2100             2100       1260.00000  Arterial   
1                2100             2100       1260.00000  Arterial   
2                2100             2100       1260.00000  Arterial   
3                2100             2100       1260.00000  Arterial   
4                2100             2100       1260.00000  Arterial   
...               ...              ...              ...       ...   
7017835         13500            13000       1287.16224  Arterial   
7017836         13500            13000       1287.16224  Arterial   
7017837         13500            13000       1287.16224  Arterial   
7017838         13500            13000       1287.16224  Arterial   
7017839         13500            13000       1287.16224  Arterial   

                    SsnGrp    SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
0        StatewideArterial       1-Rural    UTRuralLow         0     2500   
1        StatewideArterial       1-Rural    UTRuralLow         0     2500   
2        StatewideArterial       1-Rural    UTRuralLow         0     2500   
3        StatewideArterial       1-Rural    UTRuralLow         0     2500   
4        StatewideArterial       1-Rural    UTRuralLow         0     2500   
...                    ...           ...           ...       ...      ...   
7017835  StatewideArterial  2-Transition  0-AllVolumes         0  1000000   
7017836  StatewideArterial  2-Transition  0-AllVolumes         0  1000000   
7017837  StatewideArterial  2-Transition  0-AllVolumes         0  1000000   
7017838  StatewideArterial  2-Transition  0-AllVolumes         0  1000000   
7017839  StatewideArterial  2-Transition  0-AllVolumes         0  1000000   

        SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol SiteGroupDOW  \
0                   SNP     M01-Jan         0.815          1026          WD0   
1                   SNP     M01-Jan         0.815          1026          WD0   
2                   SNP     M01-Jan         0.815          1026          WD0   
3                 

In [184]:
#add tod factor

dfs_PrdForecasts_Season_DOW_TOD_wGroups = []

for df_PrdForecasts_Season_DOW in dfs_PrdForecasts_Season_DOW: 
    
    df_PrdForecasts_Season_DOW = df_PrdForecasts_Season_DOW.rename(columns={namePrd: namePrd + '_TDM'})
    #joing forecasts data with season factors
    
    df_TODFactors_Prd = df_TODFactors[df_TODFactors['HrPctOf'] == 'Prd']
    df_TODFactors_DY  = df_TODFactors[df_TODFactors['HrPctOf'] == 'DY']
    
    #get peak Hr as a Pct of Prd
    df_PrdForecasts_Season_DOW_TOD_Prd = pd.DataFrame.merge(df_PrdForecasts_Season_DOW,df_TODFactors_Prd,left_on=('SiteGroupSeason','SeasonGroup','DOWGroup',namePrd+'_TDM'),right_on=('SiteGroupSeason','SeasonGroup','DOWGroup',namePrd))
    
    #get peak Hr as a Pct of DY
    df_PrdForecasts_Season_DOW_TOD_DY = pd.DataFrame.merge(df_PrdForecasts_Season_DOW,df_TODFactors_DY,left_on=('SiteGroupSeason','SeasonGroup','DOWGroup',namePrd+'_TDM'),right_on=('SiteGroupSeason','SeasonGroup','DOWGroup','HrPctOf'))
 
    df_PrdForecasts_Season_DOW_TOD = pd.concat([df_PrdForecasts_Season_DOW_TOD_Prd, df_PrdForecasts_Season_DOW_TOD_DY])

    #display(df_PrdForecasts_Season_DOW_TOD)
    
    #filter by vc groups
    df_PrdForecasts_Season_DOW_TOD_wGroups = pd.DataFrame.merge(df_PrdForecasts_Season_DOW_TOD,df_VCGroups,on=('SeasonGroup','DOWGroup','HrPctOf','Prd'))
    
    dfs_PrdForecasts_Season_DOW_TOD_wGroups.append(df_PrdForecasts_Season_DOW_TOD_wGroups)
    
    display(df_PrdForecasts_Season_DOW_TOD_wGroups)


SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1241.2  Arterial    1.0  D2    1.0  2.0   
2       0006_152.6       1.0        2385.8  Arterial    1.0  D1    1.0  3.0   
3       0006_152.6       1.0        2385.8  Arterial    1.0  D2    1.0  3.0   
4       0038_000.5       1.0        2645.2  Arterial    1.0  D1    2.0  3.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
751123  1084_001.0       1.0         173.6  Arterial    1.0  D2    1.0  5.0   
751124  2865_001.3       2.0        2103.6  Arterial    1.0  D1    1.0  4.0   
751125  2865_001.3       2.0        2103.6  Arterial    1.0  D2    1.0  4.0   
751126  3004_000.9       2.0         100.2  Arterial    1.0  D1    1.0  4.0   
751127  3004_000.9       2.0         100.2  Arterial    1.0  D2    1.0  4.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPCT  \
0          Principal Arterial        1065  0.4916      AM  0.1819    6.5   
1          Principal Arterial        1065  0.5084      AM  0.1819    6.3   
2            Minor Arterial           983  0.7189      AM  0.1693    9.5   
3            Minor Arterial           983  0.2811      AM  0.1693   23.7   
4            Minor Arterial           933  0.4575      AM  0.1746   12.3   
...                           ...     ...     ...     ...     ...    ...   
751123          Collector             578  0.6000      DY  1.0000   11.1   
751124          Collector             785  0.6000      DY  1.0000    1.6   
751125          Collector             785  0.6000      DY  1.0000    1.6   
751126          Collector             785  0.6000      DY  1.0000    6.0   
751127          Collector             785  0.6000      DY  1.0000    6.0   

        HVPCT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0         4.8   2015          1400             1400       125.190856   
1         4.6   2015          1400             1400       129.469144   
2         6.8   2015          2200             2200       267.761494   
3        17.4   2015          2200             2200       104.698506   
4        11.2   2015          2475             2475       197.701763   
...       ...    ...           ...              ...              ...   
751123    5.4   2015           290              290       174.000000   
751124    1.3   2015          2100             2100      1260.000000   
751125    1.3   2015          2100             2100      1260.000000   
751126    2.2   2015          1400             1400       840.000000   
751127    2.2   2015          1400             1400       840.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
751123  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
751124  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
751125  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
751126  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
751127  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815           102   
1          2500             SNP     M01-Jan         0.815           105   
2          2500             SNP     M01-Jan         0.815           218   
3          2500             SNP     M

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1814.0  Arterial    1.0  D2    1.0  2.0   
2       0147_003.1       1.0         861.8  Arterial    1.0  D1    1.0  3.0   
3       0147_003.1       1.0         861.8  Arterial    1.0  D2    1.0  3.0   
4       0147_003.9       1.0         818.1  Arterial    1.0  D1    1.0  3.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
837211  1084_001.0       1.0         634.3  Arterial    1.0  D2    1.0  5.0   
837212  2865_001.3       2.0        3596.7  Arterial    1.0  D1    1.0  4.0   
837213  2865_001.3       2.0        3596.7  Arterial    1.0  D2    1.0  4.0   
837214  3004_000.9       3.0       15605.8  Arterial    1.0  D1    1.0  3.0   
837215  3004_000.9       3.0       15605.8  Arterial    1.0  D2    1.0  3.0   

                   FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPCT  HVPCT  \
0       Principal Arterial    1065  0.5738      AM  0.1884    5.4    3.9   
1       Principal Arterial    1065  0.4262      AM  0.1884    7.2    5.3   
2           Minor Arterial     983  0.5054      AM  0.1401   24.3   35.6   
3           Minor Arterial     983  0.4946      AM  0.1401   22.6   33.8   
4           Minor Arterial     983  0.5108      AM  0.1414   24.2   35.5   
...                    ...     ...     ...     ...     ...    ...    ...   
837211           Collector     572  0.6000      DY  1.0000   21.8   19.2   
837212           Collector     785  0.6000      DY  1.0000    1.7    1.6   
837213           Collector     785  0.6000      DY  1.0000    1.7    1.6   
837214      Minor Arterial     894  0.6000      DY  1.0000   19.1    7.0   
837215      Minor Arterial     894  0.6000      DY  1.0000   15.2    5.7   

        FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  DOWFACFC  \
0        2050          2100             2100       227.018232  Arterial   
1        2050          2100             2100       168.621768  Arterial   
2        2050          1200             1200        84.967848  Arterial   
3        2050          1200             1200        83.152152  Arterial   
4        2050          1500             1500       108.340680  Arterial   
...       ...           ...              ...              ...       ...   
837211   2050           800              800       480.000000  Arterial   
837212   2050          3800             3800      2280.000000  Arterial   
837213   2050          3800             3800      2280.000000  Arterial   
837214   2050         35500            35000     21000.000000  Arterial   
837215   2050         35500            35000     21000.000000  Arterial   

                   SsnGrp      SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
0       StatewideArterial         1-Rural    UTRuralLow         0     2500   
1       StatewideArterial         1-Rural    UTRuralLow         0     2500   
2       StatewideArterial         1-Rural    UTRuralLow         0     2500   
3       StatewideArterial         1-Rural    UTRuralLow         0     2500   
4       StatewideArterial         1-Rural    UTRuralLow         0     2500   
...                   ...             ...           ...       ...      ...   
837211     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837212     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837213     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837214     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837215     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   

       SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol SiteGroupDOW  \
0                  SNP     M01-Jan         0.815           185          WD0   
1                  SNP     M01-Jan         0.815           137          WD0   
2                  SNP     M01-Jan         0.815            69          WD0 

In [185]:
#df_PrdForecasts_Season_DOW_TOD_DY[(df_PrdForecasts_Season_DOW_TOD_DY['SEGID']=='0006_146.9') & (df_PrdForecasts_Season_DOW_TOD_DY['DOWGroup']=='6-Saturday')].head(20)

In [186]:
#df_PrdForecasts_Season_DOW_TOD[df_PrdForecasts_Season_DOW_TOD['SEGID']=='0006_146.9'].head(20)

In [187]:
#dftemp = dfs_PrdForecasts_Season_DOW_TOD_wGroups[0].groupby(['VCGroupCode']).agg({'VolMaxHrPct':[np.size]})
df_TODFactors_DY[df_TODFactors_DY['SeasonGroup']=='S00-Ann']

SiteGroupSeason SeasonGroup    DOWGroup Prd HrPctOf  VolPkHrPct
25020             SN0     S00-Ann    1-Monday  AM      DY      0.0386
25021             SN0     S00-Ann    1-Monday  DY      DY      0.1144
25022             SN0     S00-Ann    1-Monday  EV      DY      0.0969
25023             SN0     S00-Ann    1-Monday  MD      DY      0.0769
25024             SN0     S00-Ann    1-Monday  PM      DY      0.0926
...               ...         ...         ...  ..     ...         ...
57955             XX4     S00-Ann  W2-Weekend  AM      DY      0.0608
57956             XX4     S00-Ann  W2-Weekend  DY      DY      0.0872
57957             XX4     S00-Ann  W2-Weekend  EV      DY      0.0617
57958             XX4     S00-Ann  W2-Weekend  MD      DY      0.0658
57959             XX4     S00-Ann  W2-Weekend  PM      DY      0.0867

[1710 rows x 6 columns]

In [188]:
dfs_PkHrForecasts = []

for df_PrdForecasts_Season_DOW_TOD_wGroups in dfs_PrdForecasts_Season_DOW_TOD_wGroups: 
    
    df_PkHrForecasts = pd.DataFrame.merge(df_PrdForecasts_Season_DOW_TOD_wGroups,df_PrdDuration,on='Prd',how='left')   
    
    df_PkHrForecasts['AvgSsnDOWPkHrVol'] = df_PkHrForecasts['AvgSsnDOWPrdVol'] * df_PkHrForecasts['VolPkHrPct']

    #add truck Pctage adjustments
    #PCE for medium and heavy trucks from HCM 2000 Exhibit 23-8
    Emd = 1.2 #same as RVs
    Ehv = 1.5
    df_PkHrForecasts['TrkFac'] = 1 + (df_PkHrForecasts[nameMDPct]/100 * (Emd-1)) + (df_PkHrForecasts[nameHVPct]/100 * (Ehv-1))
    
    #calculate PCE
    df_PkHrForecasts['PrdPCEFlow' ] = (df_PkHrForecasts['AvgSsnDOWPrdVol' ] *  df_PkHrForecasts['TrkFac']) /  df_PkHrForecasts['PrdHrs']
    df_PkHrForecasts['PkHrPCEFlow'] =  df_PkHrForecasts['AvgSsnDOWPkHrVol'] *  df_PkHrForecasts['TrkFac']
    df_PkHrForecasts['PrdVC'      ] =  df_PkHrForecasts['PrdPCEFlow'      ] / (df_PkHrForecasts[nameCap1HL] * df_PkHrForecasts[nameLanes])
    df_PkHrForecasts['PkHrVC'     ] =  df_PkHrForecasts['PkHrPCEFlow'     ] / (df_PkHrForecasts[nameCap1HL] * df_PkHrForecasts[nameLanes])
    
    display(df_PkHrForecasts)
    
    dfs_PkHrForecasts.append(df_PkHrForecasts)

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1241.2  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1241.2  Arterial    1.0  D2    1.0  2.0   
2       0006_152.6       1.0        2385.8  Arterial    1.0  D1    1.0  3.0   
3       0006_152.6       1.0        2385.8  Arterial    1.0  D2    1.0  3.0   
4       0038_000.5       1.0        2645.2  Arterial    1.0  D1    2.0  3.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
751123  1084_001.0       1.0         173.6  Arterial    1.0  D2    1.0  5.0   
751124  2865_001.3       2.0        2103.6  Arterial    1.0  D1    1.0  4.0   
751125  2865_001.3       2.0        2103.6  Arterial    1.0  D2    1.0  4.0   
751126  3004_000.9       2.0         100.2  Arterial    1.0  D1    1.0  4.0   
751127  3004_000.9       2.0         100.2  Arterial    1.0  D2    1.0  4.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPCT  \
0          Principal Arterial        1065  0.4916      AM  0.1819    6.5   
1          Principal Arterial        1065  0.5084      AM  0.1819    6.3   
2            Minor Arterial           983  0.7189      AM  0.1693    9.5   
3            Minor Arterial           983  0.2811      AM  0.1693   23.7   
4            Minor Arterial           933  0.4575      AM  0.1746   12.3   
...                           ...     ...     ...     ...     ...    ...   
751123          Collector             578  0.6000      DY  1.0000   11.1   
751124          Collector             785  0.6000      DY  1.0000    1.6   
751125          Collector             785  0.6000      DY  1.0000    1.6   
751126          Collector             785  0.6000      DY  1.0000    6.0   
751127          Collector             785  0.6000      DY  1.0000    6.0   

        HVPCT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0         4.8   2015          1400             1400       125.190856   
1         4.6   2015          1400             1400       129.469144   
2         6.8   2015          2200             2200       267.761494   
3        17.4   2015          2200             2200       104.698506   
4        11.2   2015          2475             2475       197.701763   
...       ...    ...           ...              ...              ...   
751123    5.4   2015           290              290       174.000000   
751124    1.3   2015          2100             2100      1260.000000   
751125    1.3   2015          2100             2100      1260.000000   
751126    2.2   2015          1400             1400       840.000000   
751127    2.2   2015          1400             1400       840.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
751123  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
751124  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
751125  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
751126  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
751127  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815           102   
1          2500             SNP     M01-Jan         0.815           105   
2          2500             SNP     M01-Jan         0.815           218   
3          2500             SNP     M

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1814.0  Arterial    1.0  D2    1.0  2.0   
2       0147_003.1       1.0         861.8  Arterial    1.0  D1    1.0  3.0   
3       0147_003.1       1.0         861.8  Arterial    1.0  D2    1.0  3.0   
4       0147_003.9       1.0         818.1  Arterial    1.0  D1    1.0  3.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
837211  1084_001.0       1.0         634.3  Arterial    1.0  D2    1.0  5.0   
837212  2865_001.3       2.0        3596.7  Arterial    1.0  D1    1.0  4.0   
837213  2865_001.3       2.0        3596.7  Arterial    1.0  D2    1.0  4.0   
837214  3004_000.9       3.0       15605.8  Arterial    1.0  D1    1.0  3.0   
837215  3004_000.9       3.0       15605.8  Arterial    1.0  D2    1.0  3.0   

                   FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPCT  HVPCT  \
0       Principal Arterial    1065  0.5738      AM  0.1884    5.4    3.9   
1       Principal Arterial    1065  0.4262      AM  0.1884    7.2    5.3   
2           Minor Arterial     983  0.5054      AM  0.1401   24.3   35.6   
3           Minor Arterial     983  0.4946      AM  0.1401   22.6   33.8   
4           Minor Arterial     983  0.5108      AM  0.1414   24.2   35.5   
...                    ...     ...     ...     ...     ...    ...    ...   
837211           Collector     572  0.6000      DY  1.0000   21.8   19.2   
837212           Collector     785  0.6000      DY  1.0000    1.7    1.6   
837213           Collector     785  0.6000      DY  1.0000    1.7    1.6   
837214      Minor Arterial     894  0.6000      DY  1.0000   19.1    7.0   
837215      Minor Arterial     894  0.6000      DY  1.0000   15.2    5.7   

        FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  DOWFACFC  \
0        2050          2100             2100       227.018232  Arterial   
1        2050          2100             2100       168.621768  Arterial   
2        2050          1200             1200        84.967848  Arterial   
3        2050          1200             1200        83.152152  Arterial   
4        2050          1500             1500       108.340680  Arterial   
...       ...           ...              ...              ...       ...   
837211   2050           800              800       480.000000  Arterial   
837212   2050          3800             3800      2280.000000  Arterial   
837213   2050          3800             3800      2280.000000  Arterial   
837214   2050         35500            35000     21000.000000  Arterial   
837215   2050         35500            35000     21000.000000  Arterial   

                   SsnGrp      SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
0       StatewideArterial         1-Rural    UTRuralLow         0     2500   
1       StatewideArterial         1-Rural    UTRuralLow         0     2500   
2       StatewideArterial         1-Rural    UTRuralLow         0     2500   
3       StatewideArterial         1-Rural    UTRuralLow         0     2500   
4       StatewideArterial         1-Rural    UTRuralLow         0     2500   
...                   ...             ...           ...       ...      ...   
837211     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837212     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837213     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837214     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837215     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   

       SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol SiteGroupDOW  \
0                  SNP     M01-Jan         0.815           185          WD0   
1                  SNP     M01-Jan         0.815           137          WD0   
2                  SNP     M01-Jan         0.815            69          WD0 

In [189]:
df_PkHrForecasts.columns

Index(['SEGID', 'AREATYPE', 'SegDYVol_TDM', 'FUNCGROUP', 'FGFAC', 'Dir',
       'LANES', 'FT', 'FTCLASS', 'CAP1HL', 'DFAC', 'Prd_TDM', 'PRDFAC',
       'MDPCT', 'HVPCT', 'FYEAR', 'ForecastAADT', 'ForecastAADTAdj',
       'AvgAnnualPrdVol', 'DOWFACFC', 'SsnGrp', 'SsnATGroup', 'SsnVolCls',
       'Vol_From', 'Vol_To', 'SiteGroupSeason', 'SeasonGroup', 'SeasonFactor',
       'AvgSsnPrdVol', 'SiteGroupDOW', 'DOWGroup', 'DOWFactor',
       'AvgSsnDOWPrdVol', 'Prd', 'HrPctOf', 'VolPkHrPct', 'SeasonType',
       'VCGroupCode', 'PrdHrs', 'AvgSsnDOWPkHrVol', 'TrkFac', 'PrdPCEFlow',
       'PkHrPCEFlow', 'PrdVC', 'PkHrVC'],
      dtype='object')

In [190]:
df_PkHrForecasts[df_PkHrForecasts['SeasonGroup']=='S00-Ann']

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
131328  0006_146.9       1.0        1814.0  Arterial    1.0  D1    1.0  2.0   
131329  0006_146.9       1.0        1814.0  Arterial    1.0  D2    1.0  2.0   
131330  0147_003.1       1.0         861.8  Arterial    1.0  D1    1.0  3.0   
131331  0147_003.1       1.0         861.8  Arterial    1.0  D2    1.0  3.0   
131332  0147_003.9       1.0         818.1  Arterial    1.0  D1    1.0  3.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
837211  1084_001.0       1.0         634.3  Arterial    1.0  D2    1.0  5.0   
837212  2865_001.3       2.0        3596.7  Arterial    1.0  D1    1.0  4.0   
837213  2865_001.3       2.0        3596.7  Arterial    1.0  D2    1.0  4.0   
837214  3004_000.9       3.0       15605.8  Arterial    1.0  D1    1.0  3.0   
837215  3004_000.9       3.0       15605.8  Arterial    1.0  D2    1.0  3.0   

                   FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPCT  HVPCT  \
131328  Principal Arterial    1065  0.5738      AM  0.1884    5.4    3.9   
131329  Principal Arterial    1065  0.4262      AM  0.1884    7.2    5.3   
131330      Minor Arterial     983  0.5054      AM  0.1401   24.3   35.6   
131331      Minor Arterial     983  0.4946      AM  0.1401   22.6   33.8   
131332      Minor Arterial     983  0.5108      AM  0.1414   24.2   35.5   
...                    ...     ...     ...     ...     ...    ...    ...   
837211           Collector     572  0.6000      DY  1.0000   21.8   19.2   
837212           Collector     785  0.6000      DY  1.0000    1.7    1.6   
837213           Collector     785  0.6000      DY  1.0000    1.7    1.6   
837214      Minor Arterial     894  0.6000      DY  1.0000   19.1    7.0   
837215      Minor Arterial     894  0.6000      DY  1.0000   15.2    5.7   

        FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  DOWFACFC  \
131328   2050          2100             2100       227.018232  Arterial   
131329   2050          2100             2100       168.621768  Arterial   
131330   2050          1200             1200        84.967848  Arterial   
131331   2050          1200             1200        83.152152  Arterial   
131332   2050          1500             1500       108.340680  Arterial   
...       ...           ...              ...              ...       ...   
837211   2050           800              800       480.000000  Arterial   
837212   2050          3800             3800      2280.000000  Arterial   
837213   2050          3800             3800      2280.000000  Arterial   
837214   2050         35500            35000     21000.000000  Arterial   
837215   2050         35500            35000     21000.000000  Arterial   

                   SsnGrp      SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
131328  StatewideArterial         1-Rural    UTRuralLow         0     2500   
131329  StatewideArterial         1-Rural    UTRuralLow         0     2500   
131330  StatewideArterial         1-Rural    UTRuralLow         0     2500   
131331  StatewideArterial         1-Rural    UTRuralLow         0     2500   
131332  StatewideArterial         1-Rural    UTRuralLow         0     2500   
...                   ...             ...           ...       ...      ...   
837211     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837212     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837213     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837214     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837215     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   

       SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol SiteGroupDOW  \
131328             SNP     S00-Ann           1.0           227          WD0   
131329             SNP     S00-Ann           1.0           168          WD0   
131330             SNP     S00-Ann           1.0            84          WD0 

In [191]:
#15-Min Analysis

dfs_VC = []

for df_PkHrForecasts in dfs_PkHrForecasts:

    df_VC = df_PkHrForecasts
    
    #PHF conditions (from Chad's spreadsheet for Urban (0.92,0.95,0.97,0.98). HCM2000 Exhibit 9.2 says default PHF for Urban Areas is 0.92, Rural is 0.88. Rural estimated at (0.88,0.91,0.93,0.95)
    conditions = [
        (df_VC[nameAT] >= 3) & (df_VC['PkHrVC'] <= 0.85),
        (df_VC[nameAT] >= 3) & (df_VC['PkHrVC'] >  0.85) & (df_VC['PkHrVC'] <= 0.95),
        (df_VC[nameAT] >= 3) & (df_VC['PkHrVC'] >  0.95) & (df_VC['PkHrVC'] <= 1.00),
        (df_VC[nameAT] >= 3) & (df_VC['PkHrVC'] >  1.00),
        (df_VC[nameAT] <= 2) & (df_VC['PkHrVC'] <= 0.85),
        (df_VC[nameAT] <= 2) & (df_VC['PkHrVC'] >  0.85) & (df_VC['PkHrVC'] <= 0.95),
        (df_VC[nameAT] <= 2) & (df_VC['PkHrVC'] >  0.95) & (df_VC['PkHrVC'] <= 1.00),
        (df_VC[nameAT] <= 2) & (df_VC['PkHrVC'] >  1.00)
    ]
    choices = [0.92,0.95,0.97,0.98,0.88,0.91,0.93,0.95]

    df_VC['PHF'] = np.select(conditions, choices, default=0)


    #15-min volume and v/c calcs
    df_VC['Pk15PCEFlow'] = df_VC['PkHrPCEFlow']  / df_VC['PHF']
    df_VC['Pk15VC'     ] = df_VC['Pk15PCEFlow'] / (df_VC[nameCap1HL] * df_VC[nameLanes])

    #effective K-factor
    #df_VC['kFactor_effective']  = df_VC['ForecastPkHr']  / df_VC['ForecastAADT']

    #convert to int and round columns after calcs
    df_VC = df_VC.fillna(0)
    df_VC['AREATYPE'       ] = df_VC['AREATYPE'       ].astype(int)
    df_VC['FT'             ] = df_VC['FT'             ].astype(int)
    df_VC['LANES'          ] = df_VC['LANES'          ].astype(int)
    df_VC['ForecastAADT'   ] = df_VC['ForecastAADT'   ].astype(int)
    df_VC['ForecastAADTAdj'] = df_VC['ForecastAADTAdj'].astype(int)
    df_VC['PrdPCEFlow'     ] = df_VC['PrdPCEFlow'     ].astype(int)
    df_VC['PkHrPCEFlow'    ] = df_VC['PkHrPCEFlow'    ].astype(int)
    df_VC['Pk15PCEFlow'    ] = df_VC['Pk15PCEFlow'    ].astype(int)
    df_VC = df_VC.round({'SeasonFactor':2,'DOWFactor':2,'PrdVC':2,'PkHrVC':2,'Pk15VC':2,nameMDPct:2,nameHVPct:2,'VolMaxHrPct':2,'FactorTrucks':2})
    
    pd.set_option('display.max_columns', None)
    
    display(df_VC)
    
    dfs_VC.append(df_VC)
    

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES  FT  \
0       0006_146.9         1        1241.2  Arterial    1.0  D1      1   2   
1       0006_146.9         1        1241.2  Arterial    1.0  D2      1   2   
2       0006_152.6         1        2385.8  Arterial    1.0  D1      1   3   
3       0006_152.6         1        2385.8  Arterial    1.0  D2      1   3   
4       0038_000.5         1        2645.2  Arterial    1.0  D1      2   3   
...            ...       ...           ...       ...    ...  ..    ...  ..   
751123  1084_001.0         1         173.6  Arterial    1.0  D2      1   5   
751124  2865_001.3         2        2103.6  Arterial    1.0  D1      1   4   
751125  2865_001.3         2        2103.6  Arterial    1.0  D2      1   4   
751126  3004_000.9         2         100.2  Arterial    1.0  D1      1   4   
751127  3004_000.9         2         100.2  Arterial    1.0  D2      1   4   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPCT  \
0          Principal Arterial        1065  0.4916      AM  0.1819    6.5   
1          Principal Arterial        1065  0.5084      AM  0.1819    6.3   
2            Minor Arterial           983  0.7189      AM  0.1693    9.5   
3            Minor Arterial           983  0.2811      AM  0.1693   23.7   
4            Minor Arterial           933  0.4575      AM  0.1746   12.3   
...                           ...     ...     ...     ...     ...    ...   
751123          Collector             578  0.6000      DY  1.0000   11.1   
751124          Collector             785  0.6000      DY  1.0000    1.6   
751125          Collector             785  0.6000      DY  1.0000    1.6   
751126          Collector             785  0.6000      DY  1.0000    6.0   
751127          Collector             785  0.6000      DY  1.0000    6.0   

        HVPCT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0         4.8   2015          1400             1400       125.190856   
1         4.6   2015          1400             1400       129.469144   
2         6.8   2015          2200             2200       267.761494   
3        17.4   2015          2200             2200       104.698506   
4        11.2   2015          2475             2475       197.701763   
...       ...    ...           ...              ...              ...   
751123    5.4   2015           290              290       174.000000   
751124    1.3   2015          2100             2100      1260.000000   
751125    1.3   2015          2100             2100      1260.000000   
751126    2.2   2015          1400             1400       840.000000   
751127    2.2   2015          1400             1400       840.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
751123  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
751124  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
751125  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
751126  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
751127  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan          0.82           102   
1          2500             SNP     M01-Jan          0.82           105   
2          2500             SNP     M01-Jan          0.82           218   
3          2500             SNP     M01-Jan      

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES  FT  \
0       0006_146.9         1        1814.0  Arterial    1.0  D1      1   2   
1       0006_146.9         1        1814.0  Arterial    1.0  D2      1   2   
2       0147_003.1         1         861.8  Arterial    1.0  D1      1   3   
3       0147_003.1         1         861.8  Arterial    1.0  D2      1   3   
4       0147_003.9         1         818.1  Arterial    1.0  D1      1   3   
...            ...       ...           ...       ...    ...  ..    ...  ..   
837211  1084_001.0         1         634.3  Arterial    1.0  D2      1   5   
837212  2865_001.3         2        3596.7  Arterial    1.0  D1      1   4   
837213  2865_001.3         2        3596.7  Arterial    1.0  D2      1   4   
837214  3004_000.9         3       15605.8  Arterial    1.0  D1      1   3   
837215  3004_000.9         3       15605.8  Arterial    1.0  D2      1   3   

                   FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPCT  HVPCT  \
0       Principal Arterial    1065  0.5738      AM  0.1884    5.4    3.9   
1       Principal Arterial    1065  0.4262      AM  0.1884    7.2    5.3   
2           Minor Arterial     983  0.5054      AM  0.1401   24.3   35.6   
3           Minor Arterial     983  0.4946      AM  0.1401   22.6   33.8   
4           Minor Arterial     983  0.5108      AM  0.1414   24.2   35.5   
...                    ...     ...     ...     ...     ...    ...    ...   
837211           Collector     572  0.6000      DY  1.0000   21.8   19.2   
837212           Collector     785  0.6000      DY  1.0000    1.7    1.6   
837213           Collector     785  0.6000      DY  1.0000    1.7    1.6   
837214      Minor Arterial     894  0.6000      DY  1.0000   19.1    7.0   
837215      Minor Arterial     894  0.6000      DY  1.0000   15.2    5.7   

        FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  DOWFACFC  \
0        2050          2100             2100       227.018232  Arterial   
1        2050          2100             2100       168.621768  Arterial   
2        2050          1200             1200        84.967848  Arterial   
3        2050          1200             1200        83.152152  Arterial   
4        2050          1500             1500       108.340680  Arterial   
...       ...           ...              ...              ...       ...   
837211   2050           800              800       480.000000  Arterial   
837212   2050          3800             3800      2280.000000  Arterial   
837213   2050          3800             3800      2280.000000  Arterial   
837214   2050         35500            35000     21000.000000  Arterial   
837215   2050         35500            35000     21000.000000  Arterial   

                   SsnGrp      SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
0       StatewideArterial         1-Rural    UTRuralLow         0     2500   
1       StatewideArterial         1-Rural    UTRuralLow         0     2500   
2       StatewideArterial         1-Rural    UTRuralLow         0     2500   
3       StatewideArterial         1-Rural    UTRuralLow         0     2500   
4       StatewideArterial         1-Rural    UTRuralLow         0     2500   
...                   ...             ...           ...       ...      ...   
837211     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837212     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837213     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837214     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   
837215     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0  1000000   

       SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol SiteGroupDOW  \
0                  SNP     M01-Jan          0.82           185          WD0   
1                  SNP     M01-Jan          0.82           137          WD0   
2                  SNP     M01-Jan          0.82            69          WD0   
3        

In [192]:
df = dfs_VC[0]

df = df[(df[nameSegID]=='0015_282.2') * (df['VCGroupCode']=='AnnWkPM')]

df

C:\Program Files\ArcGIS\Pro\bin\Python\envs\arcgispro-py3\lib\site-packages\pandas\core\computation\expressions.py:178: UserWarning: evaluating in Python space because the '*' operator is not supported by numexpr for the bool dtype, use '&' instead
  f"evaluating in Python space because the {repr(op_str)} "


SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP   FGFAC Dir  LANES  FT  \
369570  0015_282.2         3      129585.4  Arterial  0.0043  D1      1   4   
369571  0015_282.2         3      129585.4  Arterial  0.0043  D2      1   4   
372756  0015_282.2         3      129585.4   Freeway  0.9028  D1      3  33   
372757  0015_282.2         3      129585.4   Freeway  0.9028  D2      3  33   
372758  0015_282.2         3      129585.4   Managed  0.0929  D1      1  38   
372759  0015_282.2         3      129585.4   Managed  0.0929  D2      1  38   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPCT  \
369570          Collector             748  0.2968      PM  0.4643   16.9   
369571          Collector             748  0.7032      PM  0.4643   14.6   
372756           Freeway             1730  0.4486      PM  0.2347   12.9   
372757           Freeway             1730  0.5514      PM  0.2347    9.9   
372758           Freeway             1767  0.4098      PM  0.3171    0.0   
372759           Freeway             1767  0.5902      PM  0.3171    0.0   

        HVPCT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
369570    7.2   2015        159000           159000        94.216759   
369571    6.5   2015        159000           159000       223.225151   
372756    5.8   2015        159000           159000     15113.360216   
372757    4.5   2015        159000           159000     18576.698224   
372758    0.0   2015        159000           159000      1919.468699   
372759    0.0   2015        159000           159000      2764.447111   

          DOWFACFC      SsnGrp  SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
369570  FreewayI15  FreewayI15  3-Suburban  0-AllVolumes         0  1000000   
369571  FreewayI15  FreewayI15  3-Suburban  0-AllVolumes         0  1000000   
372756  FreewayI15  FreewayI15  3-Suburban  0-AllVolumes         0  1000000   
372757  FreewayI15  FreewayI15  3-Suburban  0-AllVolumes         0  1000000   
372758  FreewayI15  FreewayI15  3-Suburban  0-AllVolumes         0  1000000   
372759  FreewayI15  FreewayI15  3-Suburban  0-AllVolumes         0  1000000   

       SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol SiteGroupDOW  \
369570             SNT     S00-Ann           1.0            94          WD2   
369571             SNT     S00-Ann           1.0           223          WD2   
372756             SN6     S00-Ann           1.0         15113          WDA   
372757             SN6     S00-Ann           1.0         18576          WDA   
372758             SN6     S00-Ann           1.0          1919          WDA   
372759             SN6     S00-Ann           1.0          2764          WDA   

          DOWGroup  DOWFactor  AvgSsnDOWPrdVol Prd HrPctOf  VolPkHrPct  \
369570  W1-Weekday       1.12              105  PM     Prd      0.3721   
369571  W1-Weekday       1.12              249  PM     Prd      0.3721   
372756  W1-Weekday       1.06            15974  PM     Prd      0.3577   
372757  W1-Weekday       1.06            19634  PM     Prd      0.3577   
372758  W1-Weekday       1.06             2028  PM     Prd      0.3577   
372759  W1-Weekday       1.06             2921  PM     Prd      0.3577   

       SeasonType VCGroupCode  PrdHrs  AvgSsnDOWPkHrVol  TrkFac  PrdPCEFlow  \
369570     Season     AnnWkPM       3           39.0705  1.0698          37   
369571     Season     AnnWkPM       3           92.6529  1.0617          88   
372756     Season     AnnWkPM       3         5713.8998  1.0548        5616   
372757     Season     AnnWkPM       3         7023.0818  1.0423        6821   
372758     Season     AnnWkPM       3          725.4156  1.0000         676   
372759     Season     AnnWkPM       3         1044.8417  1.0000         973   

        PkHrPCEFlow  PrdVC  PkHrVC   PHF  Pk15PCEFlow  Pk15VC  
369570           41   0.05    0.06  0.92           45    0.06  
369571           98   0.12    0.13  0.92          106    0.14  
372756         6027   1.08    1.16  0.98        

In [193]:
df_VC.columns

Index(['SEGID', 'AREATYPE', 'SegDYVol_TDM', 'FUNCGROUP', 'FGFAC', 'Dir',
       'LANES', 'FT', 'FTCLASS', 'CAP1HL', 'DFAC', 'Prd_TDM', 'PRDFAC',
       'MDPCT', 'HVPCT', 'FYEAR', 'ForecastAADT', 'ForecastAADTAdj',
       'AvgAnnualPrdVol', 'DOWFACFC', 'SsnGrp', 'SsnATGroup', 'SsnVolCls',
       'Vol_From', 'Vol_To', 'SiteGroupSeason', 'SeasonGroup', 'SeasonFactor',
       'AvgSsnPrdVol', 'SiteGroupDOW', 'DOWGroup', 'DOWFactor',
       'AvgSsnDOWPrdVol', 'Prd', 'HrPctOf', 'VolPkHrPct', 'SeasonType',
       'VCGroupCode', 'PrdHrs', 'AvgSsnDOWPkHrVol', 'TrkFac', 'PrdPCEFlow',
       'PkHrPCEFlow', 'PrdVC', 'PkHrVC', 'PHF', 'Pk15PCEFlow', 'Pk15VC'],
      dtype='object')

In [194]:
dfs_VC_MaxDirFG = []

for df_VC in dfs_VC:

    df_VC_MaxDirFG = df_VC.groupby([nameSegID,namePrd,'SeasonGroup','DOWGroup','HrPctOf','VCGroupCode'], as_index=False).agg({nameDir:[np.size],nameCap1HL:[np.sum],'PrdPCEFlow':[np.sum],'PkHrPCEFlow':[np.sum],'Pk15PCEFlow':[np.sum],'PrdVC':[np.max],'PkHrVC':[np.max],'Pk15VC':[np.max]})

    df_VC_MaxDirFG.columns = ([nameSegID,namePrd,'SeasonGroup','DOWGroup','HrPctOf','VCGroupCode','numRecords',nameCap1HL+'Sum','PrdPCEFlowSum','PkHrPCEFlowSum','Pk15PCEFlowSum','PrdVCMax','PkHrVCMax','Pk15VCMax'])
    
    dfs_VC_MaxDirFG.append(df_VC_MaxDirFG)
    
    display(df_VC_MaxDirFG)
                                            
    #df_Peak_VC_wGroups = pd.DataFrame.merge(df_VCGroups,df_Peak_VC,on=('SeasonGroup','DOWGroup','Prd','HrPctOf'))

SEGID Prd SeasonGroup    DOWGroup HrPctOf VCGroupCode  \
0       0006_146.9  AM     M01-Jan  W1-Weekday     Prd     JanWkAM   
1       0006_146.9  AM     M02-Feb  W1-Weekday     Prd     FebWkAM   
2       0006_146.9  AM     M03-Mar  W1-Weekday     Prd     MarWkAM   
3       0006_146.9  AM     M04-Apr  W1-Weekday     Prd     AprWkAM   
4       0006_146.9  AM     M05-May  W1-Weekday     Prd     MayWkAM   
...            ...  ..         ...         ...     ...         ...   
365359   WFRC_8218  PM     S02-Spr  W1-Weekday     Prd     SprWkPM   
365360   WFRC_8218  PM     S03-Sum    5-Friday      DY     SumFrPM   
365361   WFRC_8218  PM     S03-Sum  W1-Weekday     Prd     SumWkPM   
365362   WFRC_8218  PM     S04-Fal    5-Friday      DY     FalFrPM   
365363   WFRC_8218  PM     S04-Fal  W1-Weekday     Prd     FalWkPM   

        numRecords  CAP1HLSum  PrdPCEFlowSum  PkHrPCEFlowSum  Pk15PCEFlowSum  \
0                2       2130             65              81              93   
1                2       2130             69              87              98   
2                2       2130             77              94             108   
3                2       2130             83             103             117   
4                2       2130             87             108             122   
...            ...        ...            ...             ...             ...   
365359           2       2946              0               0               0   
365360           2       2946              0               0               0   
365361           2       2946              0               0               0   
365362           2       2946              0               0               0   
365363           2       2946              0               0               0   

        PrdVCMax  PkHrVCMax  Pk15VCMax  
0           0.03       0.04       0.04  
1           0.03       0.04       0.05  
2           0.04       0.05       0.05  
3           0.04       0.05       0.06  
4           0.04       0.05       0.06  
...          ...        ...        ...  
365359      0.00       0.00       0.00  
365360      0.00       0.00       0.00  
365361      0.00       0.00       0.00  
365362      0.00       0.00       0.00  
365363      0.00       0.00       0.00  

[365364 rows x 14 columns]

SEGID Prd SeasonGroup    DOWGroup HrPctOf VCGroupCode  \
0       0006_146.9  AM     M01-Jan  W1-Weekday     Prd     JanWkAM   
1       0006_146.9  AM     M02-Feb  W1-Weekday     Prd     FebWkAM   
2       0006_146.9  AM     M03-Mar  W1-Weekday     Prd     MarWkAM   
3       0006_146.9  AM     M04-Apr  W1-Weekday     Prd     AprWkAM   
4       0006_146.9  AM     M05-May  W1-Weekday     Prd     MayWkAM   
...            ...  ..         ...         ...     ...         ...   
396571   WFRC_8219  PM     S02-Spr  W1-Weekday     Prd     SprWkPM   
396572   WFRC_8219  PM     S03-Sum    5-Friday      DY     SumFrPM   
396573   WFRC_8219  PM     S03-Sum  W1-Weekday     Prd     SumWkPM   
396574   WFRC_8219  PM     S04-Fal    5-Friday      DY     FalFrPM   
396575   WFRC_8219  PM     S04-Fal  W1-Weekday     Prd     FalWkPM   

        numRecords  CAP1HLSum  PrdPCEFlowSum  PkHrPCEFlowSum  Pk15PCEFlowSum  \
0                2       2130            103             128             145   
1                2       2130            109             135             154   
2                2       2130            121             149             169   
3                2       2130            129             161             183   
4                2       2130            136             167             190   
...            ...        ...            ...             ...             ...   
396571           2       1878           1519            1731            1881   
396572           2       1878           6724            1800            1936   
396573           2       1878           1579            1831            1967   
396574           2       1878           6502            1806            1942   
396575           2       1878           1527            1747            1898   

        PrdVCMax  PkHrVCMax  Pk15VCMax  
0           0.06       0.07       0.08  
1           0.06       0.07       0.08  
2           0.06       0.08       0.09  
3           0.07       0.09       0.10  
4           0.07       0.09       0.10  
...          ...        ...        ...  
396571      0.85       0.97       1.04  
396572      3.58       0.96       1.03  
396573      0.88       1.02       1.08  
396574      3.46       0.96       1.03  
396575      0.85       0.98       1.05  

[396576 rows x 14 columns]

In [195]:
display(df_Scenarios)

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
0              Yes       Base15          Base      2015 Base          2015   
1               No       Base19          Base      2019 Base          2019   
2               No        TIP24           TIP       2024 TIP          2024   
3               No        RTP30           RTP       2030 RTP          2030   
4               No        RTP40           RTP       2040 RTP          2040   
5               No        RTP50           RTP       2050 RTP          2050   
6               No         NB30      No Build  2030 No Build          2030   
7               No         NB40      No Build  2040 No Build          2040   
8               No         NB50      No Build  2050 No Build          2050   
9               No         UF30         Needs     2030 Needs          2030   
10              No         UF40         Needs     2040 Needs          2040   
11              No         UF50         Needs     2050 Needs          2050   
12             Yes         S550      Scenario  2050 S5 Draft          2050   

                                                SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                      
0                  v831_SE15_Net15_Summary_SEGID_Detailed.csv             NaN   
1                  v831_SE19_Net19_Summary_SEGID_Detailed.csv          Base15   
2                  v831_SE24_Net24_Summary_SEGID_Detailed.csv          Base19   
3                  v831_SE30_Net30_Summary_SEGID_Detailed.csv           TIP24   
4                  v831_SE40_Net40_Summary_SEGID_Detailed.csv           RTP30   
5                  v831_SE50_Net50_Summary_SEGID_Detailed.csv           RTP40   
6                  v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
7                  v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
8                  v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
9                v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
10               v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
11               v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   
12          v831_SE50_Net50_Summary_SEGID_Detailed_S5Draft...             NaN   

           AdjScenarioCode  
ScenarioID                  
0                      NaN  
1                      NaN  
2                      NaN  
3                      NaN  
4                      NaN  
5                      NaN  
6                    RTP30  
7                    RTP40  
8                    RTP50  
9                    RTP30  
10                   RTP40  
11                   RTP50  
12                   RTP50

In [196]:
df = dfs_VC[0]

df = df[(df[nameSegID]=='0015_295.6') * (df['VCGroupCode']=='AnnWkPM')]

display(df)

df = dfs_VC_MaxDirFG[0]

df = df[(df[nameSegID]=='0015_295.6')]

pd.set_option('display.max_columns', None)

display(df)

C:\Program Files\ArcGIS\Pro\bin\Python\envs\arcgispro-py3\lib\site-packages\pandas\core\computation\expressions.py:178: UserWarning: evaluating in Python space because the '*' operator is not supported by numexpr for the bool dtype, use '&' instead
  f"evaluating in Python space because the {repr(op_str)} "


SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP   FGFAC Dir  LANES  FT  \
372904  0015_295.6         4      320541.3   Freeway  0.6738  D1      4  34   
372905  0015_295.6         4      320541.3   Freeway  0.6738  D2      4  34   
372906  0015_295.6         4      320541.3   Managed  0.0635  D1      1  38   
372907  0015_295.6         4      320541.3   Managed  0.0635  D2      1  38   
372908  0015_295.6         4      320541.3   CD Road  0.2627  D1      2  31   
372909  0015_295.6         4      320541.3   CD Road  0.2627  D2      3  31   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPCT  \
372904           Freeway             1871  0.4690      PM  0.2052   13.4   
372905           Freeway             1871  0.5310      PM  0.2052    8.0   
372906           Freeway             1767  0.3655      PM  0.3302    0.0   
372907           Freeway             1767  0.6345      PM  0.3302    0.0   
372908           Freeway             1473  0.5177      PM  0.2173   10.2   
372909           Freeway             1473  0.4823      PM  0.2173    7.8   

        HVPCT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
372904    6.1   2015        238075           238075     15438.140846   
372905    3.9   2015        238075           238075     17479.003816   
372906    0.0   2015        238075           238075      1824.534032   
372907    0.0   2015        238075           238075      3167.351145   
372908    4.9   2015        238075           238075      7035.771996   
372909    3.8   2015        238075           238075      6554.670337   

          DOWFACFC      SsnGrp SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
372904  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
372905  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
372906  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
372907  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
372908  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
372909  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   

       SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol SiteGroupDOW  \
372904             SN7     S00-Ann           1.0         15438          WDA   
372905             SN7     S00-Ann           1.0         17479          WDA   
372906             SN7     S00-Ann           1.0          1824          WDA   
372907             SN7     S00-Ann           1.0          3167          WDA   
372908             SN7     S00-Ann           1.0          7035          WDA   
372909             SN7     S00-Ann           1.0          6554          WDA   

          DOWGroup  DOWFactor  AvgSsnDOWPrdVol Prd HrPctOf  VolPkHrPct  \
372904  W1-Weekday       1.06            16317  PM     Prd      0.3499   
372905  W1-Weekday       1.06            18475  PM     Prd      0.3499   
372906  W1-Weekday       1.06             1927  PM     Prd      0.3499   
372907  W1-Weekday       1.06             3347  PM     Prd      0.3499   
372908  W1-Weekday       1.06             7435  PM     Prd      0.3499   
372909  W1-Weekday       1.06             6927  PM     Prd      0.3499   

       SeasonType VCGroupCode  PrdHrs  AvgSsnDOWPkHrVol  TrkFac  PrdPCEFlow  \
372904     Season     AnnWkPM       3         5709.3183  1.0573        5750   
372905     Season     AnnWkPM       3         6464.4025  1.0355        6376   
372906     Season     AnnWkPM       3          674.2573  1.0000         642   
372907     Season     AnnWkPM       3         1171.1153  1.0000        1115   
372908     Season     AnnWkPM       3         2601.5065  1.0449        2589   
372909     Season     AnnWkPM       3         2423.7573  1.0346        2388   

        PkHrPCEFlow  PrdVC  PkHrVC   PHF  Pk15PCEFlow  Pk15VC  
372904         6036   0.77    0.81  0.92         6561    0.88  
372905         6693   0.85    0.89  0.95         7046    0.94  
372906          674   0.36    0.38  0.92          732  

SEGID Prd SeasonGroup    DOWGroup HrPctOf VCGroupCode  numRecords  \
7650  0015_295.6  AM     M01-Jan  W1-Weekday     Prd     JanWkAM           6   
7651  0015_295.6  AM     M02-Feb  W1-Weekday     Prd     FebWkAM           6   
7652  0015_295.6  AM     M03-Mar  W1-Weekday     Prd     MarWkAM           6   
7653  0015_295.6  AM     M04-Apr  W1-Weekday     Prd     AprWkAM           6   
7654  0015_295.6  AM     M05-May  W1-Weekday     Prd     MayWkAM           6   
7655  0015_295.6  AM     M06-Jun  W1-Weekday     Prd     JunWkAM           6   
7656  0015_295.6  AM     M07-Jul  W1-Weekday     Prd     JulWkAM           6   
7657  0015_295.6  AM     M08-Aug  W1-Weekday     Prd     AugWkAM           6   
7658  0015_295.6  AM     M09-Sep  W1-Weekday     Prd     SepWkAM           6   
7659  0015_295.6  AM     M10-Oct  W1-Weekday     Prd     OctWkAM           6   
7660  0015_295.6  AM     M11-Nov  W1-Weekday     Prd     NovWkAM           6   
7661  0015_295.6  AM     M12-Dec  W1-Weekday     Prd     DecWkAM           6   
7662  0015_295.6  AM     S00-Ann  W1-Weekday     Prd     AnnWkAM           6   
7663  0015_295.6  AM     S01-Win  W1-Weekday     Prd     WinWkAM           6   
7664  0015_295.6  AM     S02-Spr  W1-Weekday     Prd     SprWkAM           6   
7665  0015_295.6  AM     S03-Sum  W1-Weekday     Prd     SumWkAM           6   
7666  0015_295.6  AM     S04-Fal  W1-Weekday     Prd     FalWkAM           6   
7667  0015_295.6  DY     M01-Jan  6-Saturday      DY     JanSaDY           6   
7668  0015_295.6  DY     M01-Jan    7-Sunday      DY     JanSuDY           6   
7669  0015_295.6  DY     M02-Feb  6-Saturday      DY     FebSaDY           6   
7670  0015_295.6  DY     M02-Feb    7-Sunday      DY     FebSuDY           6   
7671  0015_295.6  DY     M03-Mar  6-Saturday      DY     MarSaDY           6   
7672  0015_295.6  DY     M03-Mar    7-Sunday      DY     MarSuDY           6   
7673  0015_295.6  DY     M04-Apr  6-Saturday      DY     AprSaDY           6   
7674  0015_295.6  DY     M04-Apr    7-Sunday      DY     AprSuDY           6   
7675  0015_295.6  DY     M05-May  6-Saturday      DY     MaySaDY           6   
7676  0015_295.6  DY     M05-May    7-Sunday      DY     MaySuDY           6   
7677  0015_295.6  DY     M06-Jun  6-Saturday      DY     JunSaDY           6   
7678  0015_295.6  DY     M06-Jun    7-Sunday      DY     JunSuDY           6   
7679  0015_295.6  DY     M07-Jul  6-Saturday      DY     JulSaDY           6   
7680  0015_295.6  DY     M07-Jul    7-Sunday      DY     JulSuDY           6   
7681  0015_295.6  DY     M08-Aug  6-Saturday      DY     AugSaDY           6   
7682  0015_295.6  DY     M08-Aug    7-Sunday      DY     AugSuDY           6   
7683  0015_295.6  DY     M09-Sep  6-Saturday      DY     SepSaDY           6   
7684  0015_295.6  DY     M09-Sep    7-Sunday      DY     SepSuDY           6   
7685  0015_295.6  DY     M10-Oct  6-Saturday      DY     OctSaDY           6   
7686  0015_295.6  DY     M10-Oct    7-Sunday      DY     OctSuDY           6   
7687  0015_295.6  DY     M11-Nov  6-Saturday      DY     NovSaDY           6   
7688  0015_295.6  DY     M11-Nov    7-Sunday      DY     NovSuDY           6   
7689  0015_295.6  DY     M12-Dec  6-Saturday      DY     DecSaDY           6   
7690  0015_295.6  DY     M12-Dec    7-Sunday      DY     DecSuDY           6   
7691  0015_295.6  DY     S00-Ann  6-Saturday      DY     AnnSaDY           6   
7692  0015_295.6  DY     S00-Ann    7-Sunday      DY     AnnSuDY           6   
7693  0015_295.6  DY     S01-Win  6-Saturday      DY     WinSaDY           6   
7694  0015_295.6  DY     S01-Win    7-Sunday      DY     WinSuDY           6   
7695  0015_295.6  DY     S02-Spr  6-Saturday      DY     SprSaDY           6   
7696  0015_295.6  DY     S02-Spr    7-Sunday      DY     SprSuDY           6   
7697  0015_295.6  DY     S03-Sum  6-Saturday      DY     SumSaDY           6   
7698  0015_295.6  DY     S03-Sum    7-Sunday      DY     SumSuDY           6   
7699  0015_

# VC Groups as Columns

In [197]:
df_VCGroups

SeasonGroup SeasonType    DOWGroup HrPctOf Prd VCGroupCode
VCGroupID                                                           
0             S00-Ann     Season  W1-Weekday     Prd  AM     AnnWkAM
1             S01-Win     Season  W1-Weekday     Prd  AM     WinWkAM
2             S02-Spr     Season  W1-Weekday     Prd  AM     SprWkAM
3             S03-Sum     Season  W1-Weekday     Prd  AM     SumWkAM
4             S04-Fal     Season  W1-Weekday     Prd  AM     FalWkAM
5             M01-Jan      Month  W1-Weekday     Prd  AM     JanWkAM
6             M02-Feb      Month  W1-Weekday     Prd  AM     FebWkAM
7             M03-Mar      Month  W1-Weekday     Prd  AM     MarWkAM
8             M04-Apr      Month  W1-Weekday     Prd  AM     AprWkAM
9             M05-May      Month  W1-Weekday     Prd  AM     MayWkAM
10            M06-Jun      Month  W1-Weekday     Prd  AM     JunWkAM
11            M07-Jul      Month  W1-Weekday     Prd  AM     JulWkAM
12            M08-Aug      Month  W1-Weekday     Prd  AM     AugWkAM
13            M09-Sep      Month  W1-Weekday     Prd  AM     SepWkAM
14            M10-Oct      Month  W1-Weekday     Prd  AM     OctWkAM
15            M11-Nov      Month  W1-Weekday     Prd  AM     NovWkAM
16            M12-Dec      Month  W1-Weekday     Prd  AM     DecWkAM
17            S00-Ann     Season  W1-Weekday     Prd  MD     AnnWkMD
18            S01-Win     Season  W1-Weekday     Prd  MD     WinWkMD
19            S02-Spr     Season  W1-Weekday     Prd  MD     SprWkMD
20            S03-Sum     Season  W1-Weekday     Prd  MD     SumWkMD
21            S04-Fal     Season  W1-Weekday     Prd  MD     FalWkMD
22            M01-Jan      Month  W1-Weekday     Prd  MD     JanWkMD
23            M02-Feb      Month  W1-Weekday     Prd  MD     FebWkMD
24            M03-Mar      Month  W1-Weekday     Prd  MD     MarWkMD
25            M04-Apr      Month  W1-Weekday     Prd  MD     AprWkMD
26            M05-May      Month  W1-Weekday     Prd  MD     MayWkMD
27            M06-Jun      Month  W1-Weekday     Prd  MD     JunWkMD
28            M07-Jul      Month  W1-Weekday     Prd  MD     JulWkMD
29            M08-Aug      Month  W1-Weekday     Prd  MD     AugWkMD
30            M09-Sep      Month  W1-Weekday     Prd  MD     SepWkMD
31            M10-Oct      Month  W1-Weekday     Prd  MD     OctWkMD
32            M11-Nov      Month  W1-Weekday     Prd  MD     NovWkMD
33            M12-Dec      Month  W1-Weekday     Prd  MD     DecWkMD
34            S00-Ann     Season  W1-Weekday     Prd  PM     AnnWkPM
35            S01-Win     Season  W1-Weekday     Prd  PM     WinWkPM
36            S02-Spr     Season  W1-Weekday     Prd  PM     SprWkPM
37            S03-Sum     Season  W1-Weekday     Prd  PM     SumWkPM
38            S04-Fal     Season  W1-Weekday     Prd  PM     FalWkPM
39            M01-Jan      Month  W1-Weekday     Prd  PM     JanWkPM
40            M02-Feb      Month  W1-Weekday     Prd  PM     FebWkPM
41            M03-Mar      Month  W1-Weekday     Prd  PM     MarWkPM
42            M04-Apr      Month  W1-Weekday     Prd  PM     AprWkPM
43            M05-May      Month  W1-Weekday     Prd  PM     MayWkPM
44            M06-Jun      Month  W1-Weekday     Prd  PM     JunWkPM
45            M07-Jul      Month  W1-Weekday     Prd  PM     JulWkPM
46            M08-Aug      Month  W1-Weekday     Prd  PM     AugWkPM
47            M09-Sep      Month  W1-Weekday     Prd  PM     SepWkPM
48            M10-Oct      Month  W1-Weekday     Prd  PM     OctWkPM
49            M11-Nov      Month  W1-Weekday     Prd  PM     NovWkPM
50            M12-Dec      Month  W1-Weekday     Prd  PM     DecWkPM
51            S00-Ann     Season    5-Friday      DY  PM     AnnFrPM
52            S01-Win     Season    5-Friday      DY  PM     WinFrPM
53            S02-Spr     Season    5-Friday      DY  PM     SprFrPM
54            S03-Sum     Season    5-Friday      DY  PM     SumFrPM
55            S04-Fal     Season    5-Friday      DY  PM     FalFrPM
56      

In [198]:
dfs_VC_MaxDirFG_wVCGroups_15 = []

for df_VC_MaxDirFG in dfs_VC_MaxDirFG:

    df_VC_MaxDirFG_wVCGroups_15 = df_VC_MaxDirFG[['VCGroupCode','SEGID','Pk15VCMax']].copy()
    
    df_VC_MaxDirFG_wVCGroups_15['VCGroupCode'] = df_VC_MaxDirFG_wVCGroups_15['VCGroupCode'] + "15"
    
    df_VC_MaxDirFG_wVCGroups_15 = df_VC_MaxDirFG_wVCGroups_15.round({'Pk15VC': 2})
    
    df_VC_MaxDirFG_wVCGroups_15 = df_VC_MaxDirFG_wVCGroups_15.pivot(index='SEGID', columns="VCGroupCode",values='Pk15VCMax')
    
    df_VC_MaxDirFG_wVCGroups_15 = df_VC_MaxDirFG_wVCGroups_15.reset_index()
    
    dfs_VC_MaxDirFG_wVCGroups_15.append(df_VC_MaxDirFG_wVCGroups_15)

    display(df_VC_MaxDirFG_wVCGroups_15)
    

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.09       0.09       0.09       0.05   
1            0006_149.9       0.18       0.17       0.16       0.10   
2            0006_150.6       0.18       0.17       0.16       0.10   
3            0006_152.6       0.17       0.16       0.16       0.12   
4            0006_152.9       0.21       0.20       0.18       0.17   
...                 ...        ...        ...        ...        ...   
3577          WFRC_8208       0.00       0.00       0.00       0.00   
3578          WFRC_8209       0.00       0.00       0.00       0.00   
3579          WFRC_8213       0.00       0.00       0.00       0.00   
3580          WFRC_8215       0.00       0.00       0.00       0.00   
3581          WFRC_8218       0.00       0.00       0.00       0.00   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.05       0.07       0.11       0.09       0.10       0.06   
1                 0.09       0.13       0.17       0.16       0.16       0.10   
2                 0.09       0.13       0.17       0.16       0.15       0.10   
3                 0.09       0.14       0.19       0.17       0.17       0.13   
4                 0.10       0.18       0.20       0.19       0.18       0.16   
...                ...        ...        ...        ...        ...        ...   
3577              0.00       0.00       0.00       0.00       0.00       0.00   
3578              0.00       0.00       0.00       0.00       0.00       0.00   
3579              0.00       0.00       0.00       0.00       0.00       0.00   
3580              0.00       0.00       0.00       0.00       0.00       0.00   
3581              0.00       0.00       0.00       0.00       0.00       0.00   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.05       0.07       0.10       0.10       0.09       0.06   
1                 0.09       0.13       0.20       0.19       0.18       0.11   
2                 0.09       0.13       0.20       0.19       0.18       0.12   
3                 0.09       0.15       0.17       0.17       0.17       0.13   
4                 0.10       0.18       0.23       0.22       0.21       0.19   
...                ...        ...        ...        ...        ...        ...   
3577              0.00       0.00       0.00       0.00       0.00       0.00   
3578              0.00       0.00       0.00       0.00       0.00       0.00   
3579              0.00       0.00       0.00       0.00       0.00       0.00   
3580              0.00       0.00       0.00       0.00       0.00       0.00   
3581              0.00       0.00       0.00       0.00       0.00       0.00   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.05       0.08       0.08       0.08       0.08       0.05   
1                 0.11       0.15       0.16       0.15       0.14       0.09   
2                 0.10       0.15       0.16       0.15       0.14       0.09   
3                 0.09       0.16       0.15       0.15       0.14       0.11   
4                 0.12       0.21       0.19       0.18       0.17       0.15   
...                ...        ...        ...        ...        ...        ...   
3577              0.00       0.00       0.00       0.00       0.00       0.00   
3578              0.00       0.00       0.00       0.00       0.00       0.00   
3579              0.00       0.00       0.00       0.00       0.00       0.00   
3580              0.00       0.00       0.00       0.00       0.00       0.00   
3581              0.00       0.00       0.00       0.00       0.00       0.00   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.04       0.06       0.10       0.09       0.09       0.06   
1                 0.08       0.11       0.18       0.17       0.16

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.14       0.14       0.13       0.09   
1            0006_149.9       0.30       0.29       0.27       0.19   
2            0006_150.6       0.30       0.29       0.27       0.18   
3            0006_152.6       0.33       0.31       0.29       0.19   
4            0006_152.9       0.46       0.30       0.24       0.36   
...                 ...        ...        ...        ...        ...   
3883          WFRC_8215       0.56       0.37       0.29       0.44   
3884          WFRC_8216       0.49       0.17       0.13       0.45   
3885          WFRC_8217       1.64       1.08       0.91       1.03   
3886          WFRC_8218       1.63       0.98       0.82       1.17   
3887          WFRC_8219       1.02       0.84       0.73       0.63   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.07       0.11       0.16       0.14       0.15       0.10   
1                 0.15       0.24       0.29       0.27       0.26       0.19   
2                 0.15       0.24       0.29       0.27       0.26       0.18   
3                 0.17       0.24       0.31       0.29       0.28       0.19   
4                 0.29       0.44       0.46       0.31       0.24       0.36   
...                ...        ...        ...        ...        ...        ...   
3883              0.34       0.56       0.56       0.37       0.29       0.44   
3884              0.24       0.60       0.49       0.17       0.14       0.45   
3885              0.99       1.29       1.65       1.10       0.92       1.05   
3886              1.03       1.30       1.65       1.00       0.84       1.20   
3887              0.50       1.03       1.04       0.84       0.75       0.64   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.07       0.12       0.15       0.15       0.14       0.10   
1                 0.15       0.24       0.34       0.32       0.30       0.22   
2                 0.15       0.23       0.34       0.32       0.30       0.21   
3                 0.16       0.23       0.37       0.34       0.32       0.22   
4                 0.29       0.44       0.47       0.30       0.24       0.36   
...                ...        ...        ...        ...        ...        ...   
3883              0.34       0.56       0.56       0.36       0.28       0.44   
3884              0.24       0.61       0.52       0.16       0.13       0.47   
3885              1.00       1.30       1.67       1.06       0.89       1.05   
3886              1.04       1.33       1.65       0.96       0.80       1.18   
3887              0.51       1.04       1.07       0.86       0.75       0.66   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.08       0.12       0.13       0.13       0.12       0.08   
1                 0.17       0.28       0.27       0.26       0.24       0.17   
2                 0.18       0.27       0.27       0.26       0.24       0.16   
3                 0.19       0.27       0.29       0.28       0.26       0.17   
4                 0.29       0.46       0.45       0.30       0.24       0.34   
...                ...        ...        ...        ...        ...        ...   
3883              0.35       0.58       0.54       0.36       0.28       0.42   
3884              0.25       0.63       0.45       0.17       0.13       0.42   
3885              1.02       1.35       1.59       1.07       0.90       1.00   
3886              1.03       1.32       1.58       1.00       0.83       1.15   
3887              0.53       1.09       0.95       0.81       0.70       0.59   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.06       0.10       0.15       0.14       0.14       0.10   
1                 0.13       0.21       0.31       0.29       0.27

In [199]:
df_VC_MaxDirFG.columns

Index(['SEGID', 'Prd', 'SeasonGroup', 'DOWGroup', 'HrPctOf', 'VCGroupCode',
       'numRecords', 'CAP1HLSum', 'PrdPCEFlowSum', 'PkHrPCEFlowSum',
       'Pk15PCEFlowSum', 'PrdVCMax', 'PkHrVCMax', 'Pk15VCMax'],
      dtype='object')

In [200]:
dfs_VC_MaxDirFG_wVCGroups_Hr = []

for df_VC_MaxDirFG in dfs_VC_MaxDirFG:

    df_VC_MaxDirFG_wVCGroups_Hr = df_VC_MaxDirFG[['VCGroupCode','SEGID','PkHrVCMax']].copy()
    
    df_VC_MaxDirFG_wVCGroups_Hr['VCGroupCode'] = df_VC_MaxDirFG_wVCGroups_Hr['VCGroupCode'] + "Hr"
    
    df_VC_MaxDirFG_wVCGroups_Hr = df_VC_MaxDirFG_wVCGroups_Hr.round({'PkHrVC': 2})
    
    df_VC_MaxDirFG_wVCGroups_Hr = df_VC_MaxDirFG_wVCGroups_Hr.pivot(index='SEGID', columns="VCGroupCode",values='PkHrVCMax')
    
    df_VC_MaxDirFG_wVCGroups_Hr = df_VC_MaxDirFG_wVCGroups_Hr.reset_index()
    
    dfs_VC_MaxDirFG_wVCGroups_Hr.append(df_VC_MaxDirFG_wVCGroups_Hr)

    display(df_VC_MaxDirFG_wVCGroups_Hr)
    

VCGroupCode       SEGID  AnnFrPMHr  AnnSaDYHr  AnnSuDYHr  AnnWkAMHr  \
0            0006_146.9       0.08       0.08       0.08       0.05   
1            0006_149.9       0.16       0.15       0.14       0.09   
2            0006_150.6       0.16       0.15       0.14       0.09   
3            0006_152.6       0.15       0.14       0.14       0.11   
4            0006_152.9       0.18       0.17       0.16       0.15   
...                 ...        ...        ...        ...        ...   
3577          WFRC_8208       0.00       0.00       0.00       0.00   
3578          WFRC_8209       0.00       0.00       0.00       0.00   
3579          WFRC_8213       0.00       0.00       0.00       0.00   
3580          WFRC_8215       0.00       0.00       0.00       0.00   
3581          WFRC_8218       0.00       0.00       0.00       0.00   

VCGroupCode  AnnWkMDHr  AnnWkPMHr  AprFrPMHr  AprSaDYHr  AprSuDYHr  AprWkAMHr  \
0                 0.04       0.06       0.09       0.08       0.09       0.05   
1                 0.08       0.11       0.15       0.14       0.14       0.09   
2                 0.08       0.12       0.15       0.14       0.14       0.09   
3                 0.08       0.13       0.16       0.15       0.15       0.11   
4                 0.09       0.16       0.17       0.16       0.16       0.15   
...                ...        ...        ...        ...        ...        ...   
3577              0.00       0.00       0.00       0.00       0.00       0.00   
3578              0.00       0.00       0.00       0.00       0.00       0.00   
3579              0.00       0.00       0.00       0.00       0.00       0.00   
3580              0.00       0.00       0.00       0.00       0.00       0.00   
3581              0.00       0.00       0.00       0.00       0.00       0.00   

VCGroupCode  AprWkMDHr  AprWkPMHr  AugFrPMHr  AugSaDYHr  AugSuDYHr  AugWkAMHr  \
0                 0.04       0.06       0.09       0.09       0.08       0.05   
1                 0.08       0.11       0.18       0.16       0.16       0.10   
2                 0.08       0.11       0.18       0.16       0.16       0.10   
3                 0.08       0.13       0.15       0.15       0.15       0.12   
4                 0.09       0.16       0.21       0.19       0.18       0.17   
...                ...        ...        ...        ...        ...        ...   
3577              0.00       0.00       0.00       0.00       0.00       0.00   
3578              0.00       0.00       0.00       0.00       0.00       0.00   
3579              0.00       0.00       0.00       0.00       0.00       0.00   
3580              0.00       0.00       0.00       0.00       0.00       0.00   
3581              0.00       0.00       0.00       0.00       0.00       0.00   

VCGroupCode  AugWkMDHr  AugWkPMHr  DecFrPMHr  DecSaDYHr  DecSuDYHr  DecWkAMHr  \
0                 0.05       0.07       0.07       0.07       0.07       0.04   
1                 0.09       0.13       0.14       0.14       0.13       0.08   
2                 0.09       0.13       0.14       0.14       0.13       0.08   
3                 0.08       0.14       0.13       0.13       0.12       0.10   
4                 0.10       0.18       0.17       0.16       0.15       0.13   
...                ...        ...        ...        ...        ...        ...   
3577              0.00       0.00       0.00       0.00       0.00       0.00   
3578              0.00       0.00       0.00       0.00       0.00       0.00   
3579              0.00       0.00       0.00       0.00       0.00       0.00   
3580              0.00       0.00       0.00       0.00       0.00       0.00   
3581              0.00       0.00       0.00       0.00       0.00       0.00   

VCGroupCode  DecWkMDHr  DecWkPMHr  FalFrPMHr  FalSaDYHr  FalSuDYHr  FalWkAMHr  \
0                 0.04       0.05       0.09       0.08       0.08       0.05   
1                 0.07       0.10       0.16       0.15       0.14

VCGroupCode       SEGID  AnnFrPMHr  AnnSaDYHr  AnnSuDYHr  AnnWkAMHr  \
0            0006_146.9       0.13       0.12       0.12       0.08   
1            0006_149.9       0.27       0.25       0.24       0.17   
2            0006_150.6       0.27       0.25       0.24       0.16   
3            0006_152.6       0.29       0.27       0.25       0.17   
4            0006_152.9       0.42       0.28       0.22       0.33   
...                 ...        ...        ...        ...        ...   
3883          WFRC_8215       0.51       0.34       0.26       0.40   
3884          WFRC_8216       0.45       0.15       0.12       0.41   
3885          WFRC_8217       1.61       1.06       0.83       1.01   
3886          WFRC_8218       1.60       0.93       0.76       1.15   
3887          WFRC_8219       0.93       0.73       0.64       0.55   

VCGroupCode  AnnWkMDHr  AnnWkPMHr  AprFrPMHr  AprSaDYHr  AprSuDYHr  AprWkAMHr  \
0                 0.06       0.10       0.14       0.13       0.13       0.09   
1                 0.13       0.22       0.26       0.24       0.23       0.17   
2                 0.13       0.21       0.25       0.24       0.23       0.16   
3                 0.15       0.21       0.27       0.26       0.25       0.16   
4                 0.26       0.40       0.43       0.28       0.22       0.34   
...                ...        ...        ...        ...        ...        ...   
3883              0.31       0.51       0.51       0.34       0.27       0.41   
3884              0.22       0.56       0.45       0.16       0.13       0.42   
3885              0.96       1.26       1.61       1.07       0.84       1.03   
3886              1.00       1.27       1.62       0.95       0.77       1.17   
3887              0.44       0.96       0.95       0.74       0.66       0.56   

VCGroupCode  AprWkMDHr  AprWkPMHr  AugFrPMHr  AugSaDYHr  AugSuDYHr  AugWkAMHr  \
0                 0.06       0.10       0.13       0.13       0.12       0.09   
1                 0.13       0.21       0.30       0.28       0.26       0.19   
2                 0.13       0.20       0.30       0.28       0.26       0.18   
3                 0.14       0.20       0.32       0.30       0.28       0.19   
4                 0.27       0.41       0.43       0.27       0.22       0.33   
...                ...        ...        ...        ...        ...        ...   
3883              0.32       0.52       0.52       0.33       0.26       0.41   
3884              0.22       0.56       0.48       0.15       0.12       0.43   
3885              0.97       1.27       1.64       1.04       0.82       1.03   
3886              1.02       1.30       1.62       0.91       0.74       1.15   
3887              0.45       0.97       0.99       0.76       0.66       0.58   

VCGroupCode  AugWkMDHr  AugWkPMHr  DecFrPMHr  DecSaDYHr  DecSuDYHr  DecWkAMHr  \
0                 0.07       0.11       0.11       0.11       0.10       0.07   
1                 0.15       0.25       0.24       0.23       0.21       0.15   
2                 0.15       0.24       0.24       0.23       0.21       0.14   
3                 0.17       0.24       0.26       0.25       0.23       0.15   
4                 0.27       0.42       0.41       0.28       0.22       0.32   
...                ...        ...        ...        ...        ...        ...   
3883              0.32       0.54       0.49       0.33       0.26       0.39   
3884              0.23       0.58       0.42       0.15       0.12       0.39   
3885              0.99       1.32       1.56       1.05       0.83       0.97   
3886              1.00       1.29       1.55       0.95       0.77       1.13   
3887              0.47       1.03       0.87       0.71       0.62       0.51   

VCGroupCode  DecWkMDHr  DecWkPMHr  FalFrPMHr  FalSaDYHr  FalSuDYHr  FalWkAMHr  \
0                 0.05       0.09       0.13       0.12       0.12       0.09   
1                 0.12       0.19       0.27       0.25       0.24

In [201]:
dfs_VC_MaxDirFG_wVCGroups_Prd = []

for df_VC_MaxDirFG in dfs_VC_MaxDirFG:

    df_VC_MaxDirFG_wVCGroups_Prd = df_VC_MaxDirFG[df_VC_MaxDirFG['HrPctOf'] == 'Prd'].copy()
    
    df_VC_MaxDirFG_wVCGroups_Prd['VCGroupCode'] = df_VC_MaxDirFG_wVCGroups_Prd['VCGroupCode'] + "Prd"
    
    df_VC_MaxDirFG_wVCGroups_Prd = df_VC_MaxDirFG_wVCGroups_Prd[['VCGroupCode','SEGID','PrdVCMax']]
    
    df_VC_MaxDirFG_wVCGroups_Prd = df_VC_MaxDirFG_wVCGroups_Prd.round({'PrdVC': 2})
    
    df_VC_MaxDirFG_wVCGroups_Prd = df_VC_MaxDirFG_wVCGroups_Prd.pivot(index='SEGID', columns="VCGroupCode",values='PrdVCMax')
    
    df_VC_MaxDirFG_wVCGroups_Prd = df_VC_MaxDirFG_wVCGroups_Prd.reset_index()
    
    dfs_VC_MaxDirFG_wVCGroups_Prd.append(df_VC_MaxDirFG_wVCGroups_Prd)

    display(df_VC_MaxDirFG_wVCGroups_Prd)

VCGroupCode       SEGID  AnnWkAMPrd  AnnWkMDPrd  AnnWkPMPrd  AprWkAMPrd  \
0            0006_146.9        0.04        0.04        0.06        0.04   
1            0006_149.9        0.07        0.07        0.11        0.07   
2            0006_150.6        0.08        0.07        0.11        0.07   
3            0006_152.6        0.09        0.06        0.11        0.09   
4            0006_152.9        0.12        0.08        0.15        0.12   
...                 ...         ...         ...         ...         ...   
3577          WFRC_8208        0.00        0.00        0.00        0.00   
3578          WFRC_8209        0.00        0.00        0.00        0.00   
3579          WFRC_8213        0.00        0.00        0.00        0.00   
3580          WFRC_8215        0.00        0.00        0.00        0.00   
3581          WFRC_8218        0.00        0.00        0.00        0.00   

VCGroupCode  AprWkMDPrd  AprWkPMPrd  AugWkAMPrd  AugWkMDPrd  AugWkPMPrd  \
0                  0.04        0.06        0.04        0.04        0.06   
1                  0.07        0.10        0.08        0.08        0.12   
2                  0.07        0.10        0.09        0.08        0.12   
3                  0.07        0.12        0.10        0.07        0.12   
4                  0.08        0.14        0.14        0.09        0.17   
...                 ...         ...         ...         ...         ...   
3577               0.00        0.00        0.00        0.00        0.00   
3578               0.00        0.00        0.00        0.00        0.00   
3579               0.00        0.00        0.00        0.00        0.00   
3580               0.00        0.00        0.00        0.00        0.00   
3581               0.00        0.00        0.00        0.00        0.00   

VCGroupCode  DecWkAMPrd  DecWkMDPrd  DecWkPMPrd  FalWkAMPrd  FalWkMDPrd  \
0                  0.03        0.03        0.05        0.04        0.04   
1                  0.06        0.06        0.09        0.07        0.07   
2                  0.07        0.06        0.09        0.08        0.07   
3                  0.08        0.06        0.10        0.09        0.07   
4                  0.11        0.07        0.13        0.12        0.08   
...                 ...         ...         ...         ...         ...   
3577               0.00        0.00        0.00        0.00        0.00   
3578               0.00        0.00        0.00        0.00        0.00   
3579               0.00        0.00        0.00        0.00        0.00   
3580               0.00        0.00        0.00        0.00        0.00   
3581               0.00        0.00        0.00        0.00        0.00   

VCGroupCode  FalWkPMPrd  FebWkAMPrd  FebWkMDPrd  FebWkPMPrd  JanWkAMPrd  \
0                  0.06        0.03        0.03        0.05        0.03   
1                  0.11        0.06        0.06        0.09        0.06   
2                  0.11        0.06        0.06        0.09        0.06   
3                  0.12        0.08        0.06        0.10        0.07   
4                  0.15        0.10        0.07        0.12        0.09   
...                 ...         ...         ...         ...         ...   
3577               0.00        0.00        0.00        0.00        0.00   
3578               0.00        0.00        0.00        0.00        0.00   
3579               0.00        0.00        0.00        0.00        0.00   
3580               0.00        0.00        0.00        0.00        0.00   
3581               0.00        0.00        0.00        0.00        0.00   

VCGroupCode  JanWkMDPrd  JanWkPMPrd  JulWkAMPrd  JulWkMDPrd  JulWkPMPrd  \
0                  0.03        0.04        0.04        0.04        0.06   
1                  0.05        0.08        0.09        0.09        0.13   
2                  0.05        0.08        0.09        0.08        0.13   
3                  0.05        0.09        0.10        0.07        0.12   
4                  0.

VCGroupCode       SEGID  AnnWkAMPrd  AnnWkMDPrd  AnnWkPMPrd  AprWkAMPrd  \
0            0006_146.9        0.07        0.05        0.09        0.07   
1            0006_149.9        0.14        0.12        0.20        0.14   
2            0006_150.6        0.13        0.12        0.19        0.13   
3            0006_152.6        0.14        0.13        0.19        0.13   
4            0006_152.9        0.27        0.23        0.36        0.28   
...                 ...         ...         ...         ...         ...   
3883          WFRC_8215        0.33        0.27        0.46        0.34   
3884          WFRC_8216        0.33        0.16        0.47        0.33   
3885          WFRC_8217        0.84        0.84        1.13        0.85   
3886          WFRC_8218        0.99        0.86        1.15        1.01   
3887          WFRC_8219        0.46        0.39        0.84        0.47   

VCGroupCode  AprWkMDPrd  AprWkPMPrd  AugWkAMPrd  AugWkMDPrd  AugWkPMPrd  \
0                  0.05        0.09        0.07        0.06        0.10   
1                  0.11        0.19        0.16        0.14        0.23   
2                  0.11        0.19        0.15        0.14        0.22   
3                  0.12        0.19        0.16        0.15        0.22   
4                  0.23        0.37        0.28        0.24        0.37   
...                 ...         ...         ...         ...         ...   
3883               0.28        0.46        0.34        0.28        0.47   
3884               0.17        0.47        0.34        0.17        0.49   
3885               0.85        1.14        0.87        0.87        1.17   
3886               0.88        1.17        1.01        0.87        1.16   
3887               0.39        0.85        0.49        0.41        0.89   

VCGroupCode  DecWkAMPrd  DecWkMDPrd  DecWkPMPrd  FalWkAMPrd  FalWkMDPrd  \
0                  0.06        0.05        0.08        0.07        0.05   
1                  0.12        0.10        0.17        0.14        0.12   
2                  0.12        0.10        0.17        0.13        0.12   
3                  0.12        0.11        0.17        0.14        0.13   
4                  0.26        0.22        0.35        0.28        0.23   
...                 ...         ...         ...         ...         ...   
3883               0.32        0.26        0.44        0.34        0.28   
3884               0.32        0.16        0.45        0.34        0.17   
3885               0.80        0.80        1.08        0.85        0.86   
3886               0.98        0.85        1.13        1.00        0.87   
3887               0.42        0.36        0.78        0.47        0.40   

VCGroupCode  FalWkPMPrd  FebWkAMPrd  FebWkMDPrd  FebWkPMPrd  JanWkAMPrd  \
0                  0.09        0.06        0.04        0.08        0.06   
1                  0.20        0.12        0.10        0.16        0.11   
2                  0.19        0.11        0.10        0.16        0.10   
3                  0.19        0.11        0.11        0.16        0.11   
4                  0.37        0.26        0.22        0.35        0.24   
...                 ...         ...         ...         ...         ...   
3883               0.47        0.32        0.26        0.44        0.29   
3884               0.48        0.31        0.16        0.44        0.31   
3885               1.15        0.80        0.80        1.08        0.74   
3886               1.15        0.98        0.85        1.13        0.93   
3887               0.85        0.41        0.35        0.75        0.39   

VCGroupCode  JanWkMDPrd  JanWkPMPrd  JulWkAMPrd  JulWkMDPrd  JulWkPMPrd  \
0                  0.04        0.07        0.07        0.06        0.10   
1                  0.09        0.15        0.17        0.14        0.24   
2                  0.09        0.15        0.16        0.14        0.23   
3                  0.10        0.15        0.16        0.15        0.23   
4                  0.

In [225]:
df_Scenarios

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
0               No       Base15          Base      2015 Base          2015   
1               No       Base19          Base      2019 Base          2019   
2               No        TIP24           TIP       2024 TIP          2024   
3               No        RTP30           RTP       2030 RTP          2030   
4               No        RTP40           RTP       2040 RTP          2040   
5               No        RTP50           RTP       2050 RTP          2050   
6               No         NB30      No Build  2030 No Build          2030   
7               No         NB40      No Build  2040 No Build          2040   
8               No         NB50      No Build  2050 No Build          2050   
9               No         UF30         Needs     2030 Needs          2030   
10              No         UF40         Needs     2040 Needs          2040   
11              No         UF50         Needs     2050 Needs          2050   
12             Yes         S550      Scenario  2050 S5 Draft          2050   

                                                SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                      
0                  v831_SE15_Net15_Summary_SEGID_Detailed.csv             NaN   
1                  v831_SE19_Net19_Summary_SEGID_Detailed.csv          Base15   
2                  v831_SE24_Net24_Summary_SEGID_Detailed.csv          Base19   
3                  v831_SE30_Net30_Summary_SEGID_Detailed.csv           TIP24   
4                  v831_SE40_Net40_Summary_SEGID_Detailed.csv           RTP30   
5                  v831_SE50_Net50_Summary_SEGID_Detailed.csv           RTP40   
6                  v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
7                  v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
8                  v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
9                v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
10               v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
11               v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   
12          v831_SE50_Net50_Summary_SEGID_Detailed_S5Draft...             NaN   

           AdjScenarioCode  
ScenarioID                  
0                      NaN  
1                      NaN  
2                      NaN  
3                      NaN  
4                      NaN  
5                      NaN  
6                    RTP30  
7                    RTP40  
8                    RTP50  
9                    RTP30  
10                   RTP40  
11                   RTP50  
12                   RTP50

In [203]:
i

1

In [204]:
dfs_VC_MaxDirFG_wVCGroups = []

i=-1
for (idx, row) in df_Scenarios.iterrows():

    if row.loc['Process'] == 'Yes':

        i=i+1
        
        df_VC_MaxDirFG_wVCGroups = pd.DataFrame.merge(dfs_VC_MaxDirFG_wVCGroups_15[i],dfs_VC_MaxDirFG_wVCGroups_Hr[i],on='SEGID')
        df_VC_MaxDirFG_wVCGroups = pd.DataFrame.merge(df_VC_MaxDirFG_wVCGroups,dfs_VC_MaxDirFG_wVCGroups_Prd[i],on='SEGID')
        dfs_VC_MaxDirFG_wVCGroups.append(df_VC_MaxDirFG_wVCGroups)
        display(df_VC_MaxDirFG_wVCGroups)

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.09       0.09       0.09       0.05   
1            0006_149.9       0.18       0.17       0.16       0.10   
2            0006_150.6       0.18       0.17       0.16       0.10   
3            0006_152.6       0.17       0.16       0.16       0.12   
4            0006_152.9       0.21       0.20       0.18       0.17   
...                 ...        ...        ...        ...        ...   
3577          WFRC_8208       0.00       0.00       0.00       0.00   
3578          WFRC_8209       0.00       0.00       0.00       0.00   
3579          WFRC_8213       0.00       0.00       0.00       0.00   
3580          WFRC_8215       0.00       0.00       0.00       0.00   
3581          WFRC_8218       0.00       0.00       0.00       0.00   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.05       0.07       0.11       0.09       0.10       0.06   
1                 0.09       0.13       0.17       0.16       0.16       0.10   
2                 0.09       0.13       0.17       0.16       0.15       0.10   
3                 0.09       0.14       0.19       0.17       0.17       0.13   
4                 0.10       0.18       0.20       0.19       0.18       0.16   
...                ...        ...        ...        ...        ...        ...   
3577              0.00       0.00       0.00       0.00       0.00       0.00   
3578              0.00       0.00       0.00       0.00       0.00       0.00   
3579              0.00       0.00       0.00       0.00       0.00       0.00   
3580              0.00       0.00       0.00       0.00       0.00       0.00   
3581              0.00       0.00       0.00       0.00       0.00       0.00   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.05       0.07       0.10       0.10       0.09       0.06   
1                 0.09       0.13       0.20       0.19       0.18       0.11   
2                 0.09       0.13       0.20       0.19       0.18       0.12   
3                 0.09       0.15       0.17       0.17       0.17       0.13   
4                 0.10       0.18       0.23       0.22       0.21       0.19   
...                ...        ...        ...        ...        ...        ...   
3577              0.00       0.00       0.00       0.00       0.00       0.00   
3578              0.00       0.00       0.00       0.00       0.00       0.00   
3579              0.00       0.00       0.00       0.00       0.00       0.00   
3580              0.00       0.00       0.00       0.00       0.00       0.00   
3581              0.00       0.00       0.00       0.00       0.00       0.00   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.05       0.08       0.08       0.08       0.08       0.05   
1                 0.11       0.15       0.16       0.15       0.14       0.09   
2                 0.10       0.15       0.16       0.15       0.14       0.09   
3                 0.09       0.16       0.15       0.15       0.14       0.11   
4                 0.12       0.21       0.19       0.18       0.17       0.15   
...                ...        ...        ...        ...        ...        ...   
3577              0.00       0.00       0.00       0.00       0.00       0.00   
3578              0.00       0.00       0.00       0.00       0.00       0.00   
3579              0.00       0.00       0.00       0.00       0.00       0.00   
3580              0.00       0.00       0.00       0.00       0.00       0.00   
3581              0.00       0.00       0.00       0.00       0.00       0.00   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.04       0.06       0.10       0.09       0.09       0.06   
1                 0.08       0.11       0.18       0.17       0.16

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.14       0.14       0.13       0.09   
1            0006_149.9       0.30       0.29       0.27       0.19   
2            0006_150.6       0.30       0.29       0.27       0.18   
3            0006_152.6       0.33       0.31       0.29       0.19   
4            0006_152.9       0.46       0.30       0.24       0.36   
...                 ...        ...        ...        ...        ...   
3883          WFRC_8215       0.56       0.37       0.29       0.44   
3884          WFRC_8216       0.49       0.17       0.13       0.45   
3885          WFRC_8217       1.64       1.08       0.91       1.03   
3886          WFRC_8218       1.63       0.98       0.82       1.17   
3887          WFRC_8219       1.02       0.84       0.73       0.63   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.07       0.11       0.16       0.14       0.15       0.10   
1                 0.15       0.24       0.29       0.27       0.26       0.19   
2                 0.15       0.24       0.29       0.27       0.26       0.18   
3                 0.17       0.24       0.31       0.29       0.28       0.19   
4                 0.29       0.44       0.46       0.31       0.24       0.36   
...                ...        ...        ...        ...        ...        ...   
3883              0.34       0.56       0.56       0.37       0.29       0.44   
3884              0.24       0.60       0.49       0.17       0.14       0.45   
3885              0.99       1.29       1.65       1.10       0.92       1.05   
3886              1.03       1.30       1.65       1.00       0.84       1.20   
3887              0.50       1.03       1.04       0.84       0.75       0.64   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.07       0.12       0.15       0.15       0.14       0.10   
1                 0.15       0.24       0.34       0.32       0.30       0.22   
2                 0.15       0.23       0.34       0.32       0.30       0.21   
3                 0.16       0.23       0.37       0.34       0.32       0.22   
4                 0.29       0.44       0.47       0.30       0.24       0.36   
...                ...        ...        ...        ...        ...        ...   
3883              0.34       0.56       0.56       0.36       0.28       0.44   
3884              0.24       0.61       0.52       0.16       0.13       0.47   
3885              1.00       1.30       1.67       1.06       0.89       1.05   
3886              1.04       1.33       1.65       0.96       0.80       1.18   
3887              0.51       1.04       1.07       0.86       0.75       0.66   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.08       0.12       0.13       0.13       0.12       0.08   
1                 0.17       0.28       0.27       0.26       0.24       0.17   
2                 0.18       0.27       0.27       0.26       0.24       0.16   
3                 0.19       0.27       0.29       0.28       0.26       0.17   
4                 0.29       0.46       0.45       0.30       0.24       0.34   
...                ...        ...        ...        ...        ...        ...   
3883              0.35       0.58       0.54       0.36       0.28       0.42   
3884              0.25       0.63       0.45       0.17       0.13       0.42   
3885              1.02       1.35       1.59       1.07       0.90       1.00   
3886              1.03       1.32       1.58       1.00       0.83       1.15   
3887              0.53       1.09       0.95       0.81       0.70       0.59   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.06       0.10       0.15       0.14       0.14       0.10   
1                 0.13       0.21       0.31       0.29       0.27

# Export final tables to CSV

In [226]:
if export_results: 
    df_Scenarios.to_csv(os.path.join(dirResults, r'scenarios.csv'),index=False)
    df_VCGroup_DOWPkHr.to_csv(os.path.join(dirResults, r'vcgroups_dowpeak.csv'),index=False)
    df_VCGroup_Seasons.to_csv(os.path.join(dirResults, r'vcgroups_seasons.csv'),index=False)
    df_VCGroups.to_csv(os.path.join(dirResults, r'vcgroups.csv'),index=False)

In [206]:
df_Scenarios_toExport

ScenarioID Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
0          12     Yes         S550      Scenario  2050 S5 Draft          2050   

                                       SegSummaryCSV PrvScenarioCode  \
0  v831_SE50_Net50_Summary_SEGID_Detailed_S5Draft...             NaN   

  AdjScenarioCode  
0           RTP50

In [207]:
i

1

In [208]:
if export_results: 

    df_Scenarios_toExport = df_Scenarios[df_Scenarios['Process']=='Yes']
    
    i=0
    for (idx, row) in df_Scenarios_toExport.iterrows():    
    
        filename = os.path.join(dirResults,"3_VC_MaxDirFG_wVCGroups_" + row.loc['ScenarioCode'] + '.csv')
        display('Exporting ' + filename)
        dfs_VC_MaxDirFG_wVCGroups[i].to_csv(filename, index=False)

        filename = os.path.join(dirResults,"2_VC_MaxDirFG_" + row.loc['ScenarioCode'] + '.csv')
        display('Exporting ' + filename)
        dfs_VC_MaxDirFG[i].to_csv(filename, index=False)

        filename = os.path.join(dirResults,"1_VC_" + row.loc['ScenarioCode'] + '.csv')
        display('Exporting ' + filename)
        dfs_VC[i].to_csv(filename, index=False)
        i=i+1

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\3_VC_MaxDirFG_wVCGroups_Base15.csv'

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\2_VC_MaxDirFG_Base15.csv'

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\1_VC_Base15.csv'

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\3_VC_MaxDirFG_wVCGroups_S550.csv'

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\2_VC_MaxDirFG_S550.csv'

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\1_VC_S550.csv'

In [209]:
for (idx, row) in df_Scenarios_toExport.iterrows():
    display(row.loc['ScenarioCode'])

'Base15'

'S550'

In [210]:
df = dfs_VC_MaxDirFG_wVCGroups[0]
df[df['SEGID']=='0079_003.0']
df

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.09       0.09       0.09       0.05   
1            0006_149.9       0.18       0.17       0.16       0.10   
2            0006_150.6       0.18       0.17       0.16       0.10   
3            0006_152.6       0.17       0.16       0.16       0.12   
4            0006_152.9       0.21       0.20       0.18       0.17   
...                 ...        ...        ...        ...        ...   
3577          WFRC_8208       0.00       0.00       0.00       0.00   
3578          WFRC_8209       0.00       0.00       0.00       0.00   
3579          WFRC_8213       0.00       0.00       0.00       0.00   
3580          WFRC_8215       0.00       0.00       0.00       0.00   
3581          WFRC_8218       0.00       0.00       0.00       0.00   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.05       0.07       0.11       0.09       0.10       0.06   
1                 0.09       0.13       0.17       0.16       0.16       0.10   
2                 0.09       0.13       0.17       0.16       0.15       0.10   
3                 0.09       0.14       0.19       0.17       0.17       0.13   
4                 0.10       0.18       0.20       0.19       0.18       0.16   
...                ...        ...        ...        ...        ...        ...   
3577              0.00       0.00       0.00       0.00       0.00       0.00   
3578              0.00       0.00       0.00       0.00       0.00       0.00   
3579              0.00       0.00       0.00       0.00       0.00       0.00   
3580              0.00       0.00       0.00       0.00       0.00       0.00   
3581              0.00       0.00       0.00       0.00       0.00       0.00   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.05       0.07       0.10       0.10       0.09       0.06   
1                 0.09       0.13       0.20       0.19       0.18       0.11   
2                 0.09       0.13       0.20       0.19       0.18       0.12   
3                 0.09       0.15       0.17       0.17       0.17       0.13   
4                 0.10       0.18       0.23       0.22       0.21       0.19   
...                ...        ...        ...        ...        ...        ...   
3577              0.00       0.00       0.00       0.00       0.00       0.00   
3578              0.00       0.00       0.00       0.00       0.00       0.00   
3579              0.00       0.00       0.00       0.00       0.00       0.00   
3580              0.00       0.00       0.00       0.00       0.00       0.00   
3581              0.00       0.00       0.00       0.00       0.00       0.00   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.05       0.08       0.08       0.08       0.08       0.05   
1                 0.11       0.15       0.16       0.15       0.14       0.09   
2                 0.10       0.15       0.16       0.15       0.14       0.09   
3                 0.09       0.16       0.15       0.15       0.14       0.11   
4                 0.12       0.21       0.19       0.18       0.17       0.15   
...                ...        ...        ...        ...        ...        ...   
3577              0.00       0.00       0.00       0.00       0.00       0.00   
3578              0.00       0.00       0.00       0.00       0.00       0.00   
3579              0.00       0.00       0.00       0.00       0.00       0.00   
3580              0.00       0.00       0.00       0.00       0.00       0.00   
3581              0.00       0.00       0.00       0.00       0.00       0.00   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.04       0.06       0.10       0.09       0.09       0.06   
1                 0.08       0.11       0.18       0.17       0.16

In [211]:
df_Scenarios_toProcess

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
0              Yes       Base15          Base      2015 Base          2015   
12             Yes         S550      Scenario  2050 S5 Draft          2050   

                                                SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                      
0                  v831_SE15_Net15_Summary_SEGID_Detailed.csv             NaN   
12          v831_SE50_Net50_Summary_SEGID_Detailed_S5Draft...             NaN   

           AdjScenarioCode  
ScenarioID                  
0                      NaN  
12                   RTP50

# Exports for WebApp

In [212]:
if export_results:
    
    df_Scenarios_json = df_Scenarios.copy()
    df_Scenarios_json = df_Scenarios_json[['ScenarioCode','ScenarioName']]
    df_Scenarios_json.columns = ('value','label')
    df_Scenarios_json['filename'] = "VC_" + df_Scenarios_json['value'] + '.json'
    
    df_VCGroup_Seasons_json = df_VCGroup_Seasons.copy()
    df_VCGroup_Seasons_json = df_VCGroup_Seasons_json[['SeasonCode','SeasonName','SeasonType']]
    df_VCGroup_Seasons_json.columns = ('value','label','SeasonType')
        
    df_VCGroup_DOWPkHr_json = df_VCGroup_DOWPkHr.copy()
    df_VCGroup_DOWPkHr_json = df_VCGroup_DOWPkHr_json[['DOWPkCode','DOWPkName']]
    df_VCGroup_DOWPkHr_json.columns = ('value','label')

    df_Scenarios_json.to_json(os.path.join(dirResults, r'WebAppData\scenarios.json'),orient='records')
    #df_Scenarios_json = df_Scenarios_json.reset_index()
    #df_Scenarios_json.to_json(os.path.join(dirResults, r'WebAppData\scenarios_test.json'))
    df_VCGroup_Seasons_json.to_json(os.path.join(dirResults, r'WebAppData\vcgroups_seasons.json'),orient='records')
    df_VCGroup_DOWPkHr_json.to_json(os.path.join(dirResults, r'WebAppData\vcgroups_dowpeaks.json'),orient='records')
    

In [213]:
df_Scenarios_json

value          label        filename
ScenarioID                                       
0           Base15      2015 Base  VC_Base15.json
1           Base19      2019 Base  VC_Base19.json
2            TIP24       2024 TIP   VC_TIP24.json
3            RTP30       2030 RTP   VC_RTP30.json
4            RTP40       2040 RTP   VC_RTP40.json
5            RTP50       2050 RTP   VC_RTP50.json
6             NB30  2030 No Build    VC_NB30.json
7             NB40  2040 No Build    VC_NB40.json
8             NB50  2050 No Build    VC_NB50.json
9             UF30     2030 Needs    VC_UF30.json
10            UF40     2040 Needs    VC_UF40.json
11            UF50     2050 Needs    VC_UF50.json
12            S550  2050 S5 Draft    VC_S550.json

In [214]:
if export_results:
    
    df_Scenarios_toExport = df_Scenarios_toProcess.reset_index()
    
    for index, df_VC_MaxDirFG_wVCGroups in enumerate(dfs_VC_MaxDirFG_wVCGroups):    

        filename = "WebAppData\VC_" + df_Scenarios_toExport['ScenarioCode'].iloc[index] + '.json'
        #display(filename)

        #df_Peak_VC_MaxDirFG_wVCGroups = df_Peak_VC_MaxDirFG_wVCGroups.rename(columns={"SEGID": 'S'})

        #export to csv in data-processed
        df_VC_MaxDirFG_wVCGroups.to_json(os.path.join(dirResults, filename),orient='records')

        display('Done exporting ' + filename)

'Done exporting WebAppData\\VC_Base15.json'

'Done exporting WebAppData\\VC_S550.json'

# Temp

In [215]:
dfs_VC_MaxDirFG_wVCGroups =[]
df_TDMsf = []

display ('Scenario Codes:')

for (idx, row) in df_Scenarios.iterrows():    

    print(row.loc['ScenarioCode'])
    
    df_TDM = dfs_TDM[idx]
    df_TDMsf = df_TDM[['SEGID','FT']]
    
    df_TDMsfmax = df_TDMsf.groupby('SEGID', as_index=False).agg({'FT':[np.max]})
    df_TDMsfmax.columns = ['SEGID','FT']
    #df_TDMsf.append(df_TDMsf)
    
    df_VC_MaxDirFG_wVCGroups = pd.read_csv(os.path.join(dirResults, '3_VC_MaxDirFG_wVCGroups_' + row.loc['ScenarioCode'] + '.csv'))
    display(df_VC_MaxDirFG_wVCGroups)
    
    df_new = pd.DataFrame.merge(df_TDMsfmax,df_VC_MaxDirFG_wVCGroups,on=('SEGID'))
    display(df_new)
    
    filename = os.path.join(dirResults,r"temp\3_VC_MaxDirFG_wVCGroups_" + row.loc['ScenarioCode'] + '.csv')
    display('Exporting ' + filename)
    df_new.to_csv(filename,index=False)
    #dfs_VC_MaxDirFG_wVCGroups.append(dfs_Peak_VC_MaxDirFG_wVCGroups)


'Scenario Codes:'

Base15


SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  AnnWkMD15  \
0     0006_146.9       0.09       0.09       0.09       0.05       0.05   
1     0006_149.9       0.18       0.17       0.16       0.10       0.09   
2     0006_150.6       0.18       0.17       0.16       0.10       0.09   
3     0006_152.6       0.17       0.16       0.16       0.12       0.09   
4     0006_152.9       0.21       0.20       0.18       0.17       0.10   
...          ...        ...        ...        ...        ...        ...   
3577   WFRC_8208       0.00       0.00       0.00       0.00       0.00   
3578   WFRC_8209       0.00       0.00       0.00       0.00       0.00   
3579   WFRC_8213       0.00       0.00       0.00       0.00       0.00   
3580   WFRC_8215       0.00       0.00       0.00       0.00       0.00   
3581   WFRC_8218       0.00       0.00       0.00       0.00       0.00   

      AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  AprWkMD15  \
0          0.07       0.11       0.09       0.10       0.06       0.05   
1          0.13       0.17       0.16       0.16       0.10       0.09   
2          0.13       0.17       0.16       0.15       0.10       0.09   
3          0.14       0.19       0.17       0.17       0.13       0.09   
4          0.18       0.20       0.19       0.18       0.16       0.10   
...         ...        ...        ...        ...        ...        ...   
3577       0.00       0.00       0.00       0.00       0.00       0.00   
3578       0.00       0.00       0.00       0.00       0.00       0.00   
3579       0.00       0.00       0.00       0.00       0.00       0.00   
3580       0.00       0.00       0.00       0.00       0.00       0.00   
3581       0.00       0.00       0.00       0.00       0.00       0.00   

      AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  AugWkMD15  \
0          0.07       0.10       0.10       0.09       0.06       0.05   
1          0.13       0.20       0.19       0.18       0.11       0.11   
2          0.13       0.20       0.19       0.18       0.12       0.10   
3          0.15       0.17       0.17       0.17       0.13       0.09   
4          0.18       0.23       0.22       0.21       0.19       0.12   
...         ...        ...        ...        ...        ...        ...   
3577       0.00       0.00       0.00       0.00       0.00       0.00   
3578       0.00       0.00       0.00       0.00       0.00       0.00   
3579       0.00       0.00       0.00       0.00       0.00       0.00   
3580       0.00       0.00       0.00       0.00       0.00       0.00   
3581       0.00       0.00       0.00       0.00       0.00       0.00   

      AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  DecWkMD15  \
0          0.08       0.08       0.08       0.08       0.05       0.04   
1          0.15       0.16       0.15       0.14       0.09       0.08   
2          0.15       0.16       0.15       0.14       0.09       0.08   
3          0.16       0.15       0.15       0.14       0.11       0.08   
4          0.21       0.19       0.18       0.17       0.15       0.09   
...         ...        ...        ...        ...        ...        ...   
3577       0.00       0.00       0.00       0.00       0.00       0.00   
3578       0.00       0.00       0.00       0.00       0.00       0.00   
3579       0.00       0.00       0.00       0.00       0.00       0.00   
3580       0.00       0.00       0.00       0.00       0.00       0.00   
3581       0.00       0.00       0.00       0.00       0.00       0.00   

      DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  FalWkMD15  \
0          0.06       0.10       0.09       0.09       0.06       0.05   
1          0.11       0.18       0.17       0.16       0.10       0.09   
2          0.12       0.18       0.17       0.16       0.10       0.09   
3          0.13       0.18       0.17       0.17       0.13       0.09   
4          0.16       0.21       0.20       0.19       0.17       0.10   

SEGID    FT  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  AnnWkMD15  \
0     0006_146.9   2.0       0.09       0.09       0.09       0.05       0.05   
1     0006_149.9   2.0       0.18       0.17       0.16       0.10       0.09   
2     0006_150.6   2.0       0.18       0.17       0.16       0.10       0.09   
3     0006_152.6   3.0       0.17       0.16       0.16       0.12       0.09   
4     0006_152.9   2.0       0.21       0.20       0.18       0.17       0.10   
...          ...   ...        ...        ...        ...        ...        ...   
3577   WFRC_8208   5.0       0.00       0.00       0.00       0.00       0.00   
3578   WFRC_8209   4.0       0.00       0.00       0.00       0.00       0.00   
3579   WFRC_8213   5.0       0.00       0.00       0.00       0.00       0.00   
3580   WFRC_8215   4.0       0.00       0.00       0.00       0.00       0.00   
3581   WFRC_8218  31.0       0.00       0.00       0.00       0.00       0.00   

      AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  AprWkMD15  \
0          0.07       0.11       0.09       0.10       0.06       0.05   
1          0.13       0.17       0.16       0.16       0.10       0.09   
2          0.13       0.17       0.16       0.15       0.10       0.09   
3          0.14       0.19       0.17       0.17       0.13       0.09   
4          0.18       0.20       0.19       0.18       0.16       0.10   
...         ...        ...        ...        ...        ...        ...   
3577       0.00       0.00       0.00       0.00       0.00       0.00   
3578       0.00       0.00       0.00       0.00       0.00       0.00   
3579       0.00       0.00       0.00       0.00       0.00       0.00   
3580       0.00       0.00       0.00       0.00       0.00       0.00   
3581       0.00       0.00       0.00       0.00       0.00       0.00   

      AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  AugWkMD15  \
0          0.07       0.10       0.10       0.09       0.06       0.05   
1          0.13       0.20       0.19       0.18       0.11       0.11   
2          0.13       0.20       0.19       0.18       0.12       0.10   
3          0.15       0.17       0.17       0.17       0.13       0.09   
4          0.18       0.23       0.22       0.21       0.19       0.12   
...         ...        ...        ...        ...        ...        ...   
3577       0.00       0.00       0.00       0.00       0.00       0.00   
3578       0.00       0.00       0.00       0.00       0.00       0.00   
3579       0.00       0.00       0.00       0.00       0.00       0.00   
3580       0.00       0.00       0.00       0.00       0.00       0.00   
3581       0.00       0.00       0.00       0.00       0.00       0.00   

      AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  DecWkMD15  \
0          0.08       0.08       0.08       0.08       0.05       0.04   
1          0.15       0.16       0.15       0.14       0.09       0.08   
2          0.15       0.16       0.15       0.14       0.09       0.08   
3          0.16       0.15       0.15       0.14       0.11       0.08   
4          0.21       0.19       0.18       0.17       0.15       0.09   
...         ...        ...        ...        ...        ...        ...   
3577       0.00       0.00       0.00       0.00       0.00       0.00   
3578       0.00       0.00       0.00       0.00       0.00       0.00   
3579       0.00       0.00       0.00       0.00       0.00       0.00   
3580       0.00       0.00       0.00       0.00       0.00       0.00   
3581       0.00       0.00       0.00       0.00       0.00       0.00   

      DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  FalWkMD15  \
0          0.06       0.10       0.09       0.09       0.06       0.05   
1          0.11       0.18       0.17       0.16       0.10       0.09   
2          0.12       0.18       0.17       0.16       0.10       0.09   
3          0.13       0.18       0.17       0.17       0.13       0.09   
4

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\temp\\3_VC_MaxDirFG_wVCGroups_Base15.csv'

...

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\temp\\3_VC_MaxDirFG_wVCGroups_UF50.csv'

S550


SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  AnnWkMD15  \
0     0006_146.9       0.14       0.14       0.13       0.09       0.07   
1     0006_149.9       0.30       0.29       0.27       0.19       0.15   
2     0006_150.6       0.30       0.29       0.27       0.18       0.15   
3     0006_152.6       0.33       0.31       0.29       0.19       0.17   
4     0006_152.9       0.46       0.30       0.24       0.36       0.29   
...          ...        ...        ...        ...        ...        ...   
3883   WFRC_8215       0.56       0.37       0.29       0.44       0.34   
3884   WFRC_8216       0.49       0.17       0.13       0.45       0.24   
3885   WFRC_8217       1.64       1.08       0.91       1.03       0.99   
3886   WFRC_8218       1.63       0.98       0.82       1.17       1.03   
3887   WFRC_8219       1.02       0.84       0.73       0.63       0.50   

      AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  AprWkMD15  \
0          0.11       0.16       0.14       0.15       0.10       0.07   
1          0.24       0.29       0.27       0.26       0.19       0.15   
2          0.24       0.29       0.27       0.26       0.18       0.15   
3          0.24       0.31       0.29       0.28       0.19       0.16   
4          0.44       0.46       0.31       0.24       0.36       0.29   
...         ...        ...        ...        ...        ...        ...   
3883       0.56       0.56       0.37       0.29       0.44       0.34   
3884       0.60       0.49       0.17       0.14       0.45       0.24   
3885       1.29       1.65       1.10       0.92       1.05       1.00   
3886       1.30       1.65       1.00       0.84       1.20       1.04   
3887       1.03       1.04       0.84       0.75       0.64       0.51   

      AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  AugWkMD15  \
0          0.12       0.15       0.15       0.14       0.10       0.08   
1          0.24       0.34       0.32       0.30       0.22       0.17   
2          0.23       0.34       0.32       0.30       0.21       0.18   
3          0.23       0.37       0.34       0.32       0.22       0.19   
4          0.44       0.47       0.30       0.24       0.36       0.29   
...         ...        ...        ...        ...        ...        ...   
3883       0.56       0.56       0.36       0.28       0.44       0.35   
3884       0.61       0.52       0.16       0.13       0.47       0.25   
3885       1.30       1.67       1.06       0.89       1.05       1.02   
3886       1.33       1.65       0.96       0.80       1.18       1.03   
3887       1.04       1.07       0.86       0.75       0.66       0.53   

      AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  DecWkMD15  \
0          0.12       0.13       0.13       0.12       0.08       0.06   
1          0.28       0.27       0.26       0.24       0.17       0.13   
2          0.27       0.27       0.26       0.24       0.16       0.13   
3          0.27       0.29       0.28       0.26       0.17       0.15   
4          0.46       0.45       0.30       0.24       0.34       0.28   
...         ...        ...        ...        ...        ...        ...   
3883       0.58       0.54       0.36       0.28       0.42       0.33   
3884       0.63       0.45       0.17       0.13       0.42       0.23   
3885       1.35       1.59       1.07       0.90       1.00       0.99   
3886       1.32       1.58       1.00       0.83       1.15       1.03   
3887       1.09       0.95       0.81       0.70       0.59       0.47   

      DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  FalWkMD15  \
0          0.10       0.15       0.14       0.14       0.10       0.07   
1          0.21       0.31       0.29       0.27       0.19       0.15   
2          0.21       0.31       0.29       0.27       0.18       0.15   
3          0.21       0.33       0.31       0.29       0.19       0.17   
4          0.42       0.47       0.32       0.24       0.37       0.29   

SEGID    FT  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  AnnWkMD15  \
0     0006_146.9   2.0       0.14       0.14       0.13       0.09       0.07   
1     0006_149.9   2.0       0.30       0.29       0.27       0.19       0.15   
2     0006_150.6   2.0       0.30       0.29       0.27       0.18       0.15   
3     0006_152.6   3.0       0.33       0.31       0.29       0.19       0.17   
4     0006_152.9   2.0       0.46       0.30       0.24       0.36       0.29   
...          ...   ...        ...        ...        ...        ...        ...   
3883   WFRC_8215   4.0       0.56       0.37       0.29       0.44       0.34   
3884   WFRC_8216  33.0       0.49       0.17       0.13       0.45       0.24   
3885   WFRC_8217   4.0       1.64       1.08       0.91       1.03       0.99   
3886   WFRC_8218  31.0       1.63       0.98       0.82       1.17       1.03   
3887   WFRC_8219   3.0       1.02       0.84       0.73       0.63       0.50   

      AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  AprWkMD15  \
0          0.11       0.16       0.14       0.15       0.10       0.07   
1          0.24       0.29       0.27       0.26       0.19       0.15   
2          0.24       0.29       0.27       0.26       0.18       0.15   
3          0.24       0.31       0.29       0.28       0.19       0.16   
4          0.44       0.46       0.31       0.24       0.36       0.29   
...         ...        ...        ...        ...        ...        ...   
3883       0.56       0.56       0.37       0.29       0.44       0.34   
3884       0.60       0.49       0.17       0.14       0.45       0.24   
3885       1.29       1.65       1.10       0.92       1.05       1.00   
3886       1.30       1.65       1.00       0.84       1.20       1.04   
3887       1.03       1.04       0.84       0.75       0.64       0.51   

      AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  AugWkMD15  \
0          0.12       0.15       0.15       0.14       0.10       0.08   
1          0.24       0.34       0.32       0.30       0.22       0.17   
2          0.23       0.34       0.32       0.30       0.21       0.18   
3          0.23       0.37       0.34       0.32       0.22       0.19   
4          0.44       0.47       0.30       0.24       0.36       0.29   
...         ...        ...        ...        ...        ...        ...   
3883       0.56       0.56       0.36       0.28       0.44       0.35   
3884       0.61       0.52       0.16       0.13       0.47       0.25   
3885       1.30       1.67       1.06       0.89       1.05       1.02   
3886       1.33       1.65       0.96       0.80       1.18       1.03   
3887       1.04       1.07       0.86       0.75       0.66       0.53   

      AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  DecWkMD15  \
0          0.12       0.13       0.13       0.12       0.08       0.06   
1          0.28       0.27       0.26       0.24       0.17       0.13   
2          0.27       0.27       0.26       0.24       0.16       0.13   
3          0.27       0.29       0.28       0.26       0.17       0.15   
4          0.46       0.45       0.30       0.24       0.34       0.28   
...         ...        ...        ...        ...        ...        ...   
3883       0.58       0.54       0.36       0.28       0.42       0.33   
3884       0.63       0.45       0.17       0.13       0.42       0.23   
3885       1.35       1.59       1.07       0.90       1.00       0.99   
3886       1.32       1.58       1.00       0.83       1.15       1.03   
3887       1.09       0.95       0.81       0.70       0.59       0.47   

      DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  FalWkMD15  \
0          0.10       0.15       0.14       0.14       0.10       0.07   
1          0.21       0.31       0.29       0.27       0.19       0.15   
2          0.21       0.31       0.29       0.27       0.18       0.15   
3          0.21       0.33       0.31       0.29       0.19       0.17   
4

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\temp\\3_VC_MaxDirFG_wVCGroups_S550.csv'

In [216]:
df_TDMsfmax = df_TDMsf.groupby('SEGID', as_index=False).agg({'FT':[np.max]})
df_TDMsfmax.columns = ['SEGID','FT']
df_TDMsfmax

SEGID    FT
0     0006_146.9   2.0
1     0006_149.9   2.0
2     0006_150.6   2.0
3     0006_152.6   3.0
4     0006_152.9   2.0
...          ...   ...
3922   WFRC_8215   4.0
3923   WFRC_8216  33.0
3924   WFRC_8217   4.0
3925   WFRC_8218  31.0
3926   WFRC_8219   3.0

[3927 rows x 2 columns]

In [217]:
df_VCGroup_Seasons

SeasonCode SeasonGroup SeasonName SeasonType
0         Ann     S00-Ann     Annual     Season
1         Win     S01-Win     Winter     Season
2         Spr     S02-Spr     Spring     Season
3         Sum     S03-Sum     Summer     Season
4         Fal     S04-Fal       Fall     Season
5         Jan     M01-Jan    January      Month
6         Feb     M02-Feb   February      Month
7         Mar     M03-Mar      March      Month
8         Apr     M04-Apr      April      Month
9         May     M05-May        May      Month
10        Jun     M06-Jun       June      Month
11        Jul     M07-Jul       July      Month
12        Aug     M08-Aug     August      Month
13        Sep     M09-Sep  September      Month
14        Oct     M10-Oct    October      Month
15        Nov     M11-Nov   November      Month
16        Dec     M12-Dec   December      Month

In [218]:
df_TDMsfmax

SEGID    FT
0     0006_146.9   2.0
1     0006_149.9   2.0
2     0006_150.6   2.0
3     0006_152.6   3.0
4     0006_152.9   2.0
...          ...   ...
3922   WFRC_8215   4.0
3923   WFRC_8216  33.0
3924   WFRC_8217   4.0
3925   WFRC_8218  31.0
3926   WFRC_8219   3.0

[3927 rows x 2 columns]